# Visualização Orçamento SME

In [549]:
import pandas as pd
import requests
import json
import numpy as np
import matplotlib.pyplot as plt
import matplotlib
import glob
import datetime
from IPython.display import HTML
import pprint

pd.set_option('display.max_colwidth', 100)

In [550]:
%%javascript
IPython.OutputArea.auto_scroll_threshold = 50;

<IPython.core.display.Javascript object>

In [551]:
TOKEN = '198f959a5f39a1c441c7c863423264'
base_url = "https://gatewayapi.prodam.sp.gov.br:443/financas/orcamento/sof/v2.1.0"
headers = {'Authorization' : str('Bearer ' + TOKEN)}

# Carregando do arquivo

# Contratos

### Último ano

In [552]:
# json_files = glob.glob("wget-contratos/2017/*")

# frames = []

# for f in json_files:
#     e = json.load(open(f))
#     e_df = pd.DataFrame(e['lstContratos'])
#     frames.append(e_df)

# contratos_df = pd.concat(frames)

In [553]:
contratos_df = pd.read_json('dados/contratos-2017.json')

In [554]:
HTML(contratos_df.iloc[0:1].to_html())

# Empenhos

### Último ano

In [555]:
# json_files = glob.glob("wget-empenhos/2017/*")

# frames = []

# for f in json_files:
#     e = json.load(open(f))
#     e_df = pd.DataFrame(e['lstEmpenhos'])
#     frames.append(e_df)

# empenhos_df = pd.concat(frames)

In [556]:
empenhos_df = pd.read_json('dados/empenhos-2017.json')

### Todos anos

In [557]:
# json_files = glob.glob("wget-empenhos/*/*")

# frames = []

# for f in json_files:
#     e = json.load(open(f))
#     e_df = pd.DataFrame(e['lstEmpenhos'])
#     frames.append(e_df)

# empenhos_df_tot = pd.concat(frames)

## Baixar contratos e empenhos

In [558]:
# ver arquivo contratos_scraper.py
# e arquivo contratos_merge.py

## Arquivos já baixados

In [559]:
empenhos_contratos_df = pd.read_json('dados/empenhos-contratos-2017.json')

Quais colunas estão no empenhos_contratos e não no empenhos?

In [560]:
(empenhos_contratos_df.columns.values[
    np.invert(
        np.in1d(empenhos_contratos_df.columns.values, empenhos_df.columns.values)
        )
    ]
)

array(['codContrato'], dtype=object)

Exemplo de um contrato:

In [561]:
HTML(
    (contratos_df[contratos_df['codContrato'] == 25327])
.to_html())

Exemplo de um contrato e seu empenho relacionado:

In [562]:
HTML(
    (empenhos_contratos_df[empenhos_contratos_df['codContrato'] == 25327])
.to_html())

In [563]:
HTML(
    (empenhos_df[empenhos_df['codEmpenho'] == 120981])
.to_html())

Número de empenhos sem contratos relacionados:

In [564]:
len(empenhos_df) - len(empenhos_contratos_df)

41924

## Join contratos e empenhos

Quais colunas estão no contratos e não no empenhos_contratos?

In [565]:
list(contratos_df.columns.values[
    np.invert(
        np.in1d(contratos_df.columns.values, empenhos_contratos_df.columns.values)
        )
    ]
)

['anoExercicio',
 'codTipoContratacao',
 'datAssinaturaContrato',
 'datPublicacaoContrato',
 'datVigencia',
 'numOriginalContrato',
 'txtDescricaoModalidade',
 'txtObjetoContrato',
 'txtTipoContratacao',
 'valAditamentos',
 'valAnulacao',
 'valPago',
 'valPrincipal',
 'valReajustes']

In [566]:
# merge
delta = list(contratos_df.columns.values[
    np.invert(
        np.in1d(contratos_df.columns.values, empenhos_contratos_df.columns.values)
        )
    ]
)
delta.append('codContrato')
contratos_df_delta = contratos_df[delta]
temp = pd.merge(empenhos_contratos_df[['codEmpenho', 'codContrato']], contratos_df_delta, how='inner', 
         on='codContrato')
empenhos_df = pd.merge(empenhos_df, temp, how='left', 
         on='codEmpenho')

In [567]:
empenhos_df.columns.values

array(['anoEmpenho', 'codCategoria', 'codElemento', 'codEmpenho',
       'codEmpresa', 'codFonteRecurso', 'codFuncao', 'codGrupo',
       'codItemDespesa', 'codModalidade', 'codOrgao', 'codProcesso',
       'codPrograma', 'codProjetoAtividade', 'codSubElemento',
       'codSubFuncao', 'codUnidade', 'datEmpenho', 'mesEmpenho',
       'nomEmpresa', 'numCpfCnpj', 'numReserva', 'txtCategoriaEconomica',
       'txtDescricaoElemento', 'txtDescricaoFonteRecurso',
       'txtDescricaoFuncao', 'txtDescricaoItemDespesa',
       'txtDescricaoOrgao', 'txtDescricaoPrograma',
       'txtDescricaoProjetoAtividade', 'txtDescricaoSubElemento',
       'txtDescricaoSubFuncao', 'txtDescricaoUnidade', 'txtGrupoDespesa',
       'txtModalidadeAplicacao', 'txtRazaoSocial', 'valAnuladoEmpenho',
       'valEmpenhadoLiquido', 'valLiquidado', 'valPagoExercicio',
       'valPagoRestos', 'valTotalEmpenhado', 'codContrato',
       'anoExercicio', 'codTipoContratacao', 'datAssinaturaContrato',
       'datPublicacaoCo

## Criar coluna valPagoTotal como pago + restos

In [568]:
empenhos_df['valPagoTotal'] = empenhos_df['valPagoExercicio'] + empenhos_df['valPagoRestos']

##  Índice para corrigir inflação

In [569]:
inflacao_df = pd.DataFrame(columns=["ano", "indice"], 
  data=[
    [2006, 1.8974051],
    [2007, 1.7862712],
    [2008, 1.5965463],
    [2009, 1.6222454],
    [2010, 1.4711348],
    [2011, 1.3885172],
    [2012, 1.2982224],
    [2013, 1.229265],
    [2014, 1.1859287],
    [2015, 1.0714226],
    [2016, 1.0000453],
    [2017, 1]
  ])

## Helper para explorar grupos

In [570]:
empenhos_df.columns.values

array(['anoEmpenho', 'codCategoria', 'codElemento', 'codEmpenho',
       'codEmpresa', 'codFonteRecurso', 'codFuncao', 'codGrupo',
       'codItemDespesa', 'codModalidade', 'codOrgao', 'codProcesso',
       'codPrograma', 'codProjetoAtividade', 'codSubElemento',
       'codSubFuncao', 'codUnidade', 'datEmpenho', 'mesEmpenho',
       'nomEmpresa', 'numCpfCnpj', 'numReserva', 'txtCategoriaEconomica',
       'txtDescricaoElemento', 'txtDescricaoFonteRecurso',
       'txtDescricaoFuncao', 'txtDescricaoItemDespesa',
       'txtDescricaoOrgao', 'txtDescricaoPrograma',
       'txtDescricaoProjetoAtividade', 'txtDescricaoSubElemento',
       'txtDescricaoSubFuncao', 'txtDescricaoUnidade', 'txtGrupoDespesa',
       'txtModalidadeAplicacao', 'txtRazaoSocial', 'valAnuladoEmpenho',
       'valEmpenhadoLiquido', 'valLiquidado', 'valPagoExercicio',
       'valPagoRestos', 'valTotalEmpenhado', 'codContrato',
       'anoExercicio', 'codTipoContratacao', 'datAssinaturaContrato',
       'datPublicacaoCo

In [575]:
def groupSum(df):
    terms = [
        'txtDescricaoOrgao',
        'txtCategoriaEconomica',
        'txtDescricaoElemento',
        'txtDescricaoFonteRecurso',
        # 'txtDescricaoFuncao',
        'txtDescricaoItemDespesa',
        'txtDescricaoPrograma',
        'txtDescricaoProjetoAtividade',
        'txtDescricaoSubElemento',
        'txtDescricaoSubFuncao',
        'txtDescricaoUnidade',
        'txtGrupoDespesa',
        'txtModalidadeAplicacao',
        'txtRazaoSocial'
    ]
    for el in terms:
        result = (df
         .groupby(el)['valTotalEmpenhado', 'valLiquidado', 'valPagoTotal']
#         .groupby(el)[
#             'valAnuladoEmpenho',
#             'valEmpenhadoLiquido',
#             'valLiquidado',
#             'valPagoExercicio',
#             'valPagoRestos',
#             'valTotalEmpenhado',
#             'valAditamentos',
#             'valAnulacao',
#             'valPago',
#             'valPrincipal',
#             'valReajustes'
#         ]
         .sum().apply(lambda x: x / 1000000).sort_values('valPagoTotal', ascending=False)
        )
        display(result)
    display(
    # HTML(
    df[['txtObjetoContrato']].drop_duplicates(subset='txtObjetoContrato')
        # .to_html())
    )

### Helper para contratos

In [576]:
def groupSumContratos(df):
    terms = ['anoExercicio',
        'txtDescricaoModalidade',
        'txtDescricaoOrgao',
        'txtObjetoContrato',
        'txtRazaoSocial',
        'txtTipoContratacao',
    ]
    for el in terms:
        result = (df
         .groupby(el)['valTotalEmpenhado', 'valLiquidado']
         .sum().apply(lambda x: x / 1000000).sort_values('valLiquidado', ascending=False)
        )
        display(result)

# Atenção!

Os valores estão em milhões de reais, a não ser que indicado o contrário.

## Explorando dados

### Agrupamentos

In [577]:
groupSum(empenhos_df)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação       12966.262672  10236.129116   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação   10600.75598

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes          12798.904536  10172.665375  10469.304631
Despesas de Capital           167.358136     63.463741    131.451350

valTotalEmpenhado  \
txtDescricaoElemento                                                                     
Vencimentos e Vantagens Fixas - Pessoal Civil                              7227.363117   
Outros Serviços de Terceiros - Pessoa Jurídica                             2370.502024   
Outros Serviços de Terceiros -Pessoa Jurídica                              1902.575828   
Auxílio-Alimentação                                                         434.820030   
Material, Bem ou Serviço para Distribuição Gratuita                         390.772614   
Material de Consumo                                                         273.308796   
Outros Serviços de Terceiros - Pessoa Física                                140.887005   
Obras e Instalações                                                          89.889729   
Equipamentos e Material Permanente                                           56.995277   
Contribuições                                                                23.877403   
Auxílio-Transporte                                                           17.829964   
Indenizações e Restituições                                                  14.682730   
Outros Auxílios Financeiros a Pessoas Físicas                                 7.890976   
Obrigações Tributárias e Contributivas                                        7.591351   
Locação de Mão-de-Obra                                                        5.120272   
Aquisição de Imóveis                                                          0.762059   
Despesas de Exercícios Anteriores                                             0.725765   
Ressarcimento de Despesas de Pessoal Requisitado                              0.332970   
Premiações Culturais, Artísticas, Científicas, Desportivas e Outras           0.107596   
Passagens e Despesas com Locomoção                                            0.215488   
Diárias - Civil                                                               0.011680   

                                                                     valLiquidado  \
txtDescricaoElemento                                                                
Vencimentos e Vantagens Fixas - Pessoal Civil                         5770.231471   
Outros Serviços de Terceiros - Pessoa Jurídica                        2073.220587   
Outros Serviços de Terceiros -Pessoa Jurídica                         1367.463481   
Auxílio-Alimentação                                                    430.542262   
Material, Bem ou Serviço para Distribuição Gratuita                    162.051071   
Material de Consumo                                                    202.342032   
Outros Serviços de Terceiros - Pessoa Física                           117.782310   
Obras e Instalações                                                     39.131728   
Equipamentos e Material Permanente                                       5.020445   
Contribuições                                                           19.871110   
Auxílio-Transporte                                                      17.829964   
Indenizações e Restituições                                             14.682730   
Outros Auxílios Financeiros a Pessoas Físicas                            5.651375   
Obrigações Tributárias e Contributivas                                   5.109918   
Locação de Mão-de-Obra                                                   3.601912   
Aquisição de Imóveis                                                     0.762059   
Despesas de Exercícios Anteriores                                        0.705088   
Ressarcimento de Despesas de Pessoal Requisitado                         0.015898   
Premiações Culturais, Artísticas, Científicas, Desportivas e Outras      0.090112   
Passagens e Despesas com Locomoção                                       0.015372   
Diárias - Civil                                                          0.008193   

                                          

valTotalEmpenhado  valLiquidado  \
txtDescricaoFonteRecurso                                            
Tesouro Municipal                       7533.654836   5788.261271   
Fundo Constitucional da Educação        4440.279767   3827.119838   
Transferências Federais                  938.337874    587.762549   
Outras Fontes                             33.979873     16.566437   
Transferências Estaduais                  20.010323     16.419021   

                                  valPagoTotal  
txtDescricaoFonteRecurso                        
Tesouro Municipal                  6091.881723  
Fundo Constitucional da Educação   3827.119838  
Transferências Federais             641.024033  
Outras Fontes                        24.311365  
Transferências Estaduais             16.419021

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                                     
RPPS - PMSP                                                                   7224.500741   
Convênio - Creche                                                             2230.700574   
Limpeza de Ambientes                                                           460.588315   
Refeições Prontas                                                              593.334812   
Auxílio-Refeição - RPPS                                                        231.914947   
Transporte Escolar - EMEF                                                      226.955018   
Uniforme Escolar                                                               299.956901   
Vale-Alimentação - RPPS                                                        201.652925   
Guarda, Vigilância e Segurança em Geral                                        214.285475   
Diversos Gêneros Alimentícios                                                  159.092806   
Água e Esgoto                                                                  126.312290   
Escolas e Similares                                                             89.889729   
Energia Elétrica de Prédios Públicos                                            63.686421   
Material Escolar                                                                47.743602   
Leite e Achocolatados                                                           42.994545   
Convênios - Alfabetização, Educação e Outros                                    46.247443   
Outros Aparelhos e Equipamentos de Comunicação                                  40.036436   
Programa Transferência Recursos Financeiros - Assoc de Pais e Mestres           38.034370   
Preparo e Distribuição de Alimentos                                             33.383049   
Concessão de Bolsa-Auxílio para Estagiários                                     34.734801   
Carnes em Geral                                                                 30.159054   
Armazenagem de Alimentos                                                        37.534199   
Outras Instituições de Caráter Assistencial, Cultural ou Educacional            23.877403   
Pães, Doces, Biscoitos e Salgados                                               20.781584   
Locação de Imóveis                                                              22.911279   
Auxílio-Transporte - RPPS                                                       17.757254   
Laticínios em Geral                                                             15.931271   
Supervisão, Acompanhamento e Suporte de Serviços Técnicos                       17.282564   
Restituições a Pessoas Jurídicas                                                14.682730   
Serviço de Instalação, Ampliação de Sist. de Telefonia/Teleinformática          15.433389   
...                                                                                   ...   
Outros Equipamentos para Proteção, Segurança e Socorro                           0.003830   
Não Padronizados                                                                 0.003755   
Adiantamento - Inciso VI, Art. 2º da Lei nº 10.513/88                            0.003568   
Certificado Digital                                                              0.003080   
Diversas Ferramentas                                                             0.003018   
Transporte Escolar - EMEE                                                        0.002972   
Toner e Cartuchos de Tinta                                                       0.002790   
Assinatura de Jornais                                                            0.002176   
Adiantamento - Inciso VII, Art. 2º da Lei nº 10.513/88                           0.002100   
Utensíllios de Escritório                                                        0.002096   
Encadernação                                                             

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Gabinete do Secretário                                        9375.871273   
Departamento de Alimentação Escolar                            864.352108   
Diretoria Regional de Educação - Campo Limpo                   259.667430   
Diretoria Regional de Educação - Guaianases                    296.241506   
Diretoria Regional de Educação - São Miguel                    222.969903   
Diretoria Regional de Educação - Pirituba                      202.860499   
Diretoria Regional de Educação - Ipiranga                      188.018721   
Diretoria Regional de Educação - Freguesia/Brasilândia         212.657771   
Diretoria Regional de Educação - Itaquera                      207.890332   
Diretoria Regional de Educação - Penha                         174.380797   
Diretoria Regional de Educação - São Mateus                    178.445242   
Coordenadoria de Alimentação Escolar                           164.918054   
Diretoria Regional de Educação - Santo Amaro                   145.165673   
Diretoria Regional de Educação - Jaçanã/Tremembé               136.623102   
Diretoria Regional de Educação  Capela do Socorro              110.392806   
Diretoria Regional de Educação - Capela do Socorro             117.796633   
Diretoria Regional de Educação - Butantã                       108.010822   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Gabinete do Secretário                                   7365.919168   
Departamento de Alimentação Escolar                       555.403268   
Diretoria Regional de Educação - Campo Limpo              236.657658   
Diretoria Regional de Educação - Guaianases               214.297709   
Diretoria Regional de Educação - São Miguel               210.591931   
Diretoria Regional de Educação - Pirituba                 191.569627   
Diretoria Regional de Educação - Ipiranga                 176.640245   
Diretoria Regional de Educação - Freguesia/Brasilândia    175.734458   
Diretoria Regional de Educação - Itaquera                 172.945943   
Diretoria Regional de Educação - Penha                    163.037585   
Diretoria Regional de Educação - São Mateus               140.532773   
Coordenadoria de Alimentação Escolar                       93.102006   
Diretoria Regional de Educação - Santo Amaro              132.690529   
Diretoria Regional de Educação - Jaçanã/Tremembé          124.153965   
Diretoria Regional de Educação  Capela do Socorro          94.119925   
Diretoria Regional de Educação - Capela do Socorro         96.161940   
Diretoria Regional de Educação - Butantã                   92.570389   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Gabinete do Secretário                                   7638.083844  
Departamento de Alimentação Escolar                       571.057087  
Diretoria Regional de Educação - Campo Limpo              242.167856  
Diretoria Regional de Educação - Guaianases               215.727938  
Diretoria Regional de Educação - São Miguel               213.711664  
Diretoria Regional de Educação - Pirituba                 194.308053  
Diretoria Regional de Educação - Ipiranga                 178.577069  
Diretoria Regional de Educação - Freguesia/Brasilândia    176.804683  
Diretoria Regional de Educação - Itaquera                 175.474689  
Diretoria Regional de Educação - Penha                    164.093725  
Diretoria Regional de Educação - São Mateus               143.629764  
Coordenadoria de Alimentação Escolar                      139.099766  
Diretoria Regional de Educação - Santo Amaro              135.378423  
Diretoria Regional de Educação - Jaçanã/Tremembé          126.023384  
Diretoria Regional de Educação  Capela do Socorro          96.621876  
Diretoria Region

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                          
Pessoal e Encargos Sociais        7227.696087   5770.247369   5770.554997
Outras Despesas Correntes         5571.208449   4402.418006   4698.749634
Investimentos                      167.358136     63.463741    131.451350

valTotalEmpenhado  \
txtModalidadeAplicacao                                                                     
Aplicações Diretas                                                          10564.154302   
Transferências a Instituições Privadas sem Fins Lucrativos                   2401.965902   
Apl.Dir.Dec.Op. entre Órgãos,Fundos e Ent.Int.Orç.Fiscal e Seg.Social           0.142468   

                                                                       valLiquidado  \
txtModalidadeAplicacao                                                                
Aplicações Diretas                                                      8136.470299   
Transferências a Instituições Privadas sem Fins Lucrativos              2099.546763   
Apl.Dir.Dec.Op. entre Órgãos,Fundos e Ent.Int.Orç.Fiscal e Seg.Social      0.112054   

                                                                       valPagoTotal  
txtModalidadeAplicacao                                                               
Aplicações Diretas                                                      8488.544194  
Transferências a Instituições Privadas sem Fins Lucrativos              2112.088527  
Apl.Dir.Dec.Op. entre Órgãos,Fundos e Ent.Int.Orç.Fiscal e Seg.Social      0.123259

valTotalEmpenhado  \
txtRazaoSocial                                                                                                 
FOLHA DE PAGAMENTO _ EXECUTIVO                                                                   7224.500741   
SERV.SEC.MUN. DE EDUCAÇÃO - AUX. REFEIÇÃO                                                         434.818454   
SHA COMERCIO DE ALIMENTOS LTDA                                                                    190.741737   
CIA DE SANEAMENTO BÁSICO DO ESTADO DE SÃO PAULO SABESP                                            126.612305   
COMERCIAL MILANO BRASIL LTDA                                                                       92.039220   
DENJUD REFEIÇÕES COLETIVAS ADMINISTRAÇÃO E SERVIÇOS LTDA                                          144.606175   
APETECE SISTEMAS DE ALIMENTACAO S/A                                                               161.392758   
EBN COMERCIO IMPORTACAO E EXPORTACAO S/A                                                          107.089565   
BRINK MOBIL EQUIPAMENTOS EDUCACIONAIS LTDA                                                         66.958155   
TANGARÁ IMP.E EXP.S/A                                                                              61.845260   
ELETROPAULO METROPOLITANA ELETRICIDADE DE SÃO PAULO S.A.                                           66.003813   
NILCATEX TEXTIL LTDA                                                                               94.554172   
LIMPADORA CALIFORNIA LTDA                                                                          56.310204   
BASE SISTEMA SERVIÇOS DE ADMINISTRAÇÃO E COMERCIO LTDA                                             65.781097   
ARCOLIMP SERVIÇOS GERAIS LTDA                                                                      42.813454   
POSITIVO TECNOLOGIA S.A.                                                                           40.910940   
CENTRO DE INTEGRAÇÃO EMPRESA ESCOLA CIEE                                                           43.214780   
SOCIEDADE BENEFICIENTE EQUILIBRIO DE INTERLAGOS                                                    42.737749   
G4S INTERATIVA SERVICE LTDA                                                                        36.618904   
P.R.M. SERVIÇOS E MAO DE OBRA ESPECIALIZADA EIRELI                                                 44.011233   
CRUZADA PRO INFANCIA                                                                               33.621266   
GUIMA CONSECO CONSTRUÇÃO, SERVIÇOS E COMÉRCIO LTDA                                                 31.047000   
DEMAX SERVICOS E COMERCIO LTDA                                                                     30.635239   
SPDM-ASSOCIAÇÃO PAULISTA PARA O DESENVOLVIMENTO DA MEDICINA                                        32.364774   
ALBATROZ SEGURANÇA E VIGILÂNCIA LTDA                                                               27.713410   
G4S VANGUARDA SEGURANCA E VIGILANCIA LTDA                                                          27.801421   
SERBOM ARMAZENS GERAIS FRIGORIFICOS LTDA                                                           37.534199   
A. TONANNI CONSTRUÇÕES E SERVIÇOS LTDA                                                             25.723431   
PLURI SEGURANÇA E VIGILANCIA LTDA                                                                  24.536613   
EPS - EMPRESA PAULISTA DE SERVICOS S.A.                                                            24.503134   
...                                                                                                      ...   
NUCLEO RECREATIVO MUNDO ENCANTADO                                                                   0.369962   
CELSO HENRIQUE SANTOS DE SOUSA                                                                      0.005640   
OBRAS SOCIAIS  DE VISTA  ALEGRE                                                                     0.021400   
ONG FORÇA E PERSERVERANÇA                                  

txtObjetoContrato
0                                                   Contratação de Agente Recreativo - Edição Janeiro 2017
1                                                               RECREIO NAS FÉRIAS JANEIRO / 2017 - DRE/IQ
2                                      2º REPASSE PTRF/2017 – DRE-G – CUSTEIO – APM – CEU EMEF LAJEADO  \t
3      Celebração do Termo de Convênio nº 013/DRE-PJ/2015-RP para atendimento de 178 crianças, sendo 84...
4                                                                                                      NaN
5                                                PRORROGAÇÃO DE VIGÊNCIA- CEI EUGêNIO FRANCISCO DE SANTANA
9                                Repasse de Recursos do PNAE para o CEI SANTA ANGELA- CÓD. INEP 35181560\n
12     \r\nCONTRATAÇÃO DE AGENTES DE RECREAÇÃO PARA O RECREIO NAS FÉRIAS JANEIRO DE 2017 NO PERÍODO DE ...
15                                                                   CEI PRIMEIRO LAPIS - JANEIRO A AGOSTO
20                                                    PRORROGAÇÃO DE VIGÊNCIA - CEI VIRTUDE DA CRIANÇA III
23                                                                          CEI ADALGIZA COELHO DOS SANTOS
24     Repasses de recursos à APM, de acordo com a Lei Federal 9394/1996 e Portarias da SME indicando o...
27                                                               CELEBRAÇÃO DE CONVÊNIO- CEI ABC AURORA II
28                                                 CELEBRAÇÃO DE CONVÊNIO- CEI JARDIM IPANEMA I - 29/05/17
31     Aquisição de 87.500 Kg de Composto Lácteo Sabor Chocolate - ATA de RP nº 008/SME/CODAE/2017 - FN...
32                                 Repasse de Recursos do PNAE para o CEI AVES GALHANI- CÓD. INEP 35305534
33                                                     TERMO DE COLABORAÇÃO- CEI VITÓRIA- EM CONTINUIDADE 
34                                                              TERMO DE COLABORAÇÃO - CEI FLOR DO ORIENTE
36                                  SERVIÇOS DE MANUTENÇÃO E INSTALAÇÃO DE CONDICIONADORES DE AR DRE/DIPED
37                                                               TERMO DE COLABORAÇÃO- CEI GALPÃO ATRIA II
38                                            CELEBRAÇÃO DE TERMO DE COLABORAÇÃO- CEI REINO DOS PEQUENINOS
39                                                                CELEBRAÇÃO DE PARCERIA- CEI TRINDADE III
42                                                     CELEBRAÇÃO DE PARCERIA- CEI ESPAÇO DA COMUNIDADE VI
43                                                               CELEBRAÇÃO DE PARCERIA- CEI MARAVILHA III
45                                 CONSUMO DE ENERGIA ELÉTRICA-EMEF,EMEI,CEI,EMEBS,EMEFM,CIEJA,DRESA E CEU
46                                  CELEBRAÇÃO TERMO DE COLABORAÇÃO/PARCERIA - CEI CIDADE A.E. CARVALHO II
50                 TERMO DE COLABORAÇÃO PARA A MANUTENÇÃO DO CEI PIRAJUCARA NOS TERMOS DA PORTARIA 4548/17
54                CONSUMO DE ÁGUA E SERVIÇO  DE ÁGUA E ESGOSTO-EMEF,EMEI.CEI,CIEJA,DRESA,EMEFM,CEU E EMEBS
55                                                                RECREIO NAS FÉRIAS JULHO / 2017 - DRE/IQ
59     Manutenção do CEI Vovó Joaninha, para atendimento de 70 crianças de 0 a 3 anos, sendo 25 de berç...
...                                                                                                    ...
59030                                                                                 CEI MONTE CARMELO II
59035                                                                      Locação de brinquedos infláveis
59037                                              CONTRATAÇÃO DE AGENTE DE RECREAÇÃO - RECREIO NAS FERIAS
59041                                                                              03 SLS DO CONVÊNIO MOVA
59054                                                                                CEI MONTE CARMELO III
59064                                                                            CEI CASA DA CRIANÇA FELIZ
59067                  

## Contratos

In [578]:
groupSumContratos(contratos_df)

Empty DataFrame
Columns: [valTotalEmpenhado, valLiquidado]
Index: []

valTotalEmpenhado  valLiquidado
txtDescricaoModalidade                                 
Pregão                         943.559736    641.162346
Não Aplicável                  610.937541    474.659843
Dispensa de Licitação          591.269262    427.488146
Inexigibilidade                 61.632085     52.071161
Leilão                           0.209999      0.209999
Tomada de Preços                 0.677581      0.143517
Concorrência                     0.115772      0.115772
Convite                          0.000000      0.000000

valTotalEmpenhado  valLiquidado
txtDescricaoOrgao                                                
Secretaria Municipal de Educação        2208.401976   1595.850786

valTotalEmpenhado  \
txtObjetoContrato                                                                                                         
Aquisição de Kit de Uniforme Escolar                                                                          61.576593   
Serviços de Nutrição e Alimentação Escolar - Regiões de GUAIANASES, ITAQUERA e PENHA \n\n                     50.274381   
Aquisição de notebook                                                                                         40.021740   
Serviços de Nutrição e Alimentação Escolar - Região da FREGUESIA DO Ó e SÃO MATEUS                            44.781926   
Aquisição de kits de uniforme escolar lotes 04 e 06                                                          117.814656   
Serviços de Nutrição e Alimentação Escolar - Regiões - IPIRANGA E SÃO MIGUEL                                  42.442385   
Limpeza de CEUs.                                                                                              34.210382   
Aquisição de Kit de Uniforme Escolar                                                                          29.558169   
 Aquisição de kits de uniforme escolar lote 02                                                                26.810556   
Serviços de vigilância CEUs - lotes 01, 02, 04 e 05                                                           36.855961   
Contratação de serviços de nutrição e alimentação escolar- Lote 4 - CAPELA DO SOCORRO.                        24.768282   
AQUISIÇÃO DE KITS DE UNIFORME ESCOLAR - LOTES 04 E 06                                                         22.973738   
Serviço de nutrição e alimentação escolar - Região Jãçanã-Tremembé - Contrataçãqo emergencial.                19.452618   
Serviços de vigilância CEUs - lotes 03, 06 e 07                                                               23.945679   
Contratação de serviços de nutrição e alimentação escolar - LOTE 5 - FREGUESIA DO Ó.                          19.201828   
A presente parceria destina-se ao atendimento ás crianças por meio de Centro de Educação Infantil...          28.055642   
\r\nContratação de serviços de nutrição e alimentação escolar – LOTE 6 - GUAIANAZES.\r\n                      18.236573   
AQUISIÇÃO DE KIT MATERIAL ESCOLAR                                                                             14.547467   
Contratação de serviços de nutrição e alimentação escolar – LOTE  8 - ITAQUERA                                15.807573   
Prestação de serviços e venda de produtos / Prestação de serviços de logística integrada: Entrega...          14.182434   
CONSUMO E TARIFAS DE TELEFONIA FIXA- APOIO AO ENSINO                                                          12.780961   
AQUISIÇÃO DE KIT UNIFORME ESCOLAR                                                                             14.462154   
Consumode água e esgoto da DRE Pirituba e das Unidades Educacionais a ela subordinadas.                       11.267142   
Contratação de serviços de nutrição e alimentação escolar – LOTE  14A - SÃO MATEUS I.                         11.959116   
\r\nContratação de serviços de nutrição e alimentação escolar – LOTE  10B - SÃO MIGUEL II.                    11.651172   
Contratação de serviços de nutrição e alimentação escolar – LOTE  10A - SÃO MIGUEL I.                         11.974066   
CONSUMO DE ÁGUA - SABESP - CEI, EMEI, EMEF, CIEJA, ADM E CEU.                                                 14.087107   
PAGTO. DE CONCESSIONÁRIA - SABESP                                                                             10.532222   
\r\nContratação de serviços de nutrição e alimentação escolar – LOTE  14B - SÃO MATEUS II.                    11.177524   
SP/SR CONTRATAÇÃO DE SERVIÇOS DE AGUA E ESGOSTO REFERENTE O EXERCÍCIO DE 2017 PARA A UNIDADES DRE...           9.666959   
...                                                                                                                 ...   
CELEBRAÇÃO DE TERMO DE COLABORAÇÃO EM CONTI

valTotalEmpenhado  valLiquidado
txtRazaoSocial                                                       
PREFEITURA DO MUNICÍPIO DE SÃO PAULO        2208.401976   1595.850786

valTotalEmpenhado  \
txtTipoContratacao                                                                       
Termo de Contrato - Serviços                                               1083.524679   
Nota de Empenho Fornecimento de Bens de Consumo e/ou Permanente             396.009759   
Termo de Colaboração - Lei Federal 13.019/2014                              360.355316   
Termo de Contrato para Aquisição de Bens de Consumo e/ou Permanente         176.563671   
Termo de Convênio                                                           103.758882   
Termo de Compromisso PTRF                                                    40.178396   
Termo de Repasse PNAE                                                        23.863291   
Acordo de Cooperação - Lei Federal 13.019/2014                               10.918979   
Termo de Fomento - Lei Federal 13.019/2014                                    8.469562   
Termo de Cooperação                                                           3.001471   
Nota de Empenho para Fornecimento de Serviços                                 1.065686   
Termo de Parceria - Lei Federal 9.790/1999                                    0.390861   
Contrato da Dívida - Principal                                                0.199267   
Ordem de Execução de Serviço                                                  0.051662   
Termo de Carta-Contrato                                                       0.022322   
Sem Ônus                                                                      0.020972   
Ordem de Compra                                                               0.007200   

                                                                     valLiquidado  
txtTipoContratacao                                                                 
Termo de Contrato - Serviços                                           734.338001  
Nota de Empenho Fornecimento de Bens de Consumo e/ou Permanente        280.776631  
Termo de Colaboração - Lei Federal 13.019/2014                         249.850884  
Termo de Contrato para Aquisição de Bens de Consumo e/ou Permanente    169.319828  
Termo de Convênio                                                       87.287964  
Termo de Compromisso PTRF                                               38.926438  
Termo de Repasse PNAE                                                   19.722606  
Acordo de Cooperação - Lei Federal 13.019/2014                           7.054200  
Termo de Fomento - Lei Federal 13.019/2014                               5.503498  
Termo de Cooperação                                                      1.533608  
Nota de Empenho para Fornecimento de Serviços                            0.849191  
Termo de Parceria - Lei Federal 9.790/1999                               0.387143  
Contrato da Dívida - Principal                                           0.199237  
Ordem de Execução de Serviço                                             0.051662  
Termo de Carta-Contrato                                                  0.022322  
Sem Ônus                                                                 0.020972  
Ordem de Compra                                                          0.006600

In [579]:
HTML(
    (contratos_df[['codContrato', 'txtObjetoContrato', 'valLiquidado']])
    .sort_values('valLiquidado', ascending=False)
.to_html())

In [580]:
cod = 25327
filter_df = empenhos_contratos_df[empenhos_contratos_df['codContrato'] == cod]
HTML(filter_df.to_html())
# filter_df.txtDescricaoProjetoAtividade

### Processando termos

In [581]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import TfidfVectorizer
import nltk

txt = contratos_df['txtObjetoContrato']
stopwords = nltk.corpus.stopwords.words('portuguese')

v = TfidfVectorizer(stop_words=stopwords)
x = v.fit(txt)
vocabulary = x.vocabulary_
vocabulary
[(k, vocabulary[k]) for k in sorted(vocabulary, key=vocabulary.get, reverse=True)]

[('ônibus', 5847),
 ('ômega', 5846),
 ('óleo', 5845),
 ('ítem', 5844),
 ('étnico', 5843),
 ('âmbito', 5842),
 ('ávore', 5841),
 ('ávila', 5840),
 ('áurea', 5839),
 ('ás', 5838),
 ('árvores', 5837),
 ('árvore', 5836),
 ('área', 5835),
 ('árbitros', 5834),
 ('álvaro', 5833),
 ('álcool', 5832),
 ('álamos', 5831),
 ('águia', 5830),
 ('águas', 5829),
 ('água', 5828),
 ('ágape', 5827),
 ('àgua', 5826),
 ('àgo', 5825),
 ('zéglio', 5824),
 ('zuleika', 5823),
 ('zuando', 5822),
 ('zito', 5821),
 ('zita', 5820),
 ('zezinho', 5819),
 ('zello', 5818),
 ('zelia', 5817),
 ('zeglio', 5816),
 ('zefinha', 5815),
 ('zefa', 5814),
 ('zeca', 5813),
 ('zazá', 5812),
 ('zampieri', 5811),
 ('zacaria', 5810),
 ('yvone', 5809),
 ('yvette', 5808),
 ('yuri', 5807),
 ('yoshio', 5806),
 ('yolanda', 5805),
 ('yamaguchi', 5804),
 ('yahwe', 5803),
 ('xxiii', 5802),
 ('xxi', 5801),
 ('xv', 5800),
 ('xlevy', 5799),
 ('xis', 5798),
 ('xinha', 5797),
 ('xiii', 5796),
 ('xi', 5795),
 ('xg', 5794),
 ('xavier', 5793),
 ('xa

In [582]:
teste = (contratos_df[
    (contratos_df['txtObjetoContrato'].str.contains('vigil', case=False))
])
groupSumContratos(teste)

Empty DataFrame
Columns: [valTotalEmpenhado, valLiquidado]
Index: []

valTotalEmpenhado  valLiquidado
txtDescricaoModalidade                                 
Pregão                          60.991713     42.347136
Dispensa de Licitação            1.707695      1.455421

valTotalEmpenhado  valLiquidado
txtDescricaoOrgao                                                
Secretaria Municipal de Educação          62.699409     43.802557

valTotalEmpenhado  \
txtObjetoContrato                                                                                                         
Serviços de vigilância CEUs - lotes 01, 02, 04 e 05                                                           36.855961   
Serviços de vigilância CEUs - lotes 03, 06 e 07                                                               23.945679   
SP/MP CONTRATAÇÃO DE SERVIÇOS DE SEGURANÇA E VIGILÂNCIA DESARMADA PARA A DRE-MP SENDO 5 POSTOS DI...           1.245441   
CONTRATAÇÃO DE EMPRESA ESPECIALIZADA EM VIGILANCIA DESARMADA PARA ATENDIMENTO DA SEDE DA DRE                   0.172787   
PREGÃO ELETRÔNICO  12/2017 - CONTRATAÇÃO DE EMPRESA PARA PRESTAÇ~]AO DE SERVIÇOS DE SEGURANÇA E V...           0.190073   
CONTRATAÇÃ ODE EMPRESA ESPECIALIZADA NA PRESTAÇÃ ODE SERVIÇO DE VIGILANCIA E SEGURANÇA PATRIMONIA...           0.289467   

                                                                                                      valLiquidado  
txtObjetoContrato                                                                                                   
Serviços de vigilância CEUs - lotes 01, 02, 04 e 05                                                      25.222767  
Serviços de vigilância CEUs - lotes 03, 06 e 07                                                          16.985714  
SP/MP CONTRATAÇÃO DE SERVIÇOS DE SEGURANÇA E VIGILÂNCIA DESARMADA PARA A DRE-MP SENDO 5 POSTOS DI...      1.158513  
CONTRATAÇÃO DE EMPRESA ESPECIALIZADA EM VIGILANCIA DESARMADA PARA ATENDIMENTO DA SEDE DA DRE              0.172787  
PREGÃO ELETRÔNICO  12/2017 - CONTRATAÇÃO DE EMPRESA PARA PRESTAÇ~]AO DE SERVIÇOS DE SEGURANÇA E V...      0.138655  
CONTRATAÇÃ ODE EMPRESA ESPECIALIZADA NA PRESTAÇÃ ODE SERVIÇO DE VIGILANCIA E SEGURANÇA PATRIMONIA...      0.124121

valTotalEmpenhado  valLiquidado
txtRazaoSocial                                                       
PREFEITURA DO MUNICÍPIO DE SÃO PAULO          62.699409     43.802557

valTotalEmpenhado  \
txtTipoContratacao                                                                   
Termo de Contrato - Serviços                                             60.801640   
Nota de Empenho Fornecimento de Bens de Consumo e/ou Permanente           1.897768   

                                                                 valLiquidado  
txtTipoContratacao                                                             
Termo de Contrato - Serviços                                        42.208481  
Nota de Empenho Fornecimento de Bens de Consumo e/ou Permanente      1.594076

# Orçamento - Itens

* Fontes dos recursos (para todos itens)

## 1. Pessoal
1. Docentes
2. Getores
3. Pessoal de apoio
4. Aposentadorias

## 2. Transporte Escolar
1. Passe Livre
2. TEG
3. Outros?

## 3. Funcionamento das escolas
1. Limpeza
2. Vigilância
3. Manutenção
4. Outros?

## 4. Uniformes e materiais escolares
1. Uniformes
2. Materiais (escolares, esportivos, educativos, didáticos, artísticos... como subdividir?)
3. Outros?

## 5. Parcerias
1. Convênios creches
2. Educação especial (como subdividir?)
3. MOVA
4. Outros?

## 6. Obras e reformas
1. Novas construções (possível subdividir em unidades educacionais e outros?)
2. Reformas (idem?)
3. Outros

## 7. Alimentação
1. Refeições prontas
2. Leve-Leite
3. Preparo e distribuição
4. Insumos (para refeições preparadas pela própria SME? Como subdividir?)
5. Outros?

## 8. Pedagógico e formação
1. Cursos e formação
2. Elaboração de materiais didáticos
3. Outros?

## 9. Tecnologia da informação
1. Internet
2. Manutenção de equipamentos
3. Outros?

## 1. Pessoal

### Filtro e exploração geral

#### Checar: filtro está correto? Está realmente capturando todas despesas com pessoal?

In [583]:
pessoal_filter = (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('rpps', case=False))
    |
    (empenhos_df['txtGrupoDespesa'].str.contains('pessoal', case=False))
    |
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Estagiários', case=False))
)
pessoal = (empenhos_df[pessoal_filter])
empenhos_df.loc[pessoal_filter, 'cat_1'] = 'pessoal'
groupSum(pessoal)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação        7721.646989   6250.746595   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação   6254.198601

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes           7721.646989   6250.746595   6254.198601

valTotalEmpenhado  \
txtDescricaoElemento                                                  
Vencimentos e Vantagens Fixas - Pessoal Civil           7227.363117   
Auxílio-Alimentação                                      433.567871   
Outros Serviços de Terceiros - Pessoa Jurídica            34.734801   
Auxílio-Transporte                                        17.757254   
Outros Auxílios Financeiros a Pessoas Físicas              7.890976   
Ressarcimento de Despesas de Pessoal Requisitado           0.332970   

                                                  valLiquidado  valPagoTotal  
txtDescricaoElemento                                                          
Vencimentos e Vantagens Fixas - Pessoal Civil      5770.231471   5770.231471  
Auxílio-Alimentação                                 429.293828    429.293828  
Outros Serviços de Terceiros - Pessoa Jurídica       27.796770     30.456309  
Auxílio-Transporte                                   17.757254     17.757254  
Outros Auxílios Financeiros a Pessoas Físicas         5.651375      6.136213  
Ressarcimento de Despesas de Pessoal Requisitado      0.015898      0.323526

valTotalEmpenhado  valLiquidado  \
txtDescricaoFonteRecurso                                            
Fundo Constitucional da Educação        4440.279767   3827.119838   
Tesouro Municipal                       3278.815338   2421.606567   
Transferências Federais                    2.551884      2.020191   

                                  valPagoTotal  
txtDescricaoFonteRecurso                        
Fundo Constitucional da Educação   3827.119838  
Tesouro Municipal                  2425.058572  
Transferências Federais               2.020191

valTotalEmpenhado  \
txtDescricaoItemDespesa                                            
RPPS - PMSP                                          7224.500741   
Auxílio-Refeição - RPPS                               231.914947   
Vale-Alimentação - RPPS                               201.652925   
Concessão de Bolsa-Auxílio para Estagiários            34.734801   
Auxílio-Transporte - RPPS                              17.757254   
Concessão de auxílio-transporte a estagiários           7.890976   
Outras Despesas Fixas - Pessoal Civil                   2.862376   
PMSP                                                    0.332970   

                                               valLiquidado  valPagoTotal  
txtDescricaoItemDespesa                                                    
RPPS - PMSP                                     5768.052052   5768.052052  
Auxílio-Refeição - RPPS                          231.900788    231.900788  
Vale-Alimentação - RPPS                          197.393040    197.393040  
Concessão de Bolsa-Auxílio para Estagiários       27.796770     30.456309  
Auxílio-Transporte - RPPS                         17.757254     17.757254  
Concessão de auxílio-transporte a estagiários      5.651375      6.136213  
Outras Despesas Fixas - Pessoal Civil              2.179419      2.179419  
PMSP                                               0.015898      0.323526

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário        7721.646989   6250.746595   6254.198601

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                          
Pessoal e Encargos Sociais        7227.696087   5770.247369   5770.554997
Outras Despesas Correntes          493.950901    480.499227    483.643604

valTotalEmpenhado  \
txtModalidadeAplicacao                                                          
Aplicações Diretas                                                7679.021212   
Transferências a Instituições Privadas sem Fins Lucrativos          42.625777   

                                                            valLiquidado  \
txtModalidadeAplicacao                                                     
Aplicações Diretas                                           6217.298451   
Transferências a Instituições Privadas sem Fins Lucrativos     33.448145   

                                                            valPagoTotal  
txtModalidadeAplicacao                                                    
Aplicações Diretas                                           6217.606079  
Transferências a Instituições Privadas sem Fins Lucrativos     36.592522

valTotalEmpenhado  \
txtRazaoSocial                                                                        
FOLHA DE PAGAMENTO _ EXECUTIVO                                          7224.500741   
SERV.SEC.MUN. DE EDUCAÇÃO - AUX. REFEIÇÃO                                433.567871   
CENTRO DE INTEGRAÇÃO EMPRESA ESCOLA CIEE                                  42.625777   
SERVIDORES DA SECRETARIA MUNICIPAL DE EDUCAÇÃO - AUX. TRANSPORTE          17.757254   
MINISTÉRIO DO PLANEJAMENTO ORÇAMENTO E GESTÃO - MP                         0.332970   
CARLOS AUGUSTO DE OLIVEIRA GONÇALVES                                       0.026935   
ROSELICE APARECIDA CARDOSO SANTOS                                          0.026918   
LUCIENE SOARES MARCOLINO                                                   0.026935   
SANDRA MARIA AMANCIO DUARTE                                                0.026779   
ANDREA REGINA DE CARVALHO CASANOVA                                         0.026733   
OLAVIO DE OLIVEIRA CONCEIÇÃO                                               0.026935   
MARTA DE SOUSA SILVA                                                       0.026694   
ROZILDA FRANCISCA DA SILVA PAIXAO                                          0.026779   
NADIA A.F.DA SILVA RIBEIRO                                                 0.026784   
ALESSANDRA APARECIDA GONÇALVES GOIS MONTEIRO                               0.026767   
ZENAIDE LIMA DOS SANTOS                                                    0.026582   
ANA CLAUDIA DA SILVA                                                       0.026479   
IZABEL CRISTINA S LIMA DOS SANTOS                                          0.026918   
ELLEN BIE                                                                  0.027156   
EDNALVA SOARES ANDRADE                                                     0.026727   
DANIEL DE SOUZA MEDEIROS                                                   0.026531   
CARLA REGINA LIMA DE OLIVEIRA                                              0.026161   
CLAUDIA CORREIA                                                            0.026408   
MARLY TEIXEIRA DE CASTRO                                                   0.026279   
CRISTIANE DOS SANTOS QUEIROZ                                               0.026055   
JOSIVETE DIAS SANTANA MEIRA                                                0.026727   
MARCIA CRISTINA PERUCHI DE SOUZA                                           0.026287   
VERA LUCIA DA SILVA DOS SANTOS                                             0.026509   
KATIA VASCONCELOS VANCO                                                    0.025807   
ERICA APARECIDA BARBOSA                                                    0.026564   
...                                                                             ...   
SONIA MARIA PEREIRA                                                        0.009700   
ROGERIO GONÇALVES                                                          0.009595   
SUELI DE FATIMA CABRAL GUEDES                                              0.009700   
TATIANA MOREIRA DOS SANTOS                                                 0.009700   
WALDO FELIPE GONZALEZ YANEZ                                                0.009700   
TANIA APARECIDA FEITOSA MEDEIROS                                           0.009595   
PEDRO RODRIGUES SANTOS                                                     0.009700   
ROSANE BADIALE BAPTISTA                                                    0.009595   
OSMAR APARECIDO EDUARDINHO                                                 0.025120   
KELI CRISTINA CORREIA                                                      0.024214   
ANA DALVA DOS SANTOS PENICHE PEREIRA                                       0.007927   
BRUNO ALEXANDRE DEANINI                                                    0.006675   
FABIO LUIZ DE ARGOLO                                                       0.025120   
MICHELLE MARIA DOS SANTOS SALAZAR                               

txtObjetoContrato
267               NaN

## 1.1. Docentes

#### Checar: será que realmente esse filtro compreende todos docentes? Me parece sub representado.

In [584]:
docentes_filter = pessoal_filter & (
    (empenhos_df['txtDescricaoSubFuncao'].str.contains('Educação Básica', case=False))
    &
    ~(empenhos_df['txtDescricaoItemDespesa'].str.contains('Estagiários', case=False))
)
docentes = (pessoal[docentes_filter])
empenhos_df.loc[docentes_filter, 'cat_2'] = 'docentes'
display(len(empenhos_df[empenhos_df['cat_2'] == 'docentes']) == len(docentes))
groupSum(docentes)

/home/bpl/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:6: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  


True

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação        7252.825865   5872.021815   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação   5872.021815

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes           7252.825865   5872.021815   5872.021815

valTotalEmpenhado  \
txtDescricaoElemento                                               
Vencimentos e Vantagens Fixas - Pessoal Civil        6817.728694   
Auxílio-Alimentação                                   417.984505   
Auxílio-Transporte                                     17.112666   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Vencimentos e Vantagens Fixas - Pessoal Civil   5441.198688   5441.198688  
Auxílio-Alimentação                              413.710462    413.710462  
Auxílio-Transporte                                17.112666     17.112666

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário        7252.825865   5872.021815   5872.021815

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                          
Pessoal e Encargos Sociais        6817.728694   5441.198688   5441.198688
Outras Despesas Correntes          435.097171    430.823128    430.823128

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas            7252.825865   5872.021815   5872.021815

valTotalEmpenhado  \
txtRazaoSocial                                                                        
FOLHA DE PAGAMENTO _ EXECUTIVO                                          6817.728694   
SERV.SEC.MUN. DE EDUCAÇÃO - AUX. REFEIÇÃO                                417.984505   
SERVIDORES DA SECRETARIA MUNICIPAL DE EDUCAÇÃO - AUX. TRANSPORTE          17.112666   

                                                                  valLiquidado  \
txtRazaoSocial                                                                   
FOLHA DE PAGAMENTO _ EXECUTIVO                                     5441.198688   
SERV.SEC.MUN. DE EDUCAÇÃO - AUX. REFEIÇÃO                           413.710462   
SERVIDORES DA SECRETARIA MUNICIPAL DE EDUCAÇÃO - AUX. TRANSPORTE     17.112666   

                                                                  valPagoTotal  
txtRazaoSocial                                                                  
FOLHA DE PAGAMENTO _ EXECUTIVO                                     5441.198688  
SERV.SEC.MUN. DE EDUCAÇÃO - AUX. REFEIÇÃO                           413.710462  
SERVIDORES DA SECRETARIA MUNICIPAL DE EDUCAÇÃO - AUX. TRANSPORTE     17.112666

txtObjetoContrato
4624               NaN

## 1.2. Gestores

#### Checar: será que realmente esse filtro compreende todos gestores? Depende do filtro anterior estar certo

In [585]:
gestores_filter = pessoal_filter & (
    (pessoal['txtDescricaoSubFuncao'].str.contains('Administração Geral', case=False))
    &
    ~(pessoal['txtDescricaoItemDespesa'].str.contains('Estagiários', case=False))
)
gestores = (pessoal[gestores_filter])
empenhos_df.loc[gestores_filter, 'cat_2'] = 'gestores'
display(len(empenhos_df[empenhos_df['cat_2'] == 'gestores']) == len(gestores))
groupSum(gestores)

/home/bpl/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:6: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  


True

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação         423.332971    343.097216   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação    343.404845

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes            423.332971    343.097216    343.404845

valTotalEmpenhado  \
txtDescricaoElemento                                                  
Vencimentos e Vantagens Fixas - Pessoal Civil            406.772047   
Auxílio-Alimentação                                       15.583366   
Auxílio-Transporte                                         0.644588   
Ressarcimento de Despesas de Pessoal Requisitado           0.332970   

                                                  valLiquidado  valPagoTotal  
txtDescricaoElemento                                                          
Vencimentos e Vantagens Fixas - Pessoal Civil       326.853364    326.853364  
Auxílio-Alimentação                                  15.583366     15.583366  
Auxílio-Transporte                                    0.644588      0.644588  
Ressarcimento de Despesas de Pessoal Requisitado      0.015898      0.323526

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário         423.332971    343.097216    343.404845

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                          
Pessoal e Encargos Sociais         407.105017    326.869262    327.176890
Outras Despesas Correntes           16.227954     16.227954     16.227954

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas             423.332971    343.097216    343.404845

valTotalEmpenhado  \
txtRazaoSocial                                                                        
FOLHA DE PAGAMENTO _ EXECUTIVO                                           406.772047   
SERV.SEC.MUN. DE EDUCAÇÃO - AUX. REFEIÇÃO                                 15.583366   
SERVIDORES DA SECRETARIA MUNICIPAL DE EDUCAÇÃO - AUX. TRANSPORTE           0.644588   
MINISTÉRIO DO PLANEJAMENTO ORÇAMENTO E GESTÃO - MP                         0.332970   

                                                                  valLiquidado  \
txtRazaoSocial                                                                   
FOLHA DE PAGAMENTO _ EXECUTIVO                                      326.853364   
SERV.SEC.MUN. DE EDUCAÇÃO - AUX. REFEIÇÃO                            15.583366   
SERVIDORES DA SECRETARIA MUNICIPAL DE EDUCAÇÃO - AUX. TRANSPORTE      0.644588   
MINISTÉRIO DO PLANEJAMENTO ORÇAMENTO E GESTÃO - MP                    0.015898   

                                                                  valPagoTotal  
txtRazaoSocial                                                                  
FOLHA DE PAGAMENTO _ EXECUTIVO                                      326.853364  
SERV.SEC.MUN. DE EDUCAÇÃO - AUX. REFEIÇÃO                            15.583366  
SERVIDORES DA SECRETARIA MUNICIPAL DE EDUCAÇÃO - AUX. TRANSPORTE      0.644588  
MINISTÉRIO DO PLANEJAMENTO ORÇAMENTO E GESTÃO - MP                    0.323526

txtObjetoContrato
4627               NaN

## 1.3. Pessoal de apoio

#### Como filtrar?

## 1.4. Aposentadorias

#### Como filtrar?

## 1.5 Adiantamentos (?)

In [586]:
adiantamento_filter = (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Adiantamento - Incisos I, II e III, Art. 2º da Lei nº 10.513/88', case=False))
)
adiantamento = (empenhos_df[adiantamento_filter])
empenhos_df.loc[adiantamento_filter, 'cat_1'] = 'pessoal'
empenhos_df.loc[adiantamento_filter, 'cat_2'] = 'adiantamento'
groupSum(adiantamento)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          12.433464     12.202874   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     12.202874

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             12.433464     12.202874     12.202874

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica          12.433464   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica     12.202874     12.202874

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 12.433464     12.202874     12.202874

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                               
Adiantamento - Incisos I, II e III, Art. 2º da Lei nº 10.513/88           12.433464   

                                                                  valLiquidado  \
txtDescricaoItemDespesa                                                          
Adiantamento - Incisos I, II e III, Art. 2º da Lei nº 10.513/88      12.202874   

                                                                  valPagoTotal  
txtDescricaoItemDespesa                                                         
Adiantamento - Incisos I, II e III, Art. 2º da Lei nº 10.513/88      12.202874

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Diretoria Regional de Educação - São Miguel                      1.542215   
Diretoria Regional de Educação - Pirituba                        1.365650   
Diretoria Regional de Educação - Campo Limpo                     1.311960   
Diretoria Regional de Educação - São Mateus                      1.230525   
Diretoria Regional de Educação - Guaianases                      1.213650   
Diretoria Regional de Educação - Penha                           1.016802   
Diretoria Regional de Educação - Butantã                         0.985692   
Diretoria Regional de Educação - Ipiranga                        0.828100   
Diretoria Regional de Educação - Freguesia/Brasilândia           0.729700   
Diretoria Regional de Educação - Jaçanã/Tremembé                 0.672770   
Diretoria Regional de Educação - Itaquera                        0.633000   
Diretoria Regional de Educação - Santo Amaro                     0.435400   
Diretoria Regional de Educação  Capela do Socorro                0.410300   
Gabinete do Secretário                                           0.057700   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Diretoria Regional de Educação - São Miguel                 1.527715   
Diretoria Regional de Educação - Pirituba                   1.321850   
Diretoria Regional de Educação - Campo Limpo                1.294360   
Diretoria Regional de Educação - São Mateus                 1.213925   
Diretoria Regional de Educação - Guaianases                 1.202350   
Diretoria Regional de Educação - Penha                      0.985852   
Diretoria Regional de Educação - Butantã                    0.969792   
Diretoria Regional de Educação - Ipiranga                   0.799700   
Diretoria Regional de Educação - Freguesia/Brasilândia      0.720700   
Diretoria Regional de Educação - Jaçanã/Tremembé            0.669770   
Diretoria Regional de Educação - Itaquera                   0.627800   
Diretoria Regional de Educação - Santo Amaro                0.417460   
Diretoria Regional de Educação  Capela do Socorro           0.393900   
Gabinete do Secretário                                      0.057700   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Diretoria Regional de Educação - São Miguel                 1.527715  
Diretoria Regional de Educação - Pirituba                   1.321850  
Diretoria Regional de Educação - Campo Limpo                1.294360  
Diretoria Regional de Educação - São Mateus                 1.213925  
Diretoria Regional de Educação - Guaianases                 1.202350  
Diretoria Regional de Educação - Penha                      0.985852  
Diretoria Regional de Educação - Butantã                    0.969792  
Diretoria Regional de Educação - Ipiranga                   0.799700  
Diretoria Regional de Educação - Freguesia/Brasilândia      0.720700  
Diretoria Regional de Educação - Jaçanã/Tremembé            0.669770  
Diretoria Regional de Educação - Itaquera                   0.627800  
Diretoria Regional de Educação - Santo Amaro                0.417460  
Diretoria Regional de Educação  Capela do Socorro           0.393900  
Gabinete do Secretário                                      0.057700

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          12.433464     12.202874     12.202874

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              12.433464     12.202874     12.202874

valTotalEmpenhado  valLiquidado  \
txtRazaoSocial                                                                  
ANDREA CALDEO CALVO                                    0.040000      0.040000   
JOSÉ VALDESIO DE SOUSA                                 0.040000      0.040000   
ANGELINA LETTIERI CARVALHO                             0.039000      0.039000   
SILVIA BUENO PAQUES N.DE OLIVEIRA                      0.035000      0.035000   
EDSON NOVAES PRADO                                     0.034000      0.034000   
CLÉZIO GAUGLITZ                                        0.031000      0.031000   
IRENE CRAVO CAMPOS                                     0.031000      0.031000   
FABIANA ANTONICCI                                      0.030500      0.030500   
MARISA MICHELACCI VALLEJO                              0.030200      0.030200   
ANA MARIA ADRIANO MAIA                                 0.029500      0.029500   
FERNANDO BORGES MESQUITA                               0.029400      0.029400   
EDSON DIAS                                             0.028100      0.028100   
MARIA APARECIDA DA MOTTA SAKOTANI                      0.028100      0.028100   
HILCEMARA ROCHA BARBOSA                                0.028000      0.028000   
SANDRA APARECIDA SILVA DUTRA                           0.032000      0.028000   
EDVALDO SANTA ROSA                                     0.030000      0.027500   
ELISEU PEREIRA NEVES                                   0.027000      0.027000   
GILMAR SANTOS DE OLIVEIRA                              0.027000      0.027000   
ANA INES VALVERDE MAGALHAES AFONSO FERNANDEZ           0.026500      0.026500   
DOUGLAS SOARES DE MIRANDA                              0.026000      0.026000   
MARA SUED SOBRAL DE OLIVEIRA                           0.025000      0.025000   
MARLI MARIA DE ALMEIDA COSTA                           0.028000      0.024000   
LAILA SIWEK SALA                                       0.024000      0.024000   
SONIA DE SOUZA COSTA                                   0.024000      0.024000   
PATRICIA ROCHA MACEDO DE OLIVEIRA                      0.023500      0.023500   
MARILUCIA FERREIRA DA SILVA                            0.023200      0.023200   
ROSELI DA SILVEIRA MARQUESINI LUZ                      0.023000      0.023000   
SOLANGE RAMOS FERREIRA                                 0.023000      0.023000   
ANA CAROLINA SILVA DE ALCANTARA                        0.022500      0.022500   
TANIA MARANESI                                         0.022500      0.022500   
...                                                         ...           ...   
DALVANIZE BEZERRA DA COSTA                             0.001000      0.001000   
GRACIANY APARECIDA FONTES                              0.001000      0.001000   
THAIS MENDONÇA CORDEIRO                                0.001000      0.001000   
IVANILDA FÁTIMA PRIETO                                 0.001000      0.001000   
CELIA CONSTANCIA BARASNIEWSKI MARCHETTI                0.000955      0.000955   
RENATA PEREIRA DA SILVA                                0.000850      0.000850   
CLAUDIA CAVALCANTE DOS SANTOS FERREIRA                 0.000850      0.000850   
ANA LUCIA CARDOSO PINA                                 0.000850      0.000850   
SILVIA CAMPOS SALOMÃO                                  0.000800      0.000800   
CESAR AUGUSTO SPINOLA BEVILACQUA                       0.000800      0.000800   
CRISTINA JORGE AZEVEDO VIEIRA                          0.000800      0.000800   
ROSEMEIRE INACIA DE FREITAS                            0.000800      0.000800   
MILENA JOSEFINA TAGLIAFERRO                            0.001600      0.000800   
HILDA AMELIA BEHLING DA SILVA                          0.000800      0.000800   
SANDRA REGINA SIMEAO MARQUES DE SOUZA                  0.000800      0.000800   
MÁRCIA DE PAULA CRUZ                                   0.000600      0.000600   
SUZI HELEN ALENCAR DE DEUS SÁ                          0.000600      0.000600

txtObjetoContrato
156               NaN

## 1.5 Estágios

In [587]:
estagios_filter = pessoal_filter & (pessoal['txtDescricaoItemDespesa'].str.contains('Estagiários', case=False))
estagios = (pessoal[estagios_filter])
empenhos_df.loc[estagios_filter, 'cat_2'] = 'estagios'
display(len(empenhos_df[empenhos_df['cat_2'] == 'estagios']) == len(estagios))
groupSum(estagios)

/home/bpl/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  


True

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          42.625777     33.448145   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     36.592522

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             42.625777     33.448145     36.592522

valTotalEmpenhado  \
txtDescricaoElemento                                                
Outros Serviços de Terceiros - Pessoa Jurídica          34.734801   
Outros Auxílios Financeiros a Pessoas Físicas            7.890976   

                                                valLiquidado  valPagoTotal  
txtDescricaoElemento                                                        
Outros Serviços de Terceiros - Pessoa Jurídica     27.796770     30.456309  
Outros Auxílios Financeiros a Pessoas Físicas       5.651375      6.136213

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário          42.625777     33.448145     36.592522

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          42.625777     33.448145     36.592522

valTotalEmpenhado  \
txtModalidadeAplicacao                                                          
Transferências a Instituições Privadas sem Fins Lucrativos          42.625777   

                                                            valLiquidado  \
txtModalidadeAplicacao                                                     
Transferências a Instituições Privadas sem Fins Lucrativos     33.448145   

                                                            valPagoTotal  
txtModalidadeAplicacao                                                    
Transferências a Instituições Privadas sem Fins Lucrativos     36.592522

valTotalEmpenhado  valLiquidado  \
txtRazaoSocial                                                              
CENTRO DE INTEGRAÇÃO EMPRESA ESCOLA CIEE          42.625777     33.448145   

                                          valPagoTotal  
txtRazaoSocial                                          
CENTRO DE INTEGRAÇÃO EMPRESA ESCOLA CIEE     36.592522

txtObjetoContrato
25339               NaN

# 2. Transporte Escolar

## 2.1. Passe livre

#### Como filtrar? Acredito que este gasto deva estar fora do orçamento da SME.

In [588]:
# encontrar repasses para SMT?
(empenhos_df[empenhos_df['txtRazaoSocial'].str.contains('transporte', case=False)]
 .groupby('txtRazaoSocial')['valLiquidado']
 .sum().apply(lambda x: round(x / 1000000, 1))
 .sort_values(ascending=False)
 .head(20)
)

txtRazaoSocial
TB SERVIÇOS TRANSPORTE LIMPEZA GERENCIAMENTO E RECURSOS HUMANOS S/A     21.9
SERVIDORES DA SECRETARIA MUNICIPAL DE EDUCAÇÃO - AUX. TRANSPORTE        17.8
COOPERATIVA BRASILEIRA DE TRANSPORTE COBRATE                             6.3
INTEGRA SOLUCOES EM LOGISTICA E TRANSPORTE LTDA - EPP                    4.7
P R SELIS TRANSPORTES EIRELI - EPP                                       2.4
COOPERATIVA DE TRANSPORTE ESCOLAR DE CONDUTOR E MONITOR - COOTRECM       1.9
AÇÃO TRANSPORTES E TURISMO LTDA - EPP                                    1.7
BELLA TRANSPORTES LTDA - ME                                              1.3
JULIEDRY TRANSPORTES LTDA -ME                                            1.3
VIA LUZ TRANSPORTES DE PASSAGEIROS LTDA                                  1.3
JTI TRANSPORTES LTDA - ME                                                1.2
TRANSRUBY TRANSPORTES EM GERAL LTDA - ME                                 1.0
COOPER PLANALTO - COOPERATIVA DE TRABALHO EM TRANSPORTES RODO

## 2.2. TEG

#### Checar filtro

In [589]:
teg_filter = (
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('transporte', case=False))
)
teg = (empenhos_df[teg_filter])
empenhos_df.loc[teg_filter, 'cat_1'] = 'transporte'
empenhos_df.loc[teg_filter, 'cat_2'] = 'teg'
groupSum(teg)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação         233.014406    194.595252   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação    211.120256

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes            233.014406    194.595252    211.120256

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros - Pessoa Física          123.252825   
Outros Serviços de Terceiros -Pessoa Jurídica         103.894366   
Obrigações Tributárias e Contributivas                  5.515257   
Despesas de Exercícios Anteriores                       0.351958   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros - Pessoa Física     103.753417    112.568457  
Outros Serviços de Terceiros -Pessoa Jurídica     86.712105     94.055240  
Obrigações Tributárias e Contributivas             3.788212      4.155040  
Despesas de Exercícios Anteriores                  0.341519      0.341519

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                233.014406    194.595252    211.120256

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                          
Transporte Escolar - EMEF                                           226.955018   
INSS / Contribuinte Individual                                        5.515257   
Outros Serviços de Terceiros - Pessoa Jurídica - Tributável           0.276233   
Pequenas Reformas - Centros Esportivos e Similares                    0.112273   
Outros Serviços de Terceiros - Pessoa Física                          0.075726   
Transporte Escolar - EMEI                                             0.065014   
Serviço com a População de Rua                                        0.007867   
Transporte Escolar - EMEE                                             0.002972   
Veículos                                                              0.004048   

                                                             valLiquidado  \
txtDescricaoItemDespesa                                                     
Transporte Escolar - EMEF                                      190.285810   
INSS / Contribuinte Individual                                   3.788212   
Outros Serviços de Terceiros - Pessoa Jurídica - Tributável      0.273998   
Pequenas Reformas - Centros Esportivos e Similares               0.103859   
Outros Serviços de Terceiros - Pessoa Física                     0.067521   
Transporte Escolar - EMEI                                        0.065014   
Serviço com a População de Rua                                   0.007867   
Transporte Escolar - EMEE                                        0.002972   
Veículos                                                         0.000000   

                                                             valPagoTotal  
txtDescricaoItemDespesa                                                    
Transporte Escolar - EMEF                                      206.443985  
INSS / Contribuinte Individual                                   4.155040  
Outros Serviços de Terceiros - Pessoa Jurídica - Tributável      0.273998  
Pequenas Reformas - Centros Esportivos e Similares               0.103859  
Outros Serviços de Terceiros - Pessoa Física                     0.067521  
Transporte Escolar - EMEI                                        0.065014  
Serviço com a População de Rua                                   0.007867  
Transporte Escolar - EMEE                                        0.002972  
Veículos                                                         0.000000

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário         233.014406    194.595252    211.120256

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes         233.014406    194.595252    211.120256

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas             233.014406    194.595252    211.120256

valTotalEmpenhado  \
txtRazaoSocial                                                                              
COOPERATIVA BRASILEIRA DE TRANSPORTE COBRATE                                     7.420587   
COOPER- X - COOP SERV TRANSPORTAD AUT PAS, ESCOLARES E MON DO EST SP             6.522607   
INSTITUTO NACIONAL DO SEGURO SOCIAL                                              5.515257   
P R SELIS TRANSPORTES EIRELI - EPP                                               2.994445   
COOPER DE TRAB. DOS C. A.T.P NA  REP. FED.DO.BR COOPERUNIÃO BRASILEIRA           2.403070   
COOPERATIVA DE TRANSPORTE ESCOLAR DE CONDUTOR E MONITOR - COOTRECM               2.205080   
BELLA TRANSPORTES LTDA - ME                                                      1.472303   
JULIEDRY TRANSPORTES LTDA -ME                                                    1.518641   
VIA LUZ TRANSPORTES DE PASSAGEIROS LTDA                                          1.381945   
JTI TRANSPORTES LTDA - ME                                                        1.333289   
EDILSON DA LUZ CARVALHO                                                          1.256544   
JAMBEIROS LUXO TRANSPORTES E TURISMO LTDA ME                                     1.005418   
WM DIAS TRANSPORTE ESCOLAR LTDA ME                                               0.978898   
COOPERARTE-COOP. DE TRABALHO TRANSP.AUT. DE PASS. E DE ESCOLARES DE SP           1.094957   
TRANSLESTE TRANSPORTE ESCOLAR E TURISMO LTDA - ME                                0.940548   
MILLA TRANSPORTE E TURISMO LTDA                                                  1.081963   
FABIO E KARINA TRNASPORTE ESCOLAR LTDA ME                                        1.057522   
IRMAOS SANTANA TRANSPORTE ESCOLAR LTDA - ME                                      0.872450   
DARIO  CAMPOS DA SILVA                                                           1.030644   
SISTEMA BRASILEIRO DE TAQUARAL LTDA - ME                                         0.857560   
WAGNER ROBERTO DA SILVA TRANSPORTES - ME                                         0.889869   
VIRTUDE LOCADORA DE VEICULOS LTDA-ME                                             0.794227   
L.V.A TRANSPORTE ESCOLAR LTDA - ME                                               0.758111   
ACALANTO TRANSPORTES LTDA-ME                                                     0.768953   
J. V. N. TRANSPORTES E LOCADORA DE VEICULOS LTDA - ME                            0.587144   
CREMASCO TRANSPORTES E TERCEIRIZAÇÃO LTDA ME                                     0.612379   
WILSIL TRANSPORTE ESCOLAR LTDA - ME                                              0.553811   
ARTFRAN TRANSPORTES LTDA - ME                                                    0.631099   
QUALI SERVICE TRANSPORTES LTDA ME                                                0.510687   
ALEXSANDRA MARIA DE ASSIS TRANSPORTES ME                                         0.522243   
...                                                                                   ...   
CLAUDETE NUNES DRIUZZO                                                           0.014610   
KARINA ALVES MAURICIO                                                            0.006549   
LUIZ VIANA SILVA                                                                 0.005147   
GILVANDRO ANTONIO DE SOUZA                                                       0.007757   
VERONICA RODRIGUES DA SILVEIRA                                                   0.005724   
SERGIO JOSE DE LIMA - ME                                                         0.003633   
REGINA MARIA GENTILE CAPITULINO                                                  0.011586   
MARCIO ROBERTO SANTOS SILVA                                                      0.007274   
JOSÉ CARLOS SIMÃO                                                                0.004790   
FERNANDO DO PATROCINIO FIGUEIREDO                                                0.004993   
MARCO ANTONIO COSTA JUNIOR                                               

txtObjetoContrato
49                                                                                                     NaN
816                                                          CONTRATAÇÃO DE INTÉRPRETE/INSTRUTOR DE LIBRAS
1801                                       Contratação de Instrutor de Instrumentos de Metais e Percussão 
1888   PROGRAMA RECREIO NAS FÉRIAS - JULHO/2017 - DE ACORDO COMO EDITAL DE CREDENCIAMENTONº 004/2016/20...
1973   LOCAÇÃO DE BRINQUEDOS INFLÁVEIS, PARA A REALIZAÇÃO DO PROGRAMA RECREIO NAS FÉRIAS – JULHO/2017 N...
1987                                                        CONTRATAÇÃO DE OFICINEIRO- EXTENSÃO DE JORNADA
1993                                             2º REPASSE PTRF/ 2017 -CUSTEIO - DRE G- CEI INCONFIDENTES
2037                                                                                       JOGOS DIVERSOS 
2106                                    CONTRATAÇÃO DE EMPRESA P/PRESTAÇÃO DE SERVIÇO DE MINUTAGEM - CEUS 
2215   SP/MP CONTRATAÇÃO DE INSTRUTOR DE LIBRAS PERÍODO DE 01/06/2017 À 30/05/2018 - CEU EMEF JARDIM SÃ...
2224                        Repasse de Recursos do PNAE para o CEI STA. CLARA DE ASSIS Cód. INEP  35391281
2246                                             CONTRATAÇÃO DE AGENTES PARA RECREIO NAS FÉRIAS JULHO/2017
2248               Aquisição de materiais descartáveis para o projeto Rede 2017 - Cotação Eletrônica nº 10
2249                                                                    Poda e remoção - EMEI OSWALDO CRUZ
2251                                             CELEBRAÇÃO DE TERMO DE COLABORAÇÃO - CEI CEU ESTRELADO II
2256   Aquisição de fraldas descartáveis geriátricas para as Unidades Educacionais da Diretoria Regiona...
2379    REPASSES DE RECURSOS PARA APM DE ACORDO COM A LEI FEDERAL Nº 9394/1996, LEI MUNICIPAL Nº 13.991...
2398   Repasse de recursos para APM de acordo com a Lei Federal Nº 9394/96, Lei Municipal Nº 13.991/05,...
2419                                                       CONTRATAÇÃO DE OFICINEIRO - EXTENSÃO DE JORNADA
2422                            Contratação de Serviços de Manutenção para a EMEF Celia Regina L. Consolin
2435                     Contratação de serviços de nutrição e alimentação escolar – LOTE  11B - PENHA II.
2450   REPASSE DE RECURSO PARA APM ,DE ACORDO COM A LEI 8394/1996, PORTARIA DE SME INDICANDO O VALOR PA...
2454                    Repasse de Recursos do PNAE para o CEI JARDIM FLOR DE LIS V - CÓD. INEP 35297574\n
2511                   Contratação de Agentes de Recreação, Oficineiros e Coordenadores -Edição Julho 2017
2850                                                     CONTRATAÇÃO DE OFICINEIRO RECREIO NAS FERIAS 2017
3038                                                      PAGAMENTO DO ADITAMENTO DO CEI LAR CRIANÇA FELIZ
3042                                      CELEBRAÇÃO DO TERMO DE PARCERIA POR MEIO DE TERMO DE COLABORAÇÃO
3059                                       AQUISIÇÃO DE MATERIAL ESPORTIVO - RECREIO NAS FÉRIAS JULHO/2017
3065                               Repasse de Recursos do PNAE para o CEI VILA GUSTAVO Cód. INEP  35182588
3148                       2º REPASSE PTRF/2017 - CUSTEIO - APM CEU EMEI THERESINHA SQUINCA DA SILVA, PROF
...                                                                                                    ...
20712                                         2º REPASSE PTRF/2017 - CUSTEIO - APM - EMEI ADONIRAN BARBOSA
20821                                                                              Aquisição de mobiliario
20949  Repasse de recursos para APM de acordo com a Lei Federal nº 9.394/1996, Lei Municipal nº 13.991/...
20953  Repasse de recursos para APM de acordo com a Lei Federal nº 9.394/1996, Lei Municipal nº 13.991/...
20955  Repasse de recursos para APM de acordo com a Lei Federal nº 9.394/1996, Lei Municipal nº 13.991/...
20958  REPASSES DE RECURSOS À APM, DE ACORDO LEI FEDERAL 9394/1996 E PORTARIAS DA SME INDICANDO O VALOR...
20965  Repasse de recur

## 2.3 Aluguel de veículos

In [590]:
veiculos_filter = (
    (empenhos_df['txtDescricaoSubElemento'].str
     .contains('Locação de Bens Móveis de Outra Natureza e Intangíveis', case=False)
     &
     ~(empenhos_df['txtDescricaoItemDespesa'].str
     .contains('Locação de Bens Móveis com Finalidade Artística e Cultural', case=False)
    ))
)
veiculos = (empenhos_df[veiculos_filter])
empenhos_df.loc[veiculos_filter, 'cat_1'] = 'transporte'
empenhos_df.loc[veiculos_filter, 'cat_2'] = 'veiculos'
groupSum(veiculos)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          23.468506      15.92027   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     17.627189

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             23.468506      15.92027     17.627189

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica          23.468506   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica      15.92027     17.627189

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 23.468506      15.92027     17.627189

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoItemDespesa                                                      
Veículos Leves com Motorista            13.177409      9.390203      9.889766
Ônibus com Motorista                     5.484531      3.555379      4.550464
Veículos Pesados com Motorista           3.201524      1.763547      1.919989
Veículos Pesados                         1.155082      0.982007      1.022657
Veículos Leves                           0.427569      0.229134      0.244313
Ônibus                                   0.022391      0.000000      0.000000

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Diretoria Regional de Educação - Campo Limpo                     4.371954   
Gabinete do Secretário                                           2.531521   
Diretoria Regional de Educação - Penha                           1.698923   
Diretoria Regional de Educação - São Miguel                      1.223700   
Diretoria Regional de Educação - Santo Amaro                     1.726081   
Departamento de Alimentação Escolar                              1.144227   
Diretoria Regional de Educação - Itaquera                        1.327189   
Diretoria Regional de Educação - Ipiranga                        1.228475   
Diretoria Regional de Educação - Butantã                         1.127668   
Diretoria Regional de Educação  Capela do Socorro                0.990940   
Diretoria Regional de Educação - Pirituba                        0.964565   
Diretoria Regional de Educação - Guaianases                      0.860694   
Diretoria Regional de Educação - Jaçanã/Tremembé                 1.070547   
Diretoria Regional de Educação - Freguesia/Brasilândia           0.967392   
Diretoria Regional de Educação - São Mateus                      0.548169   
Coordenadoria de Alimentação Escolar                             0.618161   
Diretoria Regional de Educação - Capela do Socorro               1.068302   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Diretoria Regional de Educação - Campo Limpo                3.036236   
Gabinete do Secretário                                      1.686781   
Diretoria Regional de Educação - Penha                      1.258398   
Diretoria Regional de Educação - São Miguel                 1.062067   
Diretoria Regional de Educação - Santo Amaro                1.036800   
Departamento de Alimentação Escolar                         1.083600   
Diretoria Regional de Educação - Itaquera                   0.933929   
Diretoria Regional de Educação - Ipiranga                   0.912538   
Diretoria Regional de Educação - Butantã                    0.829937   
Diretoria Regional de Educação  Capela do Socorro           0.714839   
Diretoria Regional de Educação - Pirituba                   0.703872   
Diretoria Regional de Educação - Guaianases                 0.724682   
Diretoria Regional de Educação - Jaçanã/Tremembé            0.630107   
Diretoria Regional de Educação - Freguesia/Brasilândia      0.489960   
Diretoria Regional de Educação - São Mateus                 0.492430   
Coordenadoria de Alimentação Escolar                        0.134621   
Diretoria Regional de Educação - Capela do Socorro          0.189475   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Diretoria Regional de Educação - Campo Limpo                3.991971  
Gabinete do Secretário                                      1.733829  
Diretoria Regional de Educação - Penha                      1.342298  
Diretoria Regional de Educação - São Miguel                 1.120934  
Diretoria Regional de Educação - Santo Amaro                1.085174  
Departamento de Alimentação Escolar                         1.083600  
Diretoria Regional de Educação - Itaquera                   1.008471  
Diretoria Regional de Educação - Ipiranga                   0.988564  
Diretoria Regional de Educação - Butantã                    0.855946  
Diretoria Regional de Educação  Capela do Socorro           0.788414  
Diretoria Regional de Educação - Pirituba                   0.776292  
Diretoria Regional de Educação - Guaianases                 0.771783  
Diretoria Regional de Educação - Jaçanã/Tremembé            0.657608  
Diretoria Regional de Educação - Freguesia/Brasilândia      0.514119  
Diretoria Regional de Educação - São Mateus                 0.505160  
Coordenadoria de

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          23.468506      15.92027     17.627189

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              23.468506      15.92027     17.627189

valTotalEmpenhado  \
txtRazaoSocial                                                                                    
AÇÃO TRANSPORTES E TURISMO LTDA - EPP                                                  3.302512   
EBSL EMPRESA BRASILEIRA DE SERVICOS DE LOCACOES LTDA - EPP                             2.774193   
UNITRANSP - COOP. UNIÃO INTERMODAL DE TRANSP. AUTÔNOMOS DE SÃO PAULO                   1.882072   
TRANSRUBY TRANSPORTES EM GERAL LTDA - ME                                               1.329792   
DANLEX SERVIÇOS LTDA.                                                                  2.115157   
TZAR LOGÍSTICA LTDA                                                                    1.100882   
CTPT - COOP. DE TRAB. DOS PROF. DA  ÁREA  DE TRANSPORTES                               1.310132   
COOPER PLANALTO - COOPERATIVA DE TRABALHO EM TRANSPORTES RODOVIÁRIOS                   1.157570   
COOPERLESTE - COOPERATIVA DE SERVIÇOS DE TRANSPORTES                                   0.833352   
TOP 5 SOLUCOES EM TRANSPORTES LTDA.- ME                                                0.810024   
CORCOVADO TRANSPORTADORA TURISTICA LTDA                                                0.662470   
TRANSLIGHT TRANSPORTES & SERVIÇOS LTDA - EPP                                           0.615356   
G.N. GERENCIAMENTO NACIONAL DE TRANSPORTES E SERVIÇOS GERAIS LTDA                      0.702150   
MULTI VIAS LOCAÇÕES E VIAGENS LTDA EPP                                                 0.590324   
TRANSPORTES - TURISMO E SERVIÇOS JP GRANDINO EIRELI                                    0.497360   
COOPERTAC - COOPERATIVA DOS PRESTADORES DE SERVIÇOS DE TRANSPORTES DO BRASIL           0.811599   
VIA 80 TRANSPORTES LTDA - ME                                                           0.379590   
TRANSQUERQUI LTDA - EPP                                                                0.415521   
MESQUITTA SERVICOS E TRANSPORTES LTDA                                                  0.371145   
COUTINHO & FERREIRA SERVIÇOS E TRANSPORTE LTDA - EPP                                   0.271500   
COOPERCAR - COOP DOS PREST DE SERV NA ÁREA DE TRANSP EM GERAL DE SP                    0.314986   
VIVA MOTO EXPRESS LTDA - EPP                                                           0.226026   
99 TECNOLOGIA LTDA.                                                                    0.462591   
SP LOCSERV LOCAÇÃO DE VEÍCULOS E SERVIÇOS GERAIS EIRELI - EPP                          0.134716   
ALEX SANDRO MACIEL DANTAS ME                                                           0.164222   
TURISMO PAVÃO LTDA                                                                     0.136357   
ARMAZENA ARMAZENS GERAIS LTDA - EPP                                                    0.054200   
INNOVARY FUTURE COMERCIAL LTDA - ME                                                    0.018700   
BEIJA FLOR LOCADORA DE VEÍCULOS LTDA - EPP                                             0.007808   
GRANDE HEROI TURISMO LTDA - ME                                                         0.007500   
BREDA TRANSPORTES E SERVICOS S.A                                                       0.004500   
VC TRANSPORTES TURISMO E EMPREENDIMENTOS LTDA - EPP                                    0.004200   

                                                                              valLiquidado  \
txtRazaoSocial                                                                               
AÇÃO TRANSPORTES E TURISMO LTDA - EPP                                             1.725778   
EBSL EMPRESA BRASILEIRA DE SERVICOS DE LOCACOES LTDA - EPP                        1.933145   
UNITRANSP - COOP. UNIÃO INTERMODAL DE TRANSP. AUTÔNOMOS DE SÃO PAULO              1.482244   
TRANSRUBY TRANSPORTES EM GERAL LTDA - ME                                          1.033230   
DANLEX SERVIÇOS LTDA.                                                             0.948752   
TZAR LOGÍSTICA LTDA                                  

txtObjetoContrato
405                                                                                                    NaN
1386   ATA RP 005-SMG/COBES-2017 - Contratação de empresa ou cooperativa especializada na intermediação...
1424                  SERVIÇO DE LOCAÇÃO DE 420 ÔNIBUS DE VIAGEM  PARA TRANSPORTE DE ALUNOS E FUNCIONÁRIOS
4868   Contratação de Empresa Especializada para Prestação de Serviços  de Transporte de Veículos , Inc...
5985   LOCAÇÃO EMPRESA ESPECIALIZADA EM TRANSPORTE DE ÔNIBUS DE VIAGEM PARA TRANSPORTAR FUNCIONÁRIOS E ...
6883   PROGRAMA RECREIO NAS FÉRIAS - JANEIRO/2017 - DE ACORDO COM O EDITAL DE CREDENCIAMENTO Nº 004/201...
7496                                         PRESTAÇÃO DE SERVIÇOS DE MOTOFRETE PARA ATENDIMENTO DA DRE-BT
7930   Licitação Ata de Registro de Preços - Prestação de serviços de transporte com ônibus e motorista...
8438                                                                                     Locação de ônibus
8458   Contratação de Empresa Ônibus para Transporte de Alunos da DRE PJ para participação no Programa ...
8503    Contratação de empresa especializada na prestação de serviços de transporte em ônibus de fretam...
8506                                                                                     LOCAÇÃO DE ÔNIBUS
8516                                                               DL- CONTRATAÇÃO DE ÔNIBUS COM MOTORISTA
8713                              Contratação de viagens de ônibus para eventos - Programa Visão do Futuro
8951                                   Contratação de Ônibus para o 1º Mutirão do Programa Visão do Futuro
9999   REPASSES DE RECURSOS PARA APM DE ACORDO COM: LEI FEDERAL Nº 9394/1996; LEI MUNICIPAL Nº 13.991/0...
11194  contratação através de ATA DE RP Nº 02/SME/2017 – CONTRATAÇÃO DE LOCAÇÃO DE ÔNIBUS COM MOTORISTA...
11601  Contratação de transporte de alunos da Rede Municipal de Educação para o evento JAM de Robótica ...
12049  CONTRATAÇÃO EMERGENCIAL - Locação de veículos com quilometragem livre, incluso motorista e combu...
12550                      PR/SM- SERVIÇO DE TRANSPORTE EM ONIBUS DE FRETAMENTO POR VIAGEM-ARP07/SME/2017.
15298                                                     PREGÃO 02/2017-DRESA - VEICULOS via WEB e MOBILE
17398  CONTRATAÇÃO DE EMPRESA ESPECIALIZADA NA PRESTAÇÃO DE SERVIÇOS DE TRANSPORTE EM ÔNIBUS DE FRETAME...
18582  EMPRESA ESPECIALIZADA NA PRESTAÇÃO DE SERVIÇOS DE  TRANSPORTE EM ÔNIBUS DE FRETAMENTO POR VIAGEM...
19156   Contratação de serviços de transporte em ônibus de fretamento de viagem - ATA de RP nº 06/SME/2017
22060                                     LOCAÇÃO DE ONIBUS PARA TRANSPORTE DE ALUNOS - ATA RP 02/SME-2017
26354  Contratação de empresa especializada na prestação de serviço de gerenciamento de transporte de p...
27712  Contratação de empresa especializada na prestação de serviço de transporte em ônibus de fretamen...
28566                                                                              LOCAÇÃO DE CAMINHÃO BAÚ
28873  Contratação de serviços de transporte individual de passageiros via aplicativo - utilização da A...
30690       CONTRATAÇÃO DE ÔNIBUS COM MOTORISTA E COMBUSTÍVEL PARA ATENDIMENTO DA DEMANDA DA DRE IPIRANGA.
...                                                                                                    ...
33600  Transporte individual remunerado de passageiros via aplicativo customizável web e mobile com apo...
34202  DL- EMERGENCIAL - CONTRATAÇÃO DE EMPRESA ESPECIALIZADA EM LOCAÇÃO DE VEÍCULOS, COM QUILOMETRAGEM...
37489                                                              LOCAÇÃO DE VEÍCULOS LEVES COM MOTORISTA
40380                       PR/SM SERVIÇO DE TRANSPORTE EM ONIBUS DE FRETAMENTO POR VIAGEM-ARP 07/SME/2017
40575  SP/MP CONTRATAÇÃO DE EMPRESA ESPECIALIZADA NA INTERMEDIAÇÃO DE SERVIÇOS DE TRANSPORTE INDIVIDUAL...
40597                  CONTRATAÇÃO DE EMPRESA PARA TRANSPORTE E ENTREGA DE MATERIAIS DIVERSOS DRE CL E UES
40605                  

## 2.3. Outros?

# 3. Funcionamento das escolas

## 3.1. Limpeza

#### Como filtrar?

In [591]:
limpeza_filter = (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('limpeza', case=False))
    |
    (empenhos_df['txtDescricaoSubElemento'].str.contains('limpeza', case=False))
)
limpeza = (empenhos_df[limpeza_filter])
empenhos_df.loc[limpeza_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[limpeza_filter, 'cat_2'] = 'limpeza'
groupSum(limpeza)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação         465.139461    407.756859   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação    425.853968

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes            465.139461    407.756859    425.853968

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica         460.595615   
Material de Consumo                                     3.827840   
Locação de Mão-de-Obra                                  0.716006   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica    404.679844    422.004253  
Material de Consumo                                2.588546      3.279138  
Locação de Mão-de-Obra                             0.488469      0.570577

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                465.139461    407.756859    425.853968

valTotalEmpenhado  valLiquidado  \
txtDescricaoItemDespesa                                                         
Limpeza de Ambientes                                 460.588315    404.674394   
Produtos para Toucador e Higiene Pessoal               2.349727      1.613706   
Diversos Materiais de Limpeza e Higienização           1.362784      0.871918   
Limpeza e Conservação                                  0.716006      0.488469   
Antisépticos e Desinfetantes                           0.115328      0.102923   
Dedetização, Descupinização e Outros                   0.007300      0.005450   

                                              valPagoTotal  
txtDescricaoItemDespesa                                     
Limpeza de Ambientes                            421.998803  
Produtos para Toucador e Higiene Pessoal          2.040909  
Diversos Materiais de Limpeza e Higienização      1.122901  
Limpeza e Conservação                             0.570577  
Antisépticos e Desinfetantes                      0.115328  
Dedetização, Descupinização e Outros              0.005450

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Gabinete do Secretário                                         458.435946   
Diretoria Regional de Educação - São Miguel                      1.320629   
Diretoria Regional de Educação - Campo Limpo                     0.950557   
Diretoria Regional de Educação  Capela do Socorro                0.770271   
Diretoria Regional de Educação - Guaianases                      0.698750   
Diretoria Regional de Educação - Penha                           0.645757   
Diretoria Regional de Educação - São Mateus                      0.459895   
Diretoria Regional de Educação - Butantã                         0.322566   
Diretoria Regional de Educação - Jaçanã/Tremembé                 0.328513   
Diretoria Regional de Educação - Itaquera                        0.261672   
Diretoria Regional de Educação - Santo Amaro                     0.240026   
Diretoria Regional de Educação - Ipiranga                        0.235040   
Diretoria Regional de Educação - Capela do Socorro               0.214676   
Diretoria Regional de Educação - Pirituba                        0.166929   
Departamento de Alimentação Escolar                              0.077674   
Diretoria Regional de Educação - Freguesia/Brasilândia           0.009752   
Coordenadoria de Alimentação Escolar                             0.000809   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Gabinete do Secretário                                    402.873881   
Diretoria Regional de Educação - São Miguel                 0.729638   
Diretoria Regional de Educação - Campo Limpo                0.584489   
Diretoria Regional de Educação  Capela do Socorro           0.686966   
Diretoria Regional de Educação - Guaianases                 0.522635   
Diretoria Regional de Educação - Penha                      0.535053   
Diretoria Regional de Educação - São Mateus                 0.406673   
Diretoria Regional de Educação - Butantã                    0.302487   
Diretoria Regional de Educação - Jaçanã/Tremembé            0.280679   
Diretoria Regional de Educação - Itaquera                   0.172035   
Diretoria Regional de Educação - Santo Amaro                0.227643   
Diretoria Regional de Educação - Ipiranga                   0.005943   
Diretoria Regional de Educação - Capela do Socorro          0.210540   
Diretoria Regional de Educação - Pirituba                   0.136647   
Departamento de Alimentação Escolar                         0.071800   
Diretoria Regional de Educação - Freguesia/Brasilândia      0.009752   
Coordenadoria de Alimentação Escolar                        0.000000   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Gabinete do Secretário                                    419.920942  
Diretoria Regional de Educação - São Miguel                 0.900521  
Diretoria Regional de Educação - Campo Limpo                0.889156  
Diretoria Regional de Educação  Capela do Socorro           0.759155  
Diretoria Regional de Educação - Guaianases                 0.561207  
Diretoria Regional de Educação - Penha                      0.560037  
Diretoria Regional de Educação - São Mateus                 0.437826  
Diretoria Regional de Educação - Butantã                    0.322566  
Diretoria Regional de Educação - Jaçanã/Tremembé            0.305838  
Diretoria Regional de Educação - Itaquera                   0.259792  
Diretoria Regional de Educação - Santo Amaro                0.240026  
Diretoria Regional de Educação - Ipiranga                   0.231198  
Diretoria Regional de Educação - Capela do Socorro          0.210540  
Diretoria Regional de Educação - Pirituba                   0.166929  
Departamento de Alimentação Escolar                         0.077674  
Diretoria Region

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes         465.139461    407.756859    425.853968

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas             465.139461    407.756859    425.853968

valTotalEmpenhado  \
txtRazaoSocial                                                                                                           
LIMPADORA CALIFORNIA LTDA                                                                                    56.133925   
ARCOLIMP SERVIÇOS GERAIS LTDA                                                                                42.049078   
G4S INTERATIVA SERVICE LTDA                                                                                  35.803843   
GUIMA CONSECO CONSTRUÇÃO, SERVIÇOS E COMÉRCIO LTDA                                                           31.047000   
DEMAX SERVICOS E COMERCIO LTDA                                                                               30.061606   
A. TONANNI CONSTRUÇÕES E SERVIÇOS LTDA                                                                       25.723431   
EPS - EMPRESA PAULISTA DE SERVICOS S.A.                                                                      24.503134   
GOCIL SERVICOS GERAIS  LTDA                                                                                  32.003199   
TB SERVIÇOS TRANSPORTE LIMPEZA GERENCIAMENTO E RECURSOS HUMANOS S/A                                          22.812355   
CENTRO SANEAMENTO E SERVIÇOS AVANCADOS LTDA                                                                  21.535106   
AGRÍCOLA E CONSTRUTORA MONTE AZUL LTDA                                                                       21.134555   
COR LINE SISTEMA DE SERVIÇOS LTDA                                                                            20.198090   
WHITENESS - CONSULTORIA E SERVIÇOS LTDA                                                                      17.234460   
PAINEIRAS LIMPEZA E SERVIÇOS GERAIS LTDA.                                                                    14.551701   
ALTERNATIVA SERVIÇOS E TERCEIRIZAÇÃO EM GERAL LTDA                                                           12.450802   
INTERATIVA-DEDETIZACAO HIGIENIZACAO E CONSERVACAO LTDA                                                       10.704002   
EMPRESA TEJOFRAN DE SANEAMENTO E SERVIÇOS LTDA                                                               22.075470   
PROVAC TERCEIRIZAÇÃO DE MÃO DE OBRA LTDA                                                                     12.199077   
R.C.A  PRODUTOS E SERVIÇOS LTDA                                                                               5.635431   
BOLLIMP COMERCIAL DE EMBALAGENS DESCARTAVEIS E PRESTACAO DE SERVICOS DE LIMPEZA E HIGIENIZACAO LTDA           1.714793   
SPEZIA COMERCIAL DE MATERIAIS E SUPRIMENTOS EIRELI - ME                                                       0.751923   
MOMILLI COMERCIAL LTDA - EPP                                                                                  1.174376   
PRIME STOP COMERCIAL LTDA - ME                                                                                0.419597   
QUALITECNICA EMPRESA NACIONAL DE SERVICOS LTDA - ME.                                                          0.393785   
MULTISERVICE NACIONAL DE SERV LTDA                                                                            0.526609   
MEDPOA COMERCIO DE MATERIAL HOSPITALAR LTDA                                                                   0.312215   
PHOENIX COMERCIAL DE INFORMATICA PAPELARIA E MOVEIS LTDA - EPP                                                0.236837   
FUTURA COMERCIO DE PAPEIS E SERVIÇOS DIVERSOS LTDA - ME                                                       0.217595   
TOWER SERVIÇOS E MATERIAIS EIRELI - ME                                                                        0.173586   
PERFECT CLEAN SERVIÇOS ESPECIALIZADOS - EIRELI - EPP                                                          0.160632   
...                                                                                                                ...   
CIRURGICA KD LTDA                                                          

txtObjetoContrato
368                      Materiais de higiene e saúde para o uso com os alunos com necessidades especiais.
578                                                               AQUISIÇÃO DE FRALDAS PARA USO NOS CEI'S 
1195                                                         AQUISIÇÃO DE LUVA DESCARTÁVEL - TAMANHO MÉDIO
1425   AQUISIÇÃO DE PRODUTO PARA ASSADURAS, CONFORME ATA DE RP. 42/SME/2016 - COMERCIAL CENTER VALLE LTDA.
1432   AQUISIÇÃO DE PASTA E DENTE COM FLUOR E ESCOVA DENTAL INFANTIL, CONFORME ATA DE RP 38/SME/2016 - ...
1691              Contratação Emergencial de Serviços de Limpeza CEUs. por 180 dias a partir de 23/10/2017
4129                                                         Aquisição de fraldas para o Projeto Rede 2017
4541   Prestação de serviços de limpeza, asseio e conservação predial, visando a obtenção de adequadas ...
4629     DL- Aquisição de água sanitária em embalagem de 1 litros para uso das lavanderias dos CEIs DRESA.
4741                DL- Aquisição de detergente em pó embalagem de  1 kg para uso das lavanderias dos CEIs
4869                                                              FRALDAS  DESCARTÁVEIS  INFANTIL E ADULTO
4958                               SP/SR - Aquisição de detergente em pó biodegradável - COTAÇÃO Nº24/2017
5355                                                  Aquisição de produto para prevenir assadura infantil
5451              Cotação Eletrônica n.º 20/2017 - Aquisição de materiais de limpeza para os CEIs e CIEJAs
5535                                                 Ata de R.P. n.º 40/SME/2016 - Aquisição de Álcool Gel
5961                                                                                        PODA DE ARVORE
6068                                                                                    CEI PLENO VIVER IV
6154                                                                                                   NaN
6253                                                MANUTENÇÃO E CONSERVAÇÃO - EMEF ANTONIO ALVES DA SILVA
6324                                                                                    CEI JARDIM IPANEMA
6491   SP/MP CONTRATAÇÃO DE EMPRESA ESPECIALIZADA NA LOCAÇÃO DE CAMINHÕES TOCO E VUC PARA A DIRETORIA R...
6527   REG.DE PREÇOS 008/SMG-COBES/2016 - FORNEC.DE CAFÉ TORRADO E MOÍDO EM EMB.ALTO VÁCUO - GOURMET À ...
6684                                                                      CONTRATAÇÃO DE AGENTE RECREATIVO
7136                                                                      AQUISIÇÃO DE PRODUTOS DE LIMPEZA
7179                                                                           Aquisição de água sanitária
7931                                                                        Aquisição de detergente em pó.
8350                                    Aquisição de material para higiene infantil (fraldas descartáveis)
8450    REPASSES DO RECURSO PARA A APM DE ACORDO  COM A LEI FEDERAL 9394/96, LEI MUNICIPAL 13991/05, DE...
8772                                                            AQUISIÇÃO DE CREME OU GEL DENTAL INFANTIL 
9741          Aquisição de 140.000 Kg de Achocolatado em Pó - ATA DE RP Nº 016/SME/CODAE/2017 - FNDE/PNAE.
...                                                                                                    ...
50119                          CONTRATAÇÃO DE COORDENADORES DE POLO PARA O RECREIO NAS FÉRIAS JANEIRO 2017
50128                      Contratação de Agentes de Recreação, Oficineiros e Coordenador Recreio Jan 2017
50138                                 SERVIÇO DE PODA E REMOÇÃO DE ARVORES POR EQUIPE PARA JANEIRO DE 2017
50147                                   Contratação de Agente de Recreação - Recreio nas Férias - Jan/2017
52087    Aquisição de lençol descartável , em rolo 50cm x 50 m, para uso nos Centros de Educação Infantil 
52151                                                                                          sabão em pó
52260                  

## 3.2. Vigilância

#### Como filtrar?

In [592]:
vigilancia_filter = (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('vigilância', case=False))
    |
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('vigilancia', case=False))
)
vigilancia = (empenhos_df[vigilancia_filter])
empenhos_df.loc[vigilancia_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[vigilancia_filter, 'cat_2'] = 'vigilancia'
groupSum(vigilancia)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação         215.862453    181.857045   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação    198.770123

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes            215.862453    181.857045    198.770123

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica         214.285475   
Locação de Mão-de-Obra                                  1.576978   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica    180.449088    197.344181  
Locação de Mão-de-Obra                             1.407958      1.425941

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                215.862453    181.857045    198.770123

valTotalEmpenhado  valLiquidado  \
txtDescricaoItemDespesa                                                    
Guarda, Vigilância e Segurança em Geral         214.285475    180.449088   
Vigilância Ostensiva                              1.576978      1.407958   

                                         valPagoTotal  
txtDescricaoItemDespesa                                
Guarda, Vigilância e Segurança em Geral    197.344181  
Vigilância Ostensiva                         1.425941

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Gabinete do Secretário                                         205.742407   
Diretoria Regional de Educação - Freguesia/Brasilândia           2.017294   
Diretoria Regional de Educação - Santo Amaro                     1.377752   
Diretoria Regional de Educação - Campo Limpo                     1.160609   
Diretoria Regional de Educação - Jaçanã/Tremembé                 1.116469   
Diretoria Regional de Educação - São Miguel                      0.973168   
Diretoria Regional de Educação - Ipiranga                        0.837397   
Diretoria Regional de Educação - Pirituba                        0.840800   
Diretoria Regional de Educação - São Mateus                      0.645336   
Diretoria Regional de Educação - Guaianases                      0.460134   
Diretoria Regional de Educação - Butantã                         0.462254   
Diretoria Regional de Educação - Penha                           0.154315   
Departamento de Alimentação Escolar                              0.068020   
Coordenadoria de Alimentação Escolar                             0.006496   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Gabinete do Secretário                                    174.029004   
Diretoria Regional de Educação - Freguesia/Brasilândia      1.182547   
Diretoria Regional de Educação - Santo Amaro                1.125484   
Diretoria Regional de Educação - Campo Limpo                0.992040   
Diretoria Regional de Educação - Jaçanã/Tremembé            0.973041   
Diretoria Regional de Educação - São Miguel                 0.770355   
Diretoria Regional de Educação - Ipiranga                   0.767614   
Diretoria Regional de Educação - Pirituba                   0.572334   
Diretoria Regional de Educação - São Mateus                 0.549133   
Diretoria Regional de Educação - Guaianases                 0.418267   
Diretoria Regional de Educação - Butantã                    0.272224   
Diretoria Regional de Educação - Penha                      0.136983   
Departamento de Alimentação Escolar                         0.068020   
Coordenadoria de Alimentação Escolar                        0.000000   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Gabinete do Secretário                                    190.237918  
Diretoria Regional de Educação - Freguesia/Brasilândia      1.295202  
Diretoria Regional de Educação - Santo Amaro                1.226716  
Diretoria Regional de Educação - Campo Limpo                1.076030  
Diretoria Regional de Educação - Jaçanã/Tremembé            1.062511  
Diretoria Regional de Educação - São Miguel                 0.841957  
Diretoria Regional de Educação - Ipiranga                   0.837397  
Diretoria Regional de Educação - Pirituba                   0.624803  
Diretoria Regional de Educação - São Mateus                 0.588212  
Diretoria Regional de Educação - Guaianases                 0.460134  
Diretoria Regional de Educação - Butantã                    0.296908  
Diretoria Regional de Educação - Penha                      0.154315  
Departamento de Alimentação Escolar                         0.068020  
Coordenadoria de Alimentação Escolar                        0.000000

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes         215.862453    181.857045    198.770123

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas             215.862453    181.857045    198.770123

valTotalEmpenhado  \
txtRazaoSocial                                                                      
ALBATROZ SEGURANÇA E VIGILÂNCIA LTDA                                    27.713410   
G4S VANGUARDA SEGURANCA E VIGILANCIA LTDA                               27.801421   
PLURI SEGURANÇA E VIGILANCIA LTDA                                       24.536613   
SEAL SEGURANCA ALTERNATIVA EIRELI                                       25.595870   
LÓGICA SEGURANÇA E VIGILÂNCIA EIRELI                                    20.400099   
POWER - SEGURANÇA E VIGILANCIA LTDA                                     22.136168   
GOCIL SERVIÇOS DE VIGILÂNCIA E SEGURANÇA LTDA                           15.087489   
SUPORTE SERVIÇOS DE SEGURANÇA LTDA                                      10.040263   
ALSA FORT SEGURANCA LTDA                                                 7.786121   
CENTURION SEGURANÇA E VIGILANCIA LTDA                                    6.999060   
MASTER SECURITY SEGURANÇA PATRIMONIAL LTDA                               5.827682   
ACOFORTE SEGURANCA E VIGILÂNCIA LTDA                                     4.585285   
ESSENCIAL SISTEMA DE SEGURANÇA LTDA                                      4.421415   
SP-INTERSEG SISTEMAS DE SEGURANÇA LTDA.                                  3.207480   
ATENTO SAO PAULO SERVICOS DE SEGURANCA PATRIMONIAL EIRELI                3.571978   
MRS SEGURANCA E VIGILANCIA PATRIMONIAL EIRELI - EPP                      2.436216   
DUNBAR SERVIÇOS DE SEGURANÇA - EIRELI                                    1.790346   
DUBBAI SEGURANÇA E VIGILÂNCIA LTDA                                       0.694331   
ACAPULCO SEGURANCA EIRELI - EPP                                          0.369403   
TREZE LISTAS SEGURANÇA E VIGILÂNCIA LTDA                                 0.462254   
ORPAN - ORGANIZAÇÃO PANAMERICANA DE SEGURANÇA PATRIMONIAL LTDA           0.186906   
JUMPER SEGURANCA E VIGILANCIA PATRIMONIAL EIRELI - EPP                   0.034664   
MHPX SEGURANÇA E VIGILÂNCIA EIRELI - EPP                                 0.001702   
LIMPADORA CALIFORNIA LTDA                                                0.176279   

                                                                valLiquidado  \
txtRazaoSocial                                                                 
ALBATROZ SEGURANÇA E VIGILÂNCIA LTDA                               24.890311   
G4S VANGUARDA SEGURANCA E VIGILANCIA LTDA                          24.259330   
PLURI SEGURANÇA E VIGILANCIA LTDA                                  22.139465   
SEAL SEGURANCA ALTERNATIVA EIRELI                                  18.863292   
LÓGICA SEGURANÇA E VIGILÂNCIA EIRELI                               18.448181   
POWER - SEGURANÇA E VIGILANCIA LTDA                                14.820399   
GOCIL SERVIÇOS DE VIGILÂNCIA E SEGURANÇA LTDA                      13.067197   
SUPORTE SERVIÇOS DE SEGURANÇA LTDA                                  9.180736   
ALSA FORT SEGURANCA LTDA                                            6.402367   
CENTURION SEGURANÇA E VIGILANCIA LTDA                               5.621514   
MASTER SECURITY SEGURANÇA PATRIMONIAL LTDA                          5.332567   
ACOFORTE SEGURANCA E VIGILÂNCIA LTDA                                4.161541   
ESSENCIAL SISTEMA DE SEGURANÇA LTDA                                 4.043878   
SP-INTERSEG SISTEMAS DE SEGURANÇA LTDA.                             3.134473   
ATENTO SAO PAULO SERVICOS DE SEGURANCA PATRIMONIAL EIRELI           2.494368   
MRS SEGURANCA E VIGILANCIA PATRIMONIAL EIRELI - EPP                 2.180223   
DUNBAR SERVIÇOS DE SEGURANÇA - EIRELI                               1.422238   
DUBBAI SEGURANÇA E VIGILÂNCIA LTDA                                  0.602993   
ACAPULCO SEGURANCA EIRELI - EPP                                     0.337860   
TREZE LISTAS SEGURANÇA E VIGILÂNCIA LTDA                            0.272224   
ORPAN - ORGANIZAÇÃO PANAMERICANA DE SEGURANÇA PATRIMONIAL LTDA      0.163878   
JUMPER SEGURA

txtObjetoContrato
373                                                                                                    NaN
1374   PREGÃO ELETRÔNICO  12/2017 - CONTRATAÇÃO DE EMPRESA PARA PRESTAÇ~]AO DE SERVIÇOS DE SEGURANÇA E ...
2231                                             AQUISIÇÃO DE COLCHONETE - RECREIO NAS FÉRIAS - JULHO/2017
9924   Contratação de Agentes Recreativo para Recreio nas Férias - Edição Julho/2017 - Período de 10/07...
22026  PROGRAMA RECREIO NAS FÉRIAS - JANEIRO/2017 - DE ACORDO COM O EDITAL DE CREDENCIAMENTO Nº 004/201...
31464                                                      Serviços de vigilância CEUs - lotes 03, 06 e 07
31467                                                  Serviços de vigilância CEUs - lotes 01, 02, 04 e 05
32100  SP/MP CONTRATAÇÃO DE SERVIÇOS DE SEGURANÇA E VIGILÂNCIA DESARMADA PARA A DRE-MP SENDO 5 POSTOS D...
33895                                       Contratação de empresa para serviços de segurança para eventos
35498                              LOCAÇÃO DE EMPRESA PARA PRESTAÇÃO DE SERVIÇO DE MINUTAGEM - PABX - DRE 
49534  CONTRATAÇÃ ODE EMPRESA ESPECIALIZADA NA PRESTAÇÃ ODE SERVIÇO DE VIGILANCIA E SEGURANÇA PATRIMONI...
51157         CONTRATAÇÃO DE EMPRESA ESPECIALIZADA EM VIGILANCIA DESARMADA PARA ATENDIMENTO DA SEDE DA DRE
58579                               Contratação de Empresa para Serviços de Manutenção na EMEF Dom Pedro I

## 3.4 Água, esgoto, energia, telefonia

In [593]:
agua_filter = (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('água e esgoto', case=False))
    |
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('água e sistema de esgoto', case=False))
)
agua = (empenhos_df[agua_filter])
empenhos_df.loc[agua_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[agua_filter, 'cat_2'] = 'agua_esgoto'
groupSum(agua)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação         126.319533     93.020801   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação    107.440314

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes            126.319533     93.020801    107.440314

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica         126.318075   
Despesas de Exercícios Anteriores                       0.001458   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica     93.019344    107.438856  
Despesas de Exercícios Anteriores                  0.001458      0.001458

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                126.319533     93.020801    107.440314

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                              
Água e Esgoto                                                           126.312290   
Serviços de Abastecimento de Água e Sistema de Esgoto Sanitário           0.001458   
Reembolso de Água e Esgoto                                                0.005785   

                                                                 valLiquidado  \
txtDescricaoItemDespesa                                                         
Água e Esgoto                                                       93.019344   
Serviços de Abastecimento de Água e Sistema de Esgoto Sanitário      0.001458   
Reembolso de Água e Esgoto                                           0.000000   

                                                                 valPagoTotal  
txtDescricaoItemDespesa                                                        
Água e Esgoto                                                      107.438856  
Serviços de Abastecimento de Água e Sistema de Esgoto Sanitário      0.001458  
Reembolso de Água e Esgoto                                           0.000000

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Diretoria Regional de Educação - Campo Limpo                    19.281355   
Diretoria Regional de Educação - Pirituba                       11.278434   
Diretoria Regional de Educação - São Mateus                     11.432222   
Diretoria Regional de Educação - São Miguel                     10.062024   
Diretoria Regional de Educação - Santo Amaro                     8.827468   
Diretoria Regional de Educação - Ipiranga                       10.065321   
Diretoria Regional de Educação - Penha                           7.175886   
Diretoria Regional de Educação - Itaquera                        7.324075   
Diretoria Regional de Educação - Guaianases                      7.473731   
Diretoria Regional de Educação  Capela do Socorro               10.397564   
Diretoria Regional de Educação - Freguesia/Brasilândia           6.256722   
Diretoria Regional de Educação - Jaçanã/Tremembé                 5.253938   
Diretoria Regional de Educação - Butantã                         4.904792   
Diretoria Regional de Educação - Capela do Socorro               5.266000   
Gabinete do Secretário                                           1.320000   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Diretoria Regional de Educação - Campo Limpo               15.431377   
Diretoria Regional de Educação - Pirituba                   8.917984   
Diretoria Regional de Educação - São Mateus                 8.053293   
Diretoria Regional de Educação - São Miguel                 7.446496   
Diretoria Regional de Educação - Santo Amaro                6.516152   
Diretoria Regional de Educação - Ipiranga                   6.769633   
Diretoria Regional de Educação - Penha                      6.907916   
Diretoria Regional de Educação - Itaquera                   5.698005   
Diretoria Regional de Educação - Guaianases                 6.136073   
Diretoria Regional de Educação  Capela do Socorro           4.478638   
Diretoria Regional de Educação - Freguesia/Brasilândia      5.070365   
Diretoria Regional de Educação - Jaçanã/Tremembé            4.305776   
Diretoria Regional de Educação - Butantã                    3.581170   
Diretoria Regional de Educação - Capela do Socorro          3.467561   
Gabinete do Secretário                                      0.240363   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Diretoria Regional de Educação - Campo Limpo               17.479769  
Diretoria Regional de Educação - Pirituba                  10.582603  
Diretoria Regional de Educação - São Mateus                 9.369091  
Diretoria Regional de Educação - São Miguel                 8.882587  
Diretoria Regional de Educação - Santo Amaro                7.834975  
Diretoria Regional de Educação - Ipiranga                   7.740754  
Diretoria Regional de Educação - Penha                      7.106903  
Diretoria Regional de Educação - Itaquera                   6.787394  
Diretoria Regional de Educação - Guaianases                 6.635490  
Diretoria Regional de Educação  Capela do Socorro           6.230931  
Diretoria Regional de Educação - Freguesia/Brasilândia      5.601966  
Diretoria Regional de Educação - Jaçanã/Tremembé            5.137638  
Diretoria Regional de Educação - Butantã                    4.281992  
Diretoria Regional de Educação - Capela do Socorro          3.467561  
Gabinete do Secretário                                      0.300660

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes         126.319533     93.020801    107.440314

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas             126.319533     93.020801    107.440314

valTotalEmpenhado  \
txtRazaoSocial                                                                
CIA DE SANEAMENTO BÁSICO DO ESTADO DE SÃO PAULO SABESP           123.805741   
ELETROPAULO METROPOLITANA ELETRICIDADE DE SÃO PAULO S.A.           2.496292   
TELEFÔNICA BRASIL S.A.                                             0.017500   

                                                          valLiquidado  \
txtRazaoSocial                                                           
CIA DE SANEAMENTO BÁSICO DO ESTADO DE SÃO PAULO SABESP       93.020801   
ELETROPAULO METROPOLITANA ELETRICIDADE DE SÃO PAULO S.A.      0.000000   
TELEFÔNICA BRASIL S.A.                                        0.000000   

                                                          valPagoTotal  
txtRazaoSocial                                                          
CIA DE SANEAMENTO BÁSICO DO ESTADO DE SÃO PAULO SABESP      107.440314  
ELETROPAULO METROPOLITANA ELETRICIDADE DE SÃO PAULO S.A.      0.000000  
TELEFÔNICA BRASIL S.A.                                        0.000000

txtObjetoContrato
54                CONSUMO DE ÁGUA E SERVIÇO  DE ÁGUA E ESGOSTO-EMEF,EMEI.CEI,CIEJA,DRESA,EMEFM,CEU E EMEBS
115                                   CONSUMO DE ÁGUA E SERVIÇO DE ÁGUA E ESGOTO-EMEI-EMEF-CEI CIEJA-EMEBS
353                                                  CONSUMO DE ÁGUA E SERVIÇO DE ÁGUA E ESGOTO--EMEF EME.
446                                                                                                    NaN
609                                                                    CONSUMO DE ÁGUA E ESGOTO UES E CEUS
735                                                         CONSUMO DE ÁGUA E SERVIÇO DE ÁGUA E ESGOTO-CEU
783                                             PAGAMENTO CONCESSIONARIA SABESP - 2017 -UNIDADES ESCOLARES
845                            PAGAMENTO CONCESSIONARIA TELEFONICA VIVO 2017- UNIDADES ESCOLARES DRE E CEU
861                                          CONSUMO DE ÁGUA - SABESP - CEI, EMEI, EMEF, CIEJA, ADM E CEU.
1160                                                                     PAGTO. DE CONCESSIONÁRIA - SABESP
1256   SP/SR CONTRATAÇÃO DE SERVIÇOS DE AGUA E ESGOSTO REFERENTE O EXERCÍCIO DE 2017 PARA A UNIDADES DR...
1286               Consumode água e esgoto da DRE Pirituba e das Unidades Educacionais a ela subordinadas.
1371                                        PAGAMENTO DE SERVIÇO DE FORNECIMENTO DE ÁGUA E ESGOTO - SABESP
4357                                                           PAGAMENTO CONCESSIONÁRIA SABESP 2017 - CEUs
4543                                             PAGAMENTO CONCESSIONÁRIA SABESP 2017 - UNIDADES ESCOLARES
4696                                                                            CONCESSIONÁRIA SABESP 2017
6320                                          CONTRATAÇÃO DE EMPRESA PARA SERVIÇO DE AGUA E ESGOTO - 2017 
9336                                 CONSUMO DE ÁGUA E SERVIÇO DE ÁGUA E ESGOTO-UNIDADES ESCOLARES E DRESA
9378                                                  CONSUMO E TARIFAS DE TELEFONIA FIXA- APOIO AO ENSINO
9406                                                           CONSUMO E TARIFAS DE TELEFONIA FIXA - CEUS 
9411                                                             CONSUMO E TARIFAS DE TELEFONIA FIXA - DRE
11034                                                                       CONSUMO DE AGUA DRE E SUAS UES
11495         Contratação de empresa para serviços de água e esgoto - Complementar a Contratação 1189/2017
11571              FORNECIMENTO DE AGUA E ESGOSTO PARA AS UNIDADES DE CEI´s MES DE OUTUBRO A DEZEMBRO 2017
11624                CONSUMO DE ÁGUA E SERVIÇO DE ÁGUA E ESGOTO-EMEF,EME,CEI,CEU,EMEFM,EMEBS,CIEJA E DRESA
12135  SP/SR FORNECIMENTO DE SERVIÇOS DE AGUA E ESGOSTO PARA O CEU PQ SÃO CARLOS, CEU PQ VEREDAS, CEU T...
15252                              SP/SR FORNECIMENTO DE SERVIÇOS DE AGUA E ESGOSTO PARA O CEU'S DA DRE/MP
30417                                                                    CONSUMO E TARIFA DE ÁGUA E ESGOTO
35291                                                               PAGTO. DE CONCESSIONÁRIA - ELETROPAULO
40446                                                                      CONSUMO CONCESSIONÁRIA - SABESP
40489                            SP/SR SERVIÇOS DE FORNECIMENTO DE AGUA E ESGOTO PARA AS UNIDADES DE EMEIS
42271                                   CONTRATAÇÃO DE AGENTE DE RECREAÇÃO - RECREIO NAS FÉRIAS - JAN.2017
42531  PAGAMENTO DE DESPESAS DE EXERCÍCIOS ANTERIORES - SET/2012 - SERVIÇOS DE CONSUMO DE ÁGUA - CIA DE...
49508             Consumo de energia elétrica da DRE Pirituba e das Unidades Escolares a ela subordinadas.
57256  PROGRAMA RECREIO NAS FÉRIAS - JANEIRO/2017 - DE ACORDO COM O EDITAL DE CREDENCIAMENTO Nº 004/201...
59184                                                           SERVIÇOS DE ENERGIA ELETRICA - ELETROPAULO
59688             Pagamento dos serviços de fornecimento de água e esgoto para as Unidades Centrais da SME

In [594]:
eletricidade_filter = (empenhos_df['txtRazaoSocial'].str.contains('eletropaulo', case=False))
eletricidade = (empenhos_df[eletricidade_filter])
empenhos_df.loc[eletricidade_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[eletricidade_filter, 'cat_2'] = 'eletricidade'
groupSum(eletricidade)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          66.003813     44.973127   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação      50.88234

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             66.003813     44.973127      50.88234

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica          66.003813   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica     44.973127      50.88234

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 66.003813     44.973127      50.88234

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                      
Energia Elétrica de Prédios Públicos                             63.432221   
Serviços de Instalação de Rede de Energia                         0.040100   
Desmontagem, Remoção e Montagem de Equipamentos e Afins           0.001164   
Gás Canalizado                                                    0.034000   
Reembolso de Energia Elétrica                                     0.000035   
Água e Esgoto                                                     2.496292   

                                                         valLiquidado  \
txtDescricaoItemDespesa                                                 
Energia Elétrica de Prédios Públicos                        44.935585   
Serviços de Instalação de Rede de Energia                    0.037542   
Desmontagem, Remoção e Montagem de Equipamentos e Afins      0.000000   
Gás Canalizado                                               0.000000   
Reembolso de Energia Elétrica                                0.000000   
Água e Esgoto                                                0.000000   

                                                         valPagoTotal  
txtDescricaoItemDespesa                                                
Energia Elétrica de Prédios Públicos                        50.844798  
Serviços de Instalação de Rede de Energia                    0.037542  
Desmontagem, Remoção e Montagem de Equipamentos e Afins      0.000000  
Gás Canalizado                                               0.000000  
Reembolso de Energia Elétrica                                0.000000  
Água e Esgoto                                                0.000000

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Diretoria Regional de Educação - Campo Limpo                     7.175809   
Diretoria Regional de Educação - São Miguel                      7.582278   
Diretoria Regional de Educação - Pirituba                        5.568449   
Diretoria Regional de Educação - São Mateus                      7.733360   
Diretoria Regional de Educação - Guaianases                      4.292843   
Diretoria Regional de Educação - Itaquera                        4.202624   
Diretoria Regional de Educação - Penha                           4.352793   
Diretoria Regional de Educação - Ipiranga                        3.446775   
Diretoria Regional de Educação - Jaçanã/Tremembé                 3.165392   
Diretoria Regional de Educação - Freguesia/Brasilândia           3.675465   
Diretoria Regional de Educação - Santo Amaro                     4.406237   
Diretoria Regional de Educação - Butantã                         2.616579   
Diretoria Regional de Educação  Capela do Socorro                3.631647   
Diretoria Regional de Educação - Capela do Socorro               2.937000   
Gabinete do Secretário                                           1.216561   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Diretoria Regional de Educação - Campo Limpo                6.192868   
Diretoria Regional de Educação - São Miguel                 4.555495   
Diretoria Regional de Educação - Pirituba                   4.396149   
Diretoria Regional de Educação - São Mateus                 4.101346   
Diretoria Regional de Educação - Guaianases                 3.463225   
Diretoria Regional de Educação - Itaquera                   3.288448   
Diretoria Regional de Educação - Penha                      3.090721   
Diretoria Regional de Educação - Ipiranga                   2.829503   
Diretoria Regional de Educação - Jaçanã/Tremembé            2.525720   
Diretoria Regional de Educação - Freguesia/Brasilândia      2.675959   
Diretoria Regional de Educação - Santo Amaro                2.338368   
Diretoria Regional de Educação - Butantã                    2.019938   
Diretoria Regional de Educação  Capela do Socorro           1.822582   
Diretoria Regional de Educação - Capela do Socorro          1.105644   
Gabinete do Secretário                                      0.567160   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Diretoria Regional de Educação - Campo Limpo                6.818542  
Diretoria Regional de Educação - São Miguel                 4.995474  
Diretoria Regional de Educação - Pirituba                   4.931503  
Diretoria Regional de Educação - São Mateus                 4.846382  
Diretoria Regional de Educação - Guaianases                 3.887183  
Diretoria Regional de Educação - Itaquera                   3.843624  
Diretoria Regional de Educação - Penha                      3.397688  
Diretoria Regional de Educação - Ipiranga                   3.132679  
Diretoria Regional de Educação - Jaçanã/Tremembé            2.960374  
Diretoria Regional de Educação - Freguesia/Brasilândia      2.952791  
Diretoria Regional de Educação - Santo Amaro                2.778277  
Diretoria Regional de Educação - Butantã                    2.399838  
Diretoria Regional de Educação  Capela do Socorro           2.149688  
Diretoria Regional de Educação - Capela do Socorro          1.105644  
Gabinete do Secretário                                      0.682652

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          66.003813     44.973127      50.88234

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              66.003813     44.973127      50.88234

valTotalEmpenhado  \
txtRazaoSocial                                                                
ELETROPAULO METROPOLITANA ELETRICIDADE DE SÃO PAULO S.A.          66.003813   

                                                          valLiquidado  \
txtRazaoSocial                                                           
ELETROPAULO METROPOLITANA ELETRICIDADE DE SÃO PAULO S.A.     44.973127   

                                                          valPagoTotal  
txtRazaoSocial                                                          
ELETROPAULO METROPOLITANA ELETRICIDADE DE SÃO PAULO S.A.      50.88234

txtObjetoContrato
45                                 CONSUMO DE ENERGIA ELÉTRICA-EMEF,EMEI,CEI,EMEBS,EMEFM,CIEJA,DRESA E CEU
283    SP/SR SERVIÇOS DE FORNECIMENTO DE ENERGIA ELETRICA REFERENTE AO EXERCÍCIO DE 2017 PARA A UNIDADE...
741                                                               CONSUMO DE ENERGIA ELETRICA - UES E CEUS
1161                                                                           CONSUMO DE ENERGIA ELETRICA
1697                                      PAGAMENTO DE CONCESSIONÁRIA ELETROPAULO 2017 UNIDADES ESCOLARES 
3424                                                                                                   NaN
5608                                                            SERVIÇOS DE ENERGIA ELETRICA - ELETROPAULO
6088                                   CONTRATAÇÃO DE EMPRESA PARA FORNECIMENTO DE ENERGIA ELÉTRICA - 2017
6784                                                                   CONCESSIONÁRIA AES ELETROPAULO 2017
9873                                                 CONSUMO DE ENRGIA ELÉTRICA-UNIDADES ESCOLARES E DRESA
9959                                                                PAGTO. DE CONCESSIONÁRIA - ELETROPAULO
11299                                                        CONSUMO E TARIFAS DE ENERGIA ELÉTRICA - CEUS 
11505             Consumo de energia elétrica da DRE Pirituba e das Unidades Escolares a ela subordinadas.
11631                                              CONSUMO E TARIFAS DE ENERGIA ELÉTRICA - APOIO AO ENSINO
13421  PROGRAMA RECREIO NAS FÉRIAS - JANEIRO/2017 - DE ACORDO COM O EDITAL DE CREDENCIAMENTO Nº 004/201...
15241  SP/SR SERVIÇOS DE FORNECIMENTO DE ENERGIA ELETRICA REFERENTE AO EXERCÍCIO DE 2017 PARA OS CEU'S ...
16087  INEXIGIBILIDADE_ SERVIÇO DE AUMENTO DE DEMANDA DE CARGA DE ENERGIA ELETRICA PARA ATENDIMENTO DO ...
21528                                                           CONSUMO E TARIFAS DE ENERGIA ELÉTRICA -DRE
35113                             Consumo  de Energia Elétrica: EMEF-EMEI-CEI-CEU-DRESA-EMEFM-EMEBS-CIEJA 
35782                                        SERVIÇO DE FORNECIMENTO DE ENERGIA ELÉTRICA - AES ELETROPAULO
43627           PAGTO  DE DESLIGAMENTO PROGRAMADO PARA CONSTRUÇÃO DE OBRA - EMEF MARIA BERENICE DOS SANTOS
59777          Pagamento dos serviços de fornecimento de energia elétrica para as Unidades Centrais da SME

In [595]:
telefone_filter = (empenhos_df['txtDescricaoItemDespesa'].str.contains('telefonia', case=False))
telefone = (empenhos_df[telefone_filter])
empenhos_df.loc[telefone_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[telefone_filter, 'cat_2'] = 'telefone'
groupSum(telefone)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          25.054313     16.570464   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     19.735539

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             25.054313     16.570464     19.735539

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica          25.054313   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica     16.570464     19.735539

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 25.054313     16.570464     19.735539

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                                     
Serviço de Instalação, Ampliação de Sist. de Telefonia/Teleinformática          15.433389   
Telefonia Fixa                                                                   9.162018   
Telefonia Móvel                                                                  0.458906   

                                                                        valLiquidado  \
txtDescricaoItemDespesa                                                                
Serviço de Instalação, Ampliação de Sist. de Telefonia/Teleinformática     11.321042   
Telefonia Fixa                                                              5.216719   
Telefonia Móvel                                                             0.032704   

                                                                        valPagoTotal  
txtDescricaoItemDespesa                                                               
Serviço de Instalação, Ampliação de Sist. de Telefonia/Teleinformática     13.575405  
Telefonia Fixa                                                              6.124723  
Telefonia Móvel                                                             0.035411

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Gabinete do Secretário                                          15.705322   
Diretoria Regional de Educação - Campo Limpo                     1.098561   
Diretoria Regional de Educação - Jaçanã/Tremembé                 0.727494   
Diretoria Regional de Educação - Guaianases                      0.814640   
Diretoria Regional de Educação - Pirituba                        0.616080   
Diretoria Regional de Educação - São Miguel                      0.769980   
Diretoria Regional de Educação - São Mateus                      0.579139   
Diretoria Regional de Educação - Ipiranga                        0.664515   
Diretoria Regional de Educação - Penha                           0.596295   
Diretoria Regional de Educação - Freguesia/Brasilândia           0.714442   
Diretoria Regional de Educação - Santo Amaro                     0.427466   
Diretoria Regional de Educação - Itaquera                        0.466877   
Diretoria Regional de Educação - Butantã                         0.547308   
Diretoria Regional de Educação - Capela do Socorro               1.012485   
Diretoria Regional de Educação  Capela do Socorro                0.277657   
Departamento de Alimentação Escolar                              0.036052   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Gabinete do Secretário                                     11.287676   
Diretoria Regional de Educação - Campo Limpo                0.685051   
Diretoria Regional de Educação - Jaçanã/Tremembé            0.516987   
Diretoria Regional de Educação - Guaianases                 0.510620   
Diretoria Regional de Educação - Pirituba                   0.466939   
Diretoria Regional de Educação - São Miguel                 0.493618   
Diretoria Regional de Educação - São Mateus                 0.449281   
Diretoria Regional de Educação - Ipiranga                   0.455821   
Diretoria Regional de Educação - Penha                      0.425594   
Diretoria Regional de Educação - Freguesia/Brasilândia      0.342742   
Diretoria Regional de Educação - Santo Amaro                0.343078   
Diretoria Regional de Educação - Itaquera                   0.104609   
Diretoria Regional de Educação - Butantã                    0.308918   
Diretoria Regional de Educação - Capela do Socorro          0.168910   
Diretoria Regional de Educação  Capela do Socorro           0.010620   
Departamento de Alimentação Escolar                         0.000000   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Gabinete do Secretário                                     13.614811  
Diretoria Regional de Educação - Campo Limpo                0.772048  
Diretoria Regional de Educação - Jaçanã/Tremembé            0.575609  
Diretoria Regional de Educação - Guaianases                 0.554707  
Diretoria Regional de Educação - Pirituba                   0.542085  
Diretoria Regional de Educação - São Miguel                 0.526179  
Diretoria Regional de Educação - São Mateus                 0.519887  
Diretoria Regional de Educação - Ipiranga                   0.505451  
Diretoria Regional de Educação - Penha                      0.470553  
Diretoria Regional de Educação - Freguesia/Brasilândia      0.371682  
Diretoria Regional de Educação - Santo Amaro                0.359156  
Diretoria Regional de Educação - Itaquera                   0.356032  
Diretoria Regional de Educação - Butantã                    0.353483  
Diretoria Regional de Educação - Capela do Socorro          0.171792  
Diretoria Regional de Educação  Capela do Socorro           0.036286  
Departamento de Alimentação Escolar                         0.005777

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          25.054313     16.570464     19.735539

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              25.054313     16.570464     19.735539

valTotalEmpenhado  valLiquidado  \
txtRazaoSocial                                                         
PRIMESYS SOLUÇÕES EMPRESARIAIS S.A.          14.698120     10.708426   
TELEFÔNICA BRASIL S.A.                        9.974875      5.550734   
NEC LATIN AMERICA S.A.                        0.377138      0.310331   
CLARO S.A.                                    0.004180      0.000973   

                                     valPagoTotal  
txtRazaoSocial                                     
PRIMESYS SOLUÇÕES EMPRESARIAIS S.A.     12.848554  
TELEFÔNICA BRASIL S.A.                   6.552776  
NEC LATIN AMERICA S.A.                   0.333172  
CLARO S.A.                               0.001037

txtObjetoContrato
332    SP/SR CONTRATAÇÃO DE SERVIÇOS DE TELEFONIA FIXA REFERENTE AO EXERCÍCIO DE 2017 PARA AS UNIDADES ...
385                                                                                                    NaN
392                                                                   SERVIÇO DE TELEFONIA FIXA-CEI.E EMEI
579                                                                   CONSUMO DE TELEFONIA FIXA DAS U.E.s.
706                                                  CONSUMO E TARIFAS DE TELEFONIA FIXA - APOIO AO ENSINO
854                            PAGAMENTO CONCESSIONARIA TELEFONICA VIVO 2017- UNIDADES ESCOLARES DRE E CEU
4466                                                                   concessionaria telefonica dre e ues
4694   SP/SR CONTRATAÇÃO DE SERVIÇOS DE TELEFONIA FIXA REFERENTE AO EXERCÍCIO DE 2017 PARAAS UNIDADES D...
5061                                                                     SERVIÇOS DE TELEFONIA-TELEFONICA 
5797                                  SERVIÇO DE TELEFONIA FIXA-EMEI,EMEF,CEI, DRESA,EMEBS,EMEFM,CIEJA,CEU
5929                                                   SERVIÇO DE TELEFONIA FIXA-EMEF,EMEI,CEI,EMEBS,CIEJA
6551                                                                                 SERVIÇOS DE TELEFONIA
6738                                                              CONTRATAÇÃO DE SERVICOS TELEFONIA - 2017
9022                                                                        SERVIÇO DE TELEFONIA FIXA-EMEF
9791          Repasse de Recursos do PNAE para o CEI Comunidade Infantil Aglaezinha IV- CÓD. INEP 35381007
11342                            Consumo de telefonia fixa das Unidades Escolares da DRE Pirituba/Jaraguá.
11530                          2º REPASSE PTRF/2017 - CUSTEIO - DRE G - CEI LUCIANO MENDES DE ALMEIDA, DOM
11771                                                                      CONSUMO DE TELEFONIA FIXA - DRE
12442                          CONTRATAÇÃO DE COORDENADORES DE POLO PARA O RECREIO NAS FÉRIAS JANEIRO 2017
15205                                            CONTRATAÇÃO DE AGENTES PARA RECREIO NAS FÉRIAS JUNHO/2017
15403                                              CONTRATAÇÃO DE EMPRESA ESPECIALIZADA EM LOCAÇÃO DE PABX
23734                                                                   LOCAÇÃO DE EQUIPAMENTO - PABX  DRE
23736                                                                 LOCAÇÃO DE EQUIPAMENTO - PABX -CEUS 
24790                                               CONSUMO E TARIFAS DE TELEFONIA FIXA- CLARO / EMBRATEL 
28022                                                                                   MANUTENÇÃO PREDIAL
31290                                                                           Aquisição de Luva de vivil
32767                                                PAGAMENTO CONCESSIONÁRIA TELEFÔNICA/VIVO- 2017 -  DRE
32771                                                 PAGAMENTO CONCESSIONÁRIA TELEFÔNICA/VIVO- 2017 - CEU
37894    CONTRATAÇÃO DE SERVIÇO DE TELEFONIA FIXA POR COMUTADO POR ADESÃO A ATA 14/ SEMPLA/ COBES- DRE-BT 
41199                                 SERVIÇO DE FORNECIMENTO DE TELECOMUNICAÇÕES - TELEFONICA BRASIL S.A.
49177                                                                PAGTO. DE CONCESSIONÁRIA - TELEFÔNICA
49303                                                          MANUTENÇÃO E CONSERVAÇÃO - CEU PARAISÓPOLIS
49584                                                                  SERVIÇO DE TELEFONI A FIXO COMUTADO
49944                                                                           AQUISIÇÃO DE ÓLEO DE SOJA 
51211                                     CONTRATAÇÃO DE EMPRESA P/PRESTAÇÃO DE SERVIÇO DE MINUTAGEM - DRE
51212                                   CONTRATAÇÃO DE EMPRESA P/PRESTAÇÃO DE SERVIÇO DE MINUTAGEM - CEUS 
56043                                                     LOCAÇÃO DE EQUIPAMENTOS - PABX - DRE CAMPO LIMPO
56052                  

## 3.5 Mobiliário

In [596]:
mobiliario_filter = (empenhos_df['txtDescricaoSubElemento'].str.contains('Mobiliário', case=False))
mobiliario = (empenhos_df[mobiliario_filter])
empenhos_df.loc[mobiliario_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[mobiliario_filter, 'cat_2'] = 'mobiliario'
groupSum(mobiliario)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          10.793645      0.011702   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação      7.332216

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas de Capital            10.793645      0.011702      7.332216

valTotalEmpenhado  valLiquidado  \
txtDescricaoElemento                                                  
Equipamentos e Material Permanente          10.793645      0.011702   

                                    valPagoTotal  
txtDescricaoElemento                              
Equipamentos e Material Permanente      7.332216

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 10.793645      0.011702      7.332216

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoItemDespesa                                                       
Padronizados                              4.795223      0.000000      4.160380
Carteiras e Cadeiras Escolares            5.986720      0.000000      3.160134
Outros Móveis em Geral                    0.007947      0.007947      0.007947
Não Padronizados                          0.003755      0.003755      0.003755

...

valTotalEmpenhado  valLiquidado  \
txtDescricaoUnidade                                                            
Gabinete do Secretário                               10.781943      0.000000   
Diretoria Regional de Educação - Guaianases           0.007947      0.007947   
Diretoria Regional de Educação - Butantã              0.003755      0.003755   

                                             valPagoTotal  
txtDescricaoUnidade                                        
Gabinete do Secretário                           7.320514  
Diretoria Regional de Educação - Guaianases      0.007947  
Diretoria Regional de Educação - Butantã         0.003755

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                               
Investimentos            10.793645      0.011702      7.332216

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              10.793645      0.011702      7.332216

valTotalEmpenhado  \
txtRazaoSocial                                                               
ERGO MOBILI IND. E COM.  DE MOVEIS LTDA                           2.245002   
SANTOS & MATINATA MOVEIS LTDA - EPP                               1.776898   
MAQMÓVEIS INDUSTRIA E COMERCIO DE MÓVEIS LTDA                     4.049882   
FUNDAÇÃO PROF DR MANOEL PEDRO PIMENTEL- FUNAP                     0.533520   
EQUISCOLA EQUIPAMENTOS ESCOLARES LTDA-ME                          0.418824   
ANDRESSA PANINI ALBISSU EPP                                       0.362138   
CANTARES MAGAZINE - EIRELI                                        0.329306   
LUCINEIDE B DOS SANTOS MOVEIS - EPP                               0.894539   
ARTEMOVEIS - SOLUCOES E COMERCIO DE MOVEIS LTDA - ME              0.080364   
C.G. RANDI MOVEIS PARA ESCRITORIO - EPP                           0.062990   
MINIMAQ EQUIPAMENTOS PARA ESCRITORIO LTDA - EPP                   0.028480   
SPEZIA COMERCIAL DE MATERIAIS E SUPRIMENTOS EIRELI - ME           0.004447   
GHAIA COMERCIAL LTDA-EPP                                          0.003755   
INNOVARY FUTURE COMERCIAL LTDA - ME                               0.003500   

                                                         valLiquidado  \
txtRazaoSocial                                                          
ERGO MOBILI IND. E COM.  DE MOVEIS LTDA                      0.000000   
SANTOS & MATINATA MOVEIS LTDA - EPP                          0.000000   
MAQMÓVEIS INDUSTRIA E COMERCIO DE MÓVEIS LTDA                0.000000   
FUNDAÇÃO PROF DR MANOEL PEDRO PIMENTEL- FUNAP                0.000000   
EQUISCOLA EQUIPAMENTOS ESCOLARES LTDA-ME                     0.000000   
ANDRESSA PANINI ALBISSU EPP                                  0.000000   
CANTARES MAGAZINE - EIRELI                                   0.000000   
LUCINEIDE B DOS SANTOS MOVEIS - EPP                          0.000000   
ARTEMOVEIS - SOLUCOES E COMERCIO DE MOVEIS LTDA - ME         0.000000   
C.G. RANDI MOVEIS PARA ESCRITORIO - EPP                      0.000000   
MINIMAQ EQUIPAMENTOS PARA ESCRITORIO LTDA - EPP              0.000000   
SPEZIA COMERCIAL DE MATERIAIS E SUPRIMENTOS EIRELI - ME      0.004447   
GHAIA COMERCIAL LTDA-EPP                                     0.003755   
INNOVARY FUTURE COMERCIAL LTDA - ME                          0.003500   

                                                         valPagoTotal  
txtRazaoSocial                                                         
ERGO MOBILI IND. E COM.  DE MOVEIS LTDA                      2.245002  
SANTOS & MATINATA MOVEIS LTDA - EPP                          1.776898  
MAQMÓVEIS INDUSTRIA E COMERCIO DE MÓVEIS LTDA                1.223296  
FUNDAÇÃO PROF DR MANOEL PEDRO PIMENTEL- FUNAP                0.511784  
EQUISCOLA EQUIPAMENTOS ESCOLARES LTDA-ME                     0.418824  
ANDRESSA PANINI ALBISSU EPP                                  0.362138  
CANTARES MAGAZINE - EIRELI                                   0.329306  
LUCINEIDE B DOS SANTOS MOVEIS - EPP                          0.281432  
ARTEMOVEIS - SOLUCOES E COMERCIO DE MOVEIS LTDA - ME         0.080364  
C.G. RANDI MOVEIS PARA ESCRITORIO - EPP                      0.062990  
MINIMAQ EQUIPAMENTOS PARA ESCRITORIO LTDA - EPP              0.028480  
SPEZIA COMERCIAL DE MATERIAIS E SUPRIMENTOS EIRELI - ME      0.004447  
GHAIA COMERCIAL LTDA-EPP                                     0.003755  
INNOVARY FUTURE COMERCIAL LTDA - ME                          0.003500

txtObjetoContrato
25381                                                         DL - AQUISIÇÃO DE CADEIRÃO PARA ALIMENTAÇÃO 
33311  AUTORIZO a aquisição de 15 Cadeiras para alimentação infantil conforme cotação eletrônica Nº SEI...
40343                                     Aquisição de Mobiliário - Conjunto sala de aula EMEF - tamanho 2
40392                                                                      Aquisição de Mobiliário Escolar
40406                                                                      AQUISIÇÃO DE MOBILIARIO ESCOLAR
40448                                                    Aquisição de Mobiliário - Conjunto para Professor
40565                                     Aquisição Mobiliário Administrativo - Mesa comum para Secretaria
40679                                                               Conjunto sala de aula EMEF - tamanho 2
40694                                                Aquisição de Conjunto Sala de Leitura - Tam. 1 - EMEF
40697                                         Aquisição de Mobiliários para Sala de Aula EMEF - Tamanho II
40774                                             Aquisição de 540 Armários de Madeira de 02 (dois) Corpos
40778                                               Aquisição de Conjunto Sala de Leitura EMEF Tam. I e II
40894             Aquisição de Mobiliário "Sala de Aula EMEF - Tamanho I e Refeitório Escolar - Tamanho I"
40926                                                                              Aquisição de mobiliario
47030                                                              Aquisição de conjunto sala de aula EMEI
47048                                                                       Aquisição de cadeiras diversas
57040                                                                       Aquisição de Lousas escolares

## 3. 5 Manutenção

In [597]:
manutencao_filter = (
    (
        (empenhos_df['txtDescricaoSubElemento'].str.contains('Manut', case=False))
        |
        (empenhos_df['txtDescricaoItemDespesa'].str.contains('Jardinagem', case=False))
        |
        (empenhos_df['txtDescricaoItemDespesa'].str.contains('Outros Serviços Urbanos', case=False))
    )
    &
    ~(empenhos_df['txtDescricaoSubElemento'].str.contains('processamento de dados', case=False))
    &
    ~(empenhos_df['txtDescricaoSubElemento'].str.contains('software', case=False))    
)
manutencao = (empenhos_df[manutencao_filter])
empenhos_df.loc[manutencao_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[manutencao_filter, 'cat_2'] = 'manutencao'
groupSum(manutencao)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          30.577765     21.525497   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     24.463952

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             29.437765     20.956155     23.894610
Despesas de Capital             1.140000      0.569343      0.569343

valTotalEmpenhado  \
txtDescricaoElemento                                                
Outros Serviços de Terceiros -Pessoa Jurídica           29.339279   
Outros Serviços de Terceiros - Pessoa Jurídica           1.140000   
Material de Consumo                                      0.098486   

                                                valLiquidado  valPagoTotal  
txtDescricaoElemento                                                        
Outros Serviços de Terceiros -Pessoa Jurídica      20.901669     23.796124  
Outros Serviços de Terceiros - Pessoa Jurídica      0.569343      0.569343  
Material de Consumo                                 0.054486      0.098486

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 30.577765     21.525497     24.463952

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                                     
Elevadores                                                                       9.009160   
Outras Máquinas e Equipamentos                                                   4.090783   
Pequenas Reformas - Escolas de Ensino Fundamental                                3.019048   
Pequenas Reformas - Escolas de Educação Infantil                                 2.853613   
Jardinagem                                                                       2.610985   
Pequenas Reformas - Centros de Educação Infantil                                 1.656765   
Outros Serviços Urbanos                                                          1.234350   
Pequenas Reformas - Outros Imóveis                                               0.888097   
Equipamentos de Processamento de Dados                                           0.583397   
Manutenção e Reformas de Bens Imóveis                                            1.140000   
Pequenas Reformas - Imóveis Administrativos                                      0.327757   
Manutenção e Conservação de Bens Imóveis                                         0.529771   
Bens Móveis                                                                      0.151358   
Pequenas Reformas - Centros Esportivos e Similares                               0.127258   
Pequenas Reformas - Escolas de Educação Especial                                 2.090407   
Pequenas Reformas - Escolas de Ensino Médio e Supletivo                          0.073361   
Peças e Acessórios para Elevadores, Escadas Rolantes e Esteiras                  0.057770   
Equipamentos Médico-Hospitalares e Laboratoriais                                 0.033579   
Manutenção em Equipamentos de Proteção e Segurança Pessoal                       0.049171   
Diversos Materiais para Manutenção de Bens Imóveis                               0.015373   
Diversos Materiais para Manutenção de Bens Móveis                                0.007955   
Pequenas Reformas - Creches                                                      0.006468   
Aparelhos e Acessórios Sanitários                                                0.006400   
Peças e Acessórios para Aparelhos de Som, Imagem, Iluminação e Comunic           0.006120   
Materiais para Pintura e Acabamento                                              0.004868   
Pequenas Reformas - Móveis                                                       0.003950   

                                                                        valLiquidado  \
txtDescricaoItemDespesa                                                                
Elevadores                                                                  6.225331   
Outras Máquinas e Equipamentos                                              3.732811   
Pequenas Reformas - Escolas de Ensino Fundamental                           2.532999   
Pequenas Reformas - Escolas de Educação Infantil                            2.227234   
Jardinagem                                                                  1.938594   
Pequenas Reformas - Centros de Educação Infantil                            1.274057   
Outros Serviços Urbanos                                                     0.946000   
Pequenas Reformas - Outros Imóveis                                          0.687964   
Equipamentos de Processamento de Dados                                      0.522691   
Manutenção e Reformas de Bens Imóveis                                       0.569343   
Pequenas Reformas - Imóveis Administrativos                                 0.161134   
Manutenção e Conservação de Bens Imóveis                                    0.173759   
Bens Móveis                                                                 0.126757   
Pequenas Reformas - Centros Esportivos e Similares                          0.118845   
Pequenas Reformas - Escolas de Educação Especial           

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Gabinete do Secretário                                           5.926842   
Diretoria Regional de Educação - Penha                           4.302361   
Diretoria Regional de Educação - Campo Limpo                     5.188091   
Diretoria Regional de Educação - São Mateus                      1.941934   
Diretoria Regional de Educação - Pirituba                        2.068438   
Diretoria Regional de Educação - Santo Amaro                     1.938028   
Diretoria Regional de Educação - São Miguel                      1.655400   
Diretoria Regional de Educação - Guaianases                      2.083498   
Diretoria Regional de Educação - Freguesia/Brasilândia           1.374205   
Diretoria Regional de Educação - Butantã                         0.997926   
Diretoria Regional de Educação - Ipiranga                        0.870834   
Diretoria Regional de Educação  Capela do Socorro                0.807039   
Diretoria Regional de Educação - Itaquera                        0.678492   
Diretoria Regional de Educação - Jaçanã/Tremembé                 0.518089   
Diretoria Regional de Educação - Capela do Socorro               0.222857   
Departamento de Alimentação Escolar                              0.003732   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Gabinete do Secretário                                      4.879727   
Diretoria Regional de Educação - Penha                      3.070078   
Diretoria Regional de Educação - Campo Limpo                2.707139   
Diretoria Regional de Educação - São Mateus                 1.321618   
Diretoria Regional de Educação - Pirituba                   1.698392   
Diretoria Regional de Educação - Santo Amaro                1.557613   
Diretoria Regional de Educação - São Miguel                 1.040023   
Diretoria Regional de Educação - Guaianases                 1.084195   
Diretoria Regional de Educação - Freguesia/Brasilândia      0.829390   
Diretoria Regional de Educação - Butantã                    0.816381   
Diretoria Regional de Educação - Ipiranga                   0.772205   
Diretoria Regional de Educação  Capela do Socorro           0.742000   
Diretoria Regional de Educação - Itaquera                   0.441570   
Diretoria Regional de Educação - Jaçanã/Tremembé            0.338576   
Diretoria Regional de Educação - Capela do Socorro          0.222857   
Departamento de Alimentação Escolar                         0.003732   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Gabinete do Secretário                                      5.306571  
Diretoria Regional de Educação - Penha                      3.414653  
Diretoria Regional de Educação - Campo Limpo                2.990838  
Diretoria Regional de Educação - São Mateus                 1.893169  
Diretoria Regional de Educação - Pirituba                   1.842621  
Diretoria Regional de Educação - Santo Amaro                1.677633  
Diretoria Regional de Educação - São Miguel                 1.387665  
Diretoria Regional de Educação - Guaianases                 1.279092  
Diretoria Regional de Educação - Freguesia/Brasilândia      0.895999  
Diretoria Regional de Educação - Butantã                    0.859622  
Diretoria Regional de Educação - Ipiranga                   0.808540  
Diretoria Regional de Educação  Capela do Socorro           0.792172  
Diretoria Regional de Educação - Itaquera                   0.574423  
Diretoria Regional de Educação - Jaçanã/Tremembé            0.514365  
Diretoria Regional de Educação - Capela do Socorro          0.222857  
Departamento de Alimentação Escolar                         0.003732

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          29.437765     20.956155     23.894610
Investimentos                       1.140000      0.569343      0.569343

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              30.577765     21.525497     24.463952

valTotalEmpenhado  \
txtRazaoSocial                                                                                   
ELEVADORES ORION LTDA.                                                                7.629500   
CAMARGO RODRIGUES LTDA                                                                3.039063   
POTENZA ENGENHARIA E CONSTRUÇÃO LTDA                                                  2.461475   
ERA-TECNICA ENGENHARIA CONSTRUÇÕES E SERVIÇOS LTDA                                    1.234350   
ELEPAR ELEVADORES LTDA                                                                1.190297   
L & M COMERCIO E SERVIÇOS DE MANUTENÇÃO  LTDA - EPP                                   0.656720   
ACECO TI S.A.                                                                         0.583397   
CONSTRUTORA PROGREDIOR LTDA                                                           1.140000   
GOLDEN DISTRIBUIDORA LTDA.                                                            0.552979   
EBER QUINTINO GOMES ENGENHARIA - ME                                                   0.471022   
BOSTON SERVICE DO BRASIL LTDA - EPP                                                   0.432209   
KOINSTEC INSTALAÇÕES E PROJETOS LTDA EPP                                              0.421957   
DBL CONSTRUÇÕES EIRELI - EPP                                                          0.413155   
ZAC MANUTENÇÃO E REFORMAS EM GERAL SOCIEDADE EMPRESARIA LTDA EPP                      0.414279   
ENGEBRAS CONSTRUÇÕES E EMPREENDIMENTOS LTDA                                           0.388262   
MAXPOWER MANUTENCAO E REFORMA EIRELI - ME                                             0.340205   
SIM SOLUÇÕES INTEGRADAS EM MÃO DE OBRA E MATERIAIS LTDA - EPP                         0.315186   
D B DA SILVA CONSTRUÇOES  REFORMA E MANUTENÇÃO EIRELI - EPP                           0.297742   
EMPREITEC CONSTRUÇÕES E MANUTENÇÕES LTDA-EPP                                          0.299217   
MAFEN ENGENHARIA E CONSTRUÇÕES LTDA - EPP                                             0.283743   
GHANMA SERVIÇOS E CONSTRUÇÕES EIRELI - EPP                                            0.283167   
PCT ENGENHARIA E CONSTRUÇÕES LTDA                                                     0.269891   
CHEP - RESTAURO SERVICOS E OBRAS EM GERAL LTDA - EPP                                  0.242073   
CEDRO AFS EMPREITEIRA DE OBRAS EIRELI - ME                                            0.204556   
JHONATHAN SILVA SANTOS EIRELI - ME                                                    0.202646   
MARCA CONSTRUCOES E EMPREENDIMENTOS LTDA                                              0.170992   
BRUNO MONTENEGRO RIBEIRO - ME                                                         0.156554   
AFA COMERCIO E PRESTADORA DE SERVIÇO LTDA - ME                                        0.155616   
AKATIJU COMERCIAL E PRESTADORA DE SERVIÇOS LTDA-EPP                                   0.157668   
ELEVADORES SÃO PAULO LTDA - EPP                                                       0.257026   
...                                                                                        ...   
A. MIMURA COMERCIAL E SERVIÇOS  LTDA ME                                               0.007930   
SPEZIA COMERCIAL DE MATERIAIS E SUPRIMENTOS EIRELI - ME                               0.007890   
COOPERATIVA BRASILEIRA DE TRANSPORTE COBRATE                                          0.007475   
ESGOTECNICA COMERCIO E SERVIÇOS ESPECIALIZADOS LTDA-ME                                0.007200   
GERAL LESTE COM. E MANUT. DE MAQUINAS E PREDIAL LTDA - ME                             0.007200   
FHB - COMERCIAL ELETRÔNICA LTDA                                                       0.007003   
COOPERUNIDAS - COOPERATIVA DE TRANSPORTES ALTERNATIVOS                                0.006865   
MARCOS E BERTA LTDA - ME                                                              0.006400   
CRISTIANE MABEL TEIXEIRA 05498863624                       

txtObjetoContrato
36                                  SERVIÇOS DE MANUTENÇÃO E INSTALAÇÃO DE CONDICIONADORES DE AR DRE/DIPED
142                               Contratação de Empresa para Serviços de manutenção no CEI Madre Cristina
164                 Contratação de Empresa para Serviços de manutenção na EMEF Coronel Hélio Franco Chaves
177                      Contratação de Empresa para Serviços de manutenção no CEI Maria Henriqueta Catite
188                                   Contratação de Empresa para Serviços de manutenção no CEU CEI Jaçanã
204                             Contratação de Empresa para Serviços de manutenção no teatro do CEU Jaçanã
354    Contratação de Empresa para Serviços de manutenção no prédio do Bloco Esportivo e Cultural do CE...
371                             Serviço de Manutenção e recarga de extintores e equipamentos de segurança.
403                                                 MANUTENÇÃO E CONSERVAÇÃO - EMEF ANNA SILVEIRA PEDREIRA
404                         Manutenção predial – INSTALAÇÕES HIDRÁULICAS -  EMEI EUNICE DOS SANTOS, PROFA.
408                                   Manutenção predial – MANUTENÇÃO DE REVESTIMENTO – EMEF Rogê Ferreira
411                                               SERVIÇOS GERAIS DE MANUTENÇÃO PREDIAL - CEI CEU UIRAPURU
424                                    Manutenção predial – MANUTENÇÃO NO PISO - CEI SOLEDAD BARRET VIEDMA
433                                  MANUTENÇÃO E CONSERVAÇÃO - EMEF MARIA RITA DE C.ASSIA P. SIMÕES BRAGA
435                                                 MANUTENÇÃO E CONSERVAÇÃO - EMEF ANTONIO ALVES DA SILVA
439                                                 MANUTENÇÃO E CONSERVAÇÃO - EMEF MAURO FACCIO - ZACARIA
445                                                      MANUTENÇÃO E CONSERVAÇÃO - CEI JARDIM MARIA ALICE
447                                                              MANUTENÇÃO E CONSERVAÇÃO - CEI CID FRANCO
448                                                      MANUTENÇÃO E CONSERVAÇÃO - EMEF MODESTO SCAGLIUSI
449                                               MANUTENÇÃO E CONSERVAÇÃO - EMEI JOAQUIM MANUEL DE MACEDO
465                                                                                                    NaN
598           Contratação de Empresa para Serviços de manutenção na EMEI José Bonifácio de Andrada e Silva
687    SP/IT CONTRATAÇÃO DE EMPRESA PARA SERVIÇOS DE REPAROS NAS INSTALAÇÕES CENOTÉCNICAS DO TEATRO DO ...
709    SP/IT CONTRATAÇÃO DE EMPRESA PARA SERVIÇOS DE SUBSTITUIÇÃO DA CALHA DA QUADRA EMEF. PROFª. MARIS...
711    SP/MP CONTRATAÇÃO DE EMPRESA PARA SERVIÇOS DE MANUTENÇÃO NA ESTRUTURA METÁLICA DO RESERVATÓRIO D...
719                             Manutenção predial – PODA DE ÁRVORES - EMEI PROFª NEYDE GUZZI DE CHIACCHIO
723        SP/IT CONTRATAÇÃO DE EMPRESA PARA SERVIÇOS DE MANUTENÇÃO DA CAIXA D'AGUA NO CEI IND. VILA JÓIA 
765                            SP/IT - CONTRATAÇÃO PARA MANUTENÇÃO DA PARTE ELÉTRICA NO CEU PARQUE VEREDAS
795    SP/MP CONTRATAÇÃO DE EMPRESA PARA SERVIÇOS DE IMPERMEABILIZAÇÃO DA CAIXA D'AGUA DE REUSO DA CEI ...
841                               Manutenção predial – MANUTENÇÃO DE TELHADO E PISO - EMEI AFONSO SARDINHA
...                                                                                                    ...
53896                                Manutenção predial – MANUTENÇÃO  ELÉTRICA - EMEF AMADEU MENDES, PROFº
53897                                   SERVIÇOS GERAIS DE MANUTENÇÃO PREDIAL - EMEF. PROF. ROBERTO MANGE.
53898                         Manutenção predial – Manutenção nas calhas e coberturas - CEU GESTÃO JAGUARÉ
53903                               SERVIÇOS GERAIS DE MANUTENÇÃO PREDIAL - EMEI PROF. BENEDICTO CASTRUCCI
54236                                             SERVIÇO DE MANUTENÇÃO DE TELHADO - EMEI GLEBA DO PÊSSEGO
54323                  Manutenção predial – MANUTENÇÃO DE INSTALAÇÕES HIDRAULICAS - EMEI JARDIM MONTE BELO
54371                  

## 3.6 Aluguel de imóveis e IPTU

In [598]:
aluguel_imoveis_filter = (
    empenhos_df['txtDescricaoItemDespesa'].str.contains('Locação de Imóveis', case=False)
    |
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('IPTU', case=False))
)
aluguel_imoveis = (empenhos_df[aluguel_imoveis_filter])
empenhos_df.loc[aluguel_imoveis_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[aluguel_imoveis_filter, 'cat_2'] = 'aluguel_imoveis'
groupSum(aluguel_imoveis)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          24.199316     18.825336   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     19.519948

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             24.199316     18.825336     19.519948

valTotalEmpenhado  \
txtDescricaoElemento                                                
Outros Serviços de Terceiros -Pessoa Jurídica           14.870512   
Outros Serviços de Terceiros - Pessoa Física             9.048384   
Outros Serviços de Terceiros - Pessoa Jurídica           0.280420   

                                                valLiquidado  valPagoTotal  
txtDescricaoElemento                                                        
Outros Serviços de Terceiros -Pessoa Jurídica      11.425897     11.860792  
Outros Serviços de Terceiros - Pessoa Física        7.157610      7.406123  
Outros Serviços de Terceiros - Pessoa Jurídica      0.241828      0.253034

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 24.199316     18.825336     19.519948

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoItemDespesa                                               
Locação de Imóveis               22.911279     17.577437     18.270620
IPTU                              1.288037      1.247898      1.249328

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Diretoria Regional de Educação - Santo Amaro                     5.446101   
Diretoria Regional de Educação - Capela do Socorro               4.972329   
Diretoria Regional de Educação - Ipiranga                        3.411035   
Diretoria Regional de Educação - Butantã                         2.427450   
Diretoria Regional de Educação - São Mateus                      1.030175   
Diretoria Regional de Educação - São Miguel                      0.884889   
Diretoria Regional de Educação - Guaianases                      0.820028   
Gabinete do Secretário                                           1.265979   
Diretoria Regional de Educação - Itaquera                        0.806349   
Diretoria Regional de Educação - Campo Limpo                     0.659739   
Departamento de Alimentação Escolar                              0.426987   
Diretoria Regional de Educação - Jaçanã/Tremembé                 0.455894   
Diretoria Regional de Educação  Capela do Socorro                0.487779   
Diretoria Regional de Educação - Penha                           0.452543   
Diretoria Regional de Educação - Pirituba                        0.328864   
Diretoria Regional de Educação - Freguesia/Brasilândia           0.248373   
Coordenadoria de Alimentação Escolar                             0.074800   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Diretoria Regional de Educação - Santo Amaro                4.509562   
Diretoria Regional de Educação - Capela do Socorro          3.589969   
Diretoria Regional de Educação - Ipiranga                   2.927363   
Diretoria Regional de Educação - Butantã                    1.428948   
Diretoria Regional de Educação - São Mateus                 0.926937   
Diretoria Regional de Educação - São Miguel                 0.861278   
Diretoria Regional de Educação - Guaianases                 0.734312   
Gabinete do Secretário                                      0.642569   
Diretoria Regional de Educação - Itaquera                   0.631560   
Diretoria Regional de Educação - Campo Limpo                0.608687   
Departamento de Alimentação Escolar                         0.415597   
Diretoria Regional de Educação - Jaçanã/Tremembé            0.369834   
Diretoria Regional de Educação  Capela do Socorro           0.353692   
Diretoria Regional de Educação - Penha                      0.304474   
Diretoria Regional de Educação - Pirituba                   0.268537   
Diretoria Regional de Educação - Freguesia/Brasilândia      0.224994   
Coordenadoria de Alimentação Escolar                        0.027021   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Diretoria Regional de Educação - Santo Amaro                4.876779  
Diretoria Regional de Educação - Capela do Socorro          3.589969  
Diretoria Regional de Educação - Ipiranga                   2.950637  
Diretoria Regional de Educação - Butantã                    1.428948  
Diretoria Regional de Educação - São Mateus                 1.002179  
Diretoria Regional de Educação - São Miguel                 0.861278  
Diretoria Regional de Educação - Guaianases                 0.797013  
Gabinete do Secretário                                      0.730822  
Diretoria Regional de Educação - Itaquera                   0.631560  
Diretoria Regional de Educação - Campo Limpo                0.627797  
Departamento de Alimentação Escolar                         0.415597  
Diretoria Regional de Educação - Jaçanã/Tremembé            0.402316  
Diretoria Regional de Educação  Capela do Socorro           0.362026  
Diretoria Regional de Educação - Penha                      0.304474  
Diretoria Regional de Educação - Pirituba                   0.268537  
Diretoria Region

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          24.199316     18.825336     19.519948

valTotalEmpenhado  \
txtModalidadeAplicacao                                                                     
Aplicações Diretas                                                             23.918896   
Transferências a Instituições Privadas sem Fins Lucrativos                      0.137952   
Apl.Dir.Dec.Op. entre Órgãos,Fundos e Ent.Int.Orç.Fiscal e Seg.Social           0.142468   

                                                                       valLiquidado  \
txtModalidadeAplicacao                                                                
Aplicações Diretas                                                        18.583507   
Transferências a Instituições Privadas sem Fins Lucrativos                 0.129775   
Apl.Dir.Dec.Op. entre Órgãos,Fundos e Ent.Int.Orç.Fiscal e Seg.Social      0.112054   

                                                                       valPagoTotal  
txtModalidadeAplicacao                                                               
Aplicações Diretas                                                        19.266914  
Transferências a Instituições Privadas sem Fins Lucrativos                 0.129775  
Apl.Dir.Dec.Op. entre Órgãos,Fundos e Ent.Int.Orç.Fiscal e Seg.Social      0.123259

valTotalEmpenhado  \
txtRazaoSocial                                                                      
MASTER ADMINISTRACAO DE IMOVEIS PROPRIOS LTDA                            2.072770   
FEMARJAN COSTRUTORA LTDA                                                 1.694046   
SEARA BENDITA INSTITUICAO ESPIRITA                                       1.173829   
MCT ADMINISTRAÇÃO DE IMÓVEIS LTDA - EPP                                  0.964000   
HAGE ADMINISTRAÇÃO DE BENS LTDA.- ME                                     0.724383   
ROLEX CONSULTORIA E ADMINISTRAÇÃO DE BENS E NEGÓCIOS LTDA - ME           0.779624   
ENAL EMPREENDIMENTOS LTDA                                                1.473781   
OTTAVIANI EMPREENDIMENTO IMOBILIARIO LTDA                                0.601519   
S.R. ADMINISTRADORA DE BENS PROPRIOS - EIRELI                            0.593349   
SOCIEDADE  DE ARMAZENS E REPRESENTAÇÕES  SÃO LOURENÇO LTDA               0.493227   
MS BACHA ADMINISTRAÇÃO DE BENS PRÓPRIOS LTDA.                            0.457700   
HOLDING CARDOSO DISTRIBUIDORA E PARTICIPAÇOES LTDA                       0.504261   
CAMPER EMPREENDIMENTOS LTDA                                              0.390783   
DIRETORIA REGIONAL DE EDUCAÇÃO - IPIRANGA                                0.312861   
AAA HOLDING PATRIMONIAL E PARTICIPAÇÕES - EIRELI                         0.319958   
SANTO AMARO PARTICIPAÇOES LTDA                                           0.372000   
ROSANA FERREIRA DE TOLEDO                                                0.328864   
SME/ DIRETORIA REGIONAL DE EDUCAÇÃO - SANTO AMARO                        0.259742   
EGBERTO CAMPOS FRAGA FILHO                                               0.241658   
MARIA AP. FRAGA DE ALMEIDA PRADO                                         0.239366   
MARIA CAROLINA FRAGA ZWICKER                                             0.247441   
MANOEL CARLOS ALTIERI                                                    0.433480   
WALDIR DE SOUZA LOPES                                                    0.225869   
SÃO GUALTER ADMINISTRAÇÃO E PARTICIPAÇÕES LTDA                           0.232558   
CARLOS GILBERTO DO ESPIRITO SANTO                                        0.195582   
MARIA AMELIA RODRIGUES RACHID                                            0.187303   
NEURO FERREIRA DOS SANTOS                                                0.169449   
DIRETORIA REGIONAL DE EDUCAÇÃO - BUTANTÃ                                 0.165496   
MAZEN SERVIÇOS DE ADMINISTRAÇÃO LTDA                                     0.163214   
DOMINGOS ALVES DE CARVALHO                                               0.162522   
...                                                                           ...   
CARLOS TORRES MORAES                                                     0.046468   
SERGIO TORRES MORAES                                                     0.046468   
ESTECYR DE SIQUEIRA                                                      0.034392   
FUMIO NISHIYAMA                                                          0.047996   
LUIZ GIOSA                                                               0.030026   
ELZA SOARES GIOSA                                                        0.030026   
JACQUELINE BARMAK                                                        0.054185   
DORA BARMAK                                                              0.054185   
JOSÉ ALBERTO BARMAK                                                      0.054185   
IVETE APARECIDA VICENTE DOTTORI                                          0.029135   
KANDICE SCHEIDEMANTEL DA ROCHA LIMA                                      0.033566   
KRISTIAN SCHEIDEMANTEL DA ROCHA LIMA                                     0.033566   
SME - DIRETORIA REGIONAL DE EDUCAÇÃO - CAPELA DO SOCORRO                 0.025501   
MARIA CRISTINA MATTOSO RAMOS DE SOUZA                                    0.035624   
ROBERTO ASSAF                                                        

txtObjetoContrato
683               NaN

## 3.7 Obras e reformas

In [599]:
obras_reformas_filter = (
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('constru', case=False))
    |
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('reforma', case=False))
)
obras_reformas = (empenhos_df[obras_reformas_filter])
empenhos_df.loc[obras_reformas_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[obras_reformas_filter, 'cat_2'] = 'obras_reformas'
groupSum(obras_reformas)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação         109.748075     58.263296   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     78.704729

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas de Capital           109.748075     58.263296     78.704729

valTotalEmpenhado  \
txtDescricaoElemento                                                
Obras e Instalações                                     89.634945   
Indenizações e Restituições                             14.682730   
Outros Serviços de Terceiros - Pessoa Jurídica           4.668341   
Aquisição de Imóveis                                     0.762059   

                                                valLiquidado  valPagoTotal  
txtDescricaoElemento                                                        
Obras e Instalações                                39.131728     59.550083  
Indenizações e Restituições                        14.682730     14.682730  
Outros Serviços de Terceiros - Pessoa Jurídica      3.686780      3.709857  
Aquisição de Imóveis                                0.762059      0.762059

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 50.697717     23.415711     34.567339
Outras Fontes                     33.979873     16.566437     24.311365
Transferências Estaduais          20.010323     16.419021     16.419021
Transferências Federais            5.060162      1.862127      3.407003

valTotalEmpenhado  valLiquidado  \
txtDescricaoItemDespesa                                                  
Escolas e Similares                            89.634945     39.131728   
Restituições a Pessoas Jurídicas               14.682730     14.682730   
Gerenciamento                                   3.528341      3.117437   
Desapropriações                                 0.762059      0.762059   
Manutenção e Reformas de Bens Imóveis           1.140000      0.569343   

                                       valPagoTotal  
txtDescricaoItemDespesa                              
Escolas e Similares                       59.550083  
Restituições a Pessoas Jurídicas          14.682730  
Gerenciamento                              3.140515  
Desapropriações                            0.762059  
Manutenção e Reformas de Bens Imóveis      0.569343

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário         109.748075     58.263296     78.704729

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                               
Investimentos           109.748075     58.263296     78.704729

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas             109.748075     58.263296     78.704729

valTotalEmpenhado  \
txtRazaoSocial                                                              
LOPES KALIL ENGENHARIA E COMERCIO LTDA                          24.832149   
SAO PAULO SECRETARIA DA EDUCACAO                                14.682730   
LEMAM CONSTRUCOES E COMERCIO S.A.                               15.664034   
CONSÓRCIO FBS - LOPES KALIL                                     14.142956   
CONSTRUTORA CRONACON LTDA                                       10.552064   
CONSTRUMEDICI ENGENHARIA E COMÉRCIO  LTDA                        5.406643   
FLASA ENGENHARIA E CONSTRUCOES LTDA                              6.325143   
SIMETRICA ENGENHARIA LTDA                                        2.269715   
KALLAS ENGENHARIA LTDA                                           1.991962   
DB CONSTRUCOES LTDA                                              2.148101   
ENGEBRAS CONSTRUÇÕES E EMPREENDIMENTOS LTDA                      5.766503   
CONSTRUTORA ITAJAI LTDA                                          1.666799   
DEPTO DESAP COND AC  JUD EM DESAPR                               0.762059   
HE ENGENHARIA  COMÉRCIO E REPRESENTAÇÕES LTDA                    0.755351   
CONSTRUTORA PROGREDIOR LTDA                                      1.140000   
SANED ENGENHARIA  E EMPREENDIMENTOS S.A                          0.547165   
CENTRAL DE PLANEJAMENTO DE  OBRAS  E CONSTRUÇÕES  LTDA           0.522889   
ALMEIDA SAPATA ENGENHARIA E CONSTRUÇÕES LTDA                     0.559027   
SYSTEM ENGENHARIA LTDA                                           0.012787   

                                                        valLiquidado  \
txtRazaoSocial                                                         
LOPES KALIL ENGENHARIA E COMERCIO LTDA                     14.212378   
SAO PAULO SECRETARIA DA EDUCACAO                           14.682730   
LEMAM CONSTRUCOES E COMERCIO S.A.                           5.957008   
CONSÓRCIO FBS - LOPES KALIL                                 4.945245   
CONSTRUTORA CRONACON LTDA                                   2.944424   
CONSTRUMEDICI ENGENHARIA E COMÉRCIO  LTDA                   3.873227   
FLASA ENGENHARIA E CONSTRUCOES LTDA                         1.975835   
SIMETRICA ENGENHARIA LTDA                                   1.835567   
KALLAS ENGENHARIA LTDA                                      0.325909   
DB CONSTRUCOES LTDA                                         1.447351   
ENGEBRAS CONSTRUÇÕES E EMPREENDIMENTOS LTDA                 1.091909   
CONSTRUTORA ITAJAI LTDA                                     1.355032   
DEPTO DESAP COND AC  JUD EM DESAPR                          0.762059   
HE ENGENHARIA  COMÉRCIO E REPRESENTAÇÕES LTDA               0.741501   
CONSTRUTORA PROGREDIOR LTDA                                 0.569343   
SANED ENGENHARIA  E EMPREENDIMENTOS S.A                     0.531595   
CENTRAL DE PLANEJAMENTO DE  OBRAS  E CONSTRUÇÕES  LTDA      0.522875   
ALMEIDA SAPATA ENGENHARIA E CONSTRUÇÕES LTDA                0.489309   
SYSTEM ENGENHARIA LTDA                                      0.000000   

                                                        valPagoTotal  
txtRazaoSocial                                                        
LOPES KALIL ENGENHARIA E COMERCIO LTDA                     21.855359  
SAO PAULO SECRETARIA DA EDUCACAO                           14.682730  
LEMAM CONSTRUCOES E COMERCIO S.A.                           9.157260  
CONSÓRCIO FBS - LOPES KALIL                                 7.446875  
CONSTRUTORA CRONACON LTDA                                   5.540711  
CONSTRUMEDICI ENGENHARIA E COMÉRCIO  LTDA                   4.723819  
FLASA ENGENHARIA E CONSTRUCOES LTDA                         3.218295  
SIMETRICA ENGENHARIA LTDA                                   2.269715  
KALLAS ENGENHARIA LTDA                                      1.676465  
DB CONSTRUCOES LTDA                                         1.563723  
ENGEBRAS CONSTRUÇÕES E EMPREENDIMENTOS LTDA                 1.562200  
CO

txtObjetoContrato
387                                     NaN
7380  CONFECÇÃO  DE COLETES, LONAS E XADREZ

## 3.8 CEUs - outros custos

In [600]:
ceu_filter = (
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('Operação e Manutenção dos Centros Educacionais Unificados', case=False))
    &
    (
        (empenhos_df['txtDescricaoItemDespesa'].str.contains('Outros Serviços de Áudio, Vídeo, Foto, Som, Luz e Imagens', case=False))
        |
        (empenhos_df['txtDescricaoItemDespesa'].str.contains('Lavanderia em Geral', case=False))
        |
        (empenhos_df['txtDescricaoItemDespesa'].str.contains('Monitoramento Aquático', case=False))
    )
)
ceu = (empenhos_df[ceu_filter])
empenhos_df.loc[ceu_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[ceu_filter, 'cat_2'] = 'ceu_outros'
groupSum(ceu)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          28.004133     23.396643   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     25.410115

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             28.004133     23.396643     25.410115

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica          28.004133   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica     23.396643     25.410115

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 28.004133     23.396643     25.410115

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                        
Lavanderia em Geral                                                 8.897260   
Outros Serviços de Áudio, Vídeo, Foto, Som, Luz e Imagens           9.379732   
Monitoramento Aquático                                              9.727140   

                                                           valLiquidado  \
txtDescricaoItemDespesa                                                   
Lavanderia em Geral                                            8.152681   
Outros Serviços de Áudio, Vídeo, Foto, Som, Luz e Imagens      8.203001   
Monitoramento Aquático                                         7.040960   

                                                           valPagoTotal  
txtDescricaoItemDespesa                                                  
Lavanderia em Geral                                            8.897260  
Outros Serviços de Áudio, Vídeo, Foto, Som, Luz e Imagens      8.831185  
Monitoramento Aquático                                         7.681670

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário          28.004133     23.396643     25.410115

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          28.004133     23.396643     25.410115

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              28.004133     23.396643     25.410115

valTotalEmpenhado  \
txtRazaoSocial                                                       
MARTINS & LOCOCO LAVANDERIA LTDA                          8.897260   
E.SERVICE COMERCIO E SERVIÇOS LTDA                        5.162101   
FLASH ILUMINACÃO E SONORIZACÃO LTDA - EPP                 3.304667   
LUME SERVIÇOS GERAIS LTDA EPP                             2.899012   
SHAMOU - ESPORTES COMÉRCIO E SERVIÇOS LTDA - ME           2.130006   
BAKMAR ELETRONICA LTDA ME                                 1.349765   
FHB - COMERCIAL ELETRÔNICA LTDA                           1.137263   
FLYPPER SALVAMENTO AQUÁTICO LTDA. EPP                     1.503474   
ARCOLIMP SERVIÇOS GERAIS LTDA                             0.764375   
LIFE WORK SERVIÇOS ESPECIALIZADOS LTDA                    0.689026   
E SERVICE SOLUCOES EM SERVICOS EIRELI - ME                0.167185   

                                                 valLiquidado  valPagoTotal  
txtRazaoSocial                                                               
MARTINS & LOCOCO LAVANDERIA LTDA                     8.152681      8.897260  
E.SERVICE COMERCIO E SERVIÇOS LTDA                   3.413503      3.770282  
FLASH ILUMINACÃO E SONORIZACÃO LTDA - EPP            3.016439      3.296961  
LUME SERVIÇOS GERAIS LTDA EPP                        2.504761      2.703958  
SHAMOU - ESPORTES COMÉRCIO E SERVIÇOS LTDA - ME      1.839776      2.036581  
BAKMAR ELETRONICA LTDA ME                            1.173434      1.184251  
FHB - COMERCIAL ELETRÔNICA LTDA                      0.887909      0.968531  
FLYPPER SALVAMENTO AQUÁTICO LTDA. EPP                0.950726      0.950726  
ARCOLIMP SERVIÇOS GERAIS LTDA                        0.684738      0.757645  
LIFE WORK SERVIÇOS ESPECIALIZADOS LTDA               0.620458      0.677482  
E SERVICE SOLUCOES EM SERVICOS EIRELI - ME           0.152217      0.166436

txtObjetoContrato
2463                                                                                                   NaN
5582                                               Contratação emergencial de manutenção de Som de 23 CEUs
5583                                        Contratação emergencial de manutenção de Iluminação de 23 CEUs
38767                                        SERVIÇOS GERAIS DE MANUTENÇÃO PREDIAL - EMEF. JARDIM PAULO VI
38925                           CONTRATAÇÃO DE AGENTE RECREATIVO - RECREIO NAS FÉRIAS EDIÇÃO JULHO DE 2017
38929  PR-SM(S.MATEUS) – PR-VP/SB (SAPOPEMBA) – CONTRATAÇÃO DE OFICINEIROS - RECREIO NAS FÉRIAS JULHO/2017
40132       Contratação emergencial de serviços de manutenção dos equipamentos de Som dos Teatros de CEUs.
40138  Contratação emergencial de serviços de manutenção dos equipamentos de Iluminação dos Teatros de ...

## 3.? UniCEU

In [601]:
uniceu_filter = (
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('uniceu', case=False))
)
uniceu = (empenhos_df[uniceu_filter])
empenhos_df.loc[uniceu_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[uniceu_filter, 'cat_2'] = 'uniceu'
groupSum(uniceu)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação            3.07456      2.142509   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação      2.870959

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes              2.990401      2.142509      2.786800
Despesas de Capital             0.084159      0.000000      0.084159

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica           2.989290   
Equipamentos e Material Permanente                      0.084159   
Material de Consumo                                     0.001112   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica      2.142509      2.786800  
Equipamentos e Material Permanente                 0.000000      0.084159  
Material de Consumo                                0.000000      0.000000

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                   3.07456      2.142509      2.870959

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                        
Supervisão, Acompanhamento e Suporte de Serviços Técnicos           2.731250   
Guarda, Vigilância e Segurança em Geral                             0.228290   
Outros Equipamentos para Vídeo, Áudio e Foto                        0.084159   
Refeições para Eventos em Educação                                  0.029750   
Diversos Materiais de Limpeza e Higienização                        0.001112   

                                                           valLiquidado  \
txtDescricaoItemDespesa                                                   
Supervisão, Acompanhamento e Suporte de Serviços Técnicos      1.909764   
Guarda, Vigilância e Segurança em Geral                        0.202995   
Outros Equipamentos para Vídeo, Áudio e Foto                   0.000000   
Refeições para Eventos em Educação                             0.029750   
Diversos Materiais de Limpeza e Higienização                   0.000000   

                                                           valPagoTotal  
txtDescricaoItemDespesa                                                  
Supervisão, Acompanhamento e Suporte de Serviços Técnicos      2.534567  
Guarda, Vigilância e Segurança em Geral                        0.222483  
Outros Equipamentos para Vídeo, Áudio e Foto                   0.084159  
Refeições para Eventos em Educação                             0.029750  
Diversos Materiais de Limpeza e Higienização                   0.000000

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário            3.07456      2.142509      2.870959

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes           2.990401      2.142509      2.786800
Investimentos                       0.084159      0.000000      0.084159

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas                3.07456      2.142509      2.870959

valTotalEmpenhado  \
txtRazaoSocial                                                                                  
UNIAO SOCIAL CAMILIANA                                                               2.731250   
MRS SEGURANCA E VIGILANCIA PATRIMONIAL EIRELI - EPP                                  0.228290   
HS COMERCIO LOCAÇÃO E MANUTENÇÃO DE EQUIPAMENTOS DE INFORMATICA LTDA - EPP           0.084159   
F.G.R. SILVA BUFFET E EVENTOS LTDA.                                                  0.029750   
CCK COMERCIAL EIRELI - EPP                                                           0.001112   

                                                                            valLiquidado  \
txtRazaoSocial                                                                             
UNIAO SOCIAL CAMILIANA                                                          1.909764   
MRS SEGURANCA E VIGILANCIA PATRIMONIAL EIRELI - EPP                             0.202995   
HS COMERCIO LOCAÇÃO E MANUTENÇÃO DE EQUIPAMENTOS DE INFORMATICA LTDA - EPP      0.000000   
F.G.R. SILVA BUFFET E EVENTOS LTDA.                                             0.029750   
CCK COMERCIAL EIRELI - EPP                                                      0.000000   

                                                                            valPagoTotal  
txtRazaoSocial                                                                            
UNIAO SOCIAL CAMILIANA                                                          2.534567  
MRS SEGURANCA E VIGILANCIA PATRIMONIAL EIRELI - EPP                             0.222483  
HS COMERCIO LOCAÇÃO E MANUTENÇÃO DE EQUIPAMENTOS DE INFORMATICA LTDA - EPP      0.084159  
F.G.R. SILVA BUFFET E EVENTOS LTDA.                                             0.029750  
CCK COMERCIAL EIRELI - EPP                                                      0.000000

txtObjetoContrato
30987                                                                                      NaN
33422  Aquisição de lixeiras para a Universidade nos Centros Educacionais Unificados – UniCEU 
40511                                                         AQUISIÇÃO DE PROJETOR MULTIMIDIA
56439                     Utilização de Ata de Registro de Preços – Fornecimento de kit lanche

## 3.9 Eventos, oficinas, recreação

In [602]:
eventos_filter = (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Eventos Esportivos, Culturais e Turísticos', case=False))
    |
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Oficineiros', case=False))

)
eventos = (empenhos_df[eventos_filter])
empenhos_df.loc[eventos_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[eventos_filter, 'cat_2'] = 'eventos'
groupSum(eventos)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          10.788179      9.045793   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação      9.126208

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             10.788179      9.045793      9.126208

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica           8.018114   
Outros Serviços de Terceiros - Pessoa Física            2.770065   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica      6.497739      6.497739  
Outros Serviços de Terceiros - Pessoa Física       2.548054      2.628469

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 10.788179      9.045793      9.126208

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                        
Eventos Esportivos, Culturais e Turísticos                          7.310114   
Oficineiros                                                         2.770065   
Eventos Esportivos, Culturais e Turísticos - Cooperativas           0.708000   

                                                           valLiquidado  \
txtDescricaoItemDespesa                                                   
Eventos Esportivos, Culturais e Turísticos                     5.812939   
Oficineiros                                                    2.548054   
Eventos Esportivos, Culturais e Turísticos - Cooperativas      0.684800   

                                                           valPagoTotal  
txtDescricaoItemDespesa                                                  
Eventos Esportivos, Culturais e Turísticos                     5.812939  
Oficineiros                                                    2.628469  
Eventos Esportivos, Culturais e Turísticos - Cooperativas      0.684800

...

valTotalEmpenhado  valLiquidado  \
txtDescricaoUnidade                                                             
Gabinete do Secretário                                 9.992492      8.334085   
Diretoria Regional de Educação - Campo Limpo           0.460737      0.402741   
Diretoria Regional de Educação - Ipiranga              0.132132      0.119688   
Diretoria Regional de Educação - Penha                 0.118952      0.105414   
Diretoria Regional de Educação - Butantã               0.027095      0.027095   
Diretoria Regional de Educação - São Mateus            0.021710      0.021710   
Diretoria Regional de Educação - Guaianases            0.013280      0.013280   
Diretoria Regional de Educação - São Miguel            0.012300      0.012300   
Diretoria Regional de Educação - Itaquera              0.006240      0.006240   
Diretoria Regional de Educação - Santo Amaro           0.003240      0.003240   

                                              valPagoTotal  
txtDescricaoUnidade                                         
Gabinete do Secretário                            8.337109  
Diretoria Regional de Educação - Campo Limpo      0.457077  
Diretoria Regional de Educação - Ipiranga         0.131400  
Diretoria Regional de Educação - Penha            0.116757  
Diretoria Regional de Educação - Butantã          0.027095  
Diretoria Regional de Educação - São Mateus       0.021710  
Diretoria Regional de Educação - Guaianases       0.013280  
Diretoria Regional de Educação - São Miguel       0.012300  
Diretoria Regional de Educação - Itaquera         0.006240  
Diretoria Regional de Educação - Santo Amaro      0.003240

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          10.788179      9.045793      9.126208

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              10.788179      9.045793      9.126208

valTotalEmpenhado  \
txtRazaoSocial                                                                        
TOKA EVENTOS ARTISTICOS EIRELI                                             0.702000   
COOPERATIVA PAULISTA DE TEATRO                                             0.564000   
CONFEDERAÇÃO BRASILEIRA DE ARTES MARCIAIS CHINESAS - KUNG FU               0.630115   
BAIOQUE PRODUCOES ARTISTICAS LTDA - ME                                     0.350000   
FEDERAÇÃO DO DESPORTO ESCOLAR DO ESTADO DE SÃO PAULO                       0.330915   
BOLZAN E ASCHENBACH EVENTOS LTDA                                           0.276000   
FEDERAÇÃO PAULISTA DE KARATE                                               0.258095   
NAJARA CINE VIDEO E EVENTOS LTDA                                           0.603800   
FEDERAÇÃO PAULISTA DE ARTES MARCIAIS INTERESTILOS                          0.223940   
RIGMATOUR EVENTOS E TURISMO LTDA - ME                                      0.175000   
CARLOS NAVAS PRODUCOES EIRELI - ME                                         0.155000   
DANIEL DE SOUZA LIMA 22328226809                                           0.150000   
COOPERATIVA DE TRABALHO DOS PROFISSIONAIS DE MUSICA DE SAO PAULO           0.144000   
GRIMARK EVENTOS LTDA - ME                                                  0.130000   
CASA FORTE SP PRODUCOES ARTISTICAS LTDA - ME                               0.120000   
SINGLE PRODUCOES E EVENTOS ARTISTICOS EIRELI                               0.119000   
XLEVY PRODUÇÕES ARTISTICAS LTDA                                            0.115000   
CRIOLA FILMES E PRODUCOES ARTISTICAS LTDA-ME                               0.112000   
MM & ETF PROMOÇÃO E PUBLICIDADE LTDA - ME                                  0.110000   
BRANCO EVENTOS LTDA                                                        0.107000   
GIRANDOLA PRODUCOES ARTISTICAS EIRELI                                      0.104000   
FEDERAÇÃO PAULISTA DE KUNG FU, WUSHU E KUOSHU TRADICIONAL                  0.123909   
LUIZ LOBATO DA SILVA 22078012840                                           0.094800   
AGO LONA                                                                   0.150000   
PAULO MARCOS FALCO DE BRITO PRODUÇÕES ARTISTICAS - ME                      0.072000   
SAZARTE PRODUÇÕES LTDA                                                     0.070000   
T.T. SOMAIO PRODUÇÕES ARTÍSTICAS E CULTURAIS                               0.069000   
ADRIANY DE SOUSA MOTA                                                      0.068808   
DENIS DA SILVA SANTOS                                                      0.065000   
MARCELO BESSA DE LIMA                                                      0.060756   
...                                                                             ...   
WANDERLEY MARTINI JUNIOR SARGENTO                                          0.000168   
VILMA MAXIMIANO VIEIRA                                                     0.000780   
SHEILA APARECIDA DA SILVA OLIVEIRA                                         0.000780   
LUCAS MICHELÃO                                                             0.000900   
HELIO DAMIAO SOARES DA SILVA                                               0.000900   
MARCIA JESUS DA SILVA GARCIA                                               0.000780   
ALEXANDRE GOMES DE ANDRADE                                                 0.000900   
ROSEMARY DELMONDES SILVA                                                   0.000900   
FABIANA SILVA FERREIRA                                                     0.000780   
MARCELO VIEIRA DA SILVA                                                    0.000900   
HEITOR RIMAN                                                               0.000780   
FERNANDA DA SILVA                                                          0.000420   
SILVIO ROBERTO VIEIRA DOS SANTOS FILHO                                     0.000672   
ADNAIELY LACERDA DE JESUS OLIVEIRA                              

txtObjetoContrato
2003                                                      CONTRATAÇÃO DE OFICINEIRO - EXETENSÃO DE JORNADA
2005                                                       CONTRATAÇÃO DE OFICINEIRO - EXTENSÃO DE JORNADA
2205          CONTRATAÇÃO DE OFICINEIROS - EXTENSÃO DE JORNADA NOS CEUs PERIODO DE 05/06/2017 À 31/08/2017
2209         CONTRATAÇÃO DE OFICINEIROS - EXTENSÃO DE JORNADA NOS CEU'S PERÍODO DE 05/06/2017 A 31/08/2017
2210       CONTRATAÇAO DE OFICINEIROS - EXTENSÃO DE JORNADA NOS CEUS NO PERÍODO DE 05/06/2017 A 31/08/2017
2236                                                       Contratação de Oficineiro - Extensão de Jornada
2240                                               Contratação oficineiros - Extensão de Jornada nos CEUS 
2269                                                      CONTRATAÇÃO DE OFICINEIROS - EXENSÃO DE JORNADA.
2270                                                     CONTRATAÇÃO DE OFICINEIROS - EXTENSÃO DE JORNADA.
2609            CONTRATAÇÃO DE OFICINEIROS PARA O PROGRAMA EXTENSÃO DE JORNADA  DOS ALUNOS NOS CEUs E CECI
2681                             PRESTAÇÃO DE SERVIÇO COMO OFICINEIRO NO PROGRAMA EXTENSÃO DE JORNADA/2017
2686                             Prestação de serviço como oficineiro no Programa Extensão de Jornada/2017
2689                           PRESTAÇÃO DE SERVIÇO COMO OFICINEIRO NO PROGRAMA EXTENSÃO DE JORNADA/2017\n
2696                             Prestação de serviço como Oficineiro no Programa Extensão de Jornada/2017
2715             CONTRATAÇÃO DE OFICINEIROS PARA O PROGRAMA EXTENSÃO DE JORNADA DOS ALUNOS NOS CEUs E CECI
3064                        Apresentações do Espetáculo “REISADO DA BORBOLETA, DO MARACUJÁ E DO PICA-PAU” 
3593                    CONTRATAÇÃO DE AGENTE DE RECREAÇÃO PARA O PROJETO RECREIO NAS FÉRIAS - JULHO/2017.
3594                     CONTRATAÇÃO DE AGENTE DE RECREAÇÃO PAR O PROJETO RECREIO NAS FÉRIAS - JULHO/2017.
3602   PR-SM(S.MATEUS) – PR-VP/SB (SAPOPEMBA) – CONTRATAÇÃO DE COORDENADORES DE POLO - RECREIO NAS FÉRI...
3607   PR-SM(S.MATEUS) – PR-VP/SB (SAPOPEMBA) – CONTRATAÇÃO DE AGENTE DE RECREAÇÃO -  RECREIO NAS FÉRIA...
3644                                        CONTRATAÇÃO DE AGENTES DE POLO - RECREIO NAS FÉRIAS JULHO/2017
3760                                              CONTRATAÇÃO DE AGENTE RECREATIVO PARA RECREIO NAS FÉRIAS
3843   Contratação de Agente Recreativo para Recreio nas Férias - Edição Julho/2017 - Período de 10/07 ...
4703                                                                                 CONTRATAÇÃO ARTISTICA
4918   CONTRATAÇÃO DE APRESENTAÇÃO ARTÍSTICA DE CONTAÇÃO DE HISTÓRIA “A BARCA DA TARTARUGA & OUTRAS HIS...
4920                                                           Programação Artística e Cultural  dos  CEUs
4930                                                             Programação Artística e Cultural dos CEUs
4937                                                                     CONTRATAÇÃO ARTÍSTICA\r\n\r\n\r\n
4939                                                     Programação Artística e Cultural dos CEUs\r\n\r\n
4945                                                                                 CONTRATAÇÃO ARTÍSTICA
...                                                                                                    ...
58212                                             CONTRATAÇÃO DE AGENTE RECREATIVO - EDIÇÃO JANEIRO 2017\n
58309                                              Contratação de oficineiro-recreio nas férias .-Jan/2017
58312                                                                                               agente
58313                                    Contratação de Coordenador de Polo -Recreio nas Ferias - Jan/2017
58318                                    Contratação de Agente de Recreação -Recreio nas Ferias - jan/2017
58331                                      Contratação de Coordenador de Polo -Recreio nas Ferias jan/2017
58335                  

## 3.3. Outros?

# 4. Uniformes e materiais escolares

## 4.1. Uniformes

#### Checar filtro: pode estar sub representado

In [603]:
uniformes_filter = empenhos_df['txtDescricaoItemDespesa'].str.contains('uniforme', case=False)
uniformes = (empenhos_df[uniformes_filter])
empenhos_df.loc[uniformes_filter, 'cat_1'] = 'uniforme_materiais'
empenhos_df.loc[uniformes_filter, 'cat_2'] = 'uniforme'
groupSum(uniformes)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          300.02518    101.825344   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação    203.651681

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             300.02518    101.825344    203.651681

valTotalEmpenhado  \
txtDescricaoElemento                                                     
Material, Bem ou Serviço para Distribuição Gratuita         299.956901   
Material de Consumo                                           0.035434   
Outros Serviços de Terceiros -Pessoa Jurídica                 0.032845   

                                                     valLiquidado  \
txtDescricaoElemento                                                
Material, Bem ou Serviço para Distribuição Gratuita    101.765057   
Material de Consumo                                      0.027442   
Outros Serviços de Terceiros -Pessoa Jurídica            0.032845   

                                                     valPagoTotal  
txtDescricaoElemento                                               
Material, Bem ou Serviço para Distribuição Gratuita    203.583401  
Material de Consumo                                      0.035434  
Outros Serviços de Terceiros -Pessoa Jurídica            0.032845

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 300.02518    101.825344    203.651681

valTotalEmpenhado  valLiquidado  \
txtDescricaoItemDespesa                                                     
Uniforme Escolar                                 299.956901    101.765057   
Uniformes, Camisas, Coletes e Outros               0.032845      0.032845   
Diversos Uniformes, Tecidos e Aviamentos           0.025565      0.017573   
Uniformes Esportivos                               0.009870      0.009870   

                                          valPagoTotal  
txtDescricaoItemDespesa                                 
Uniforme Escolar                            203.583401  
Uniformes, Camisas, Coletes e Outros          0.032845  
Diversos Uniformes, Tecidos e Aviamentos      0.025565  
Uniformes Esportivos                          0.009870

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                    
Gabinete do Secretário                                    299.966473   
Diretoria Regional de Educação - Penha                      0.017870   
Diretoria Regional de Educação  Capela do Socorro           0.015924   
Diretoria Regional de Educação - Ipiranga                   0.013064   
Diretoria Regional de Educação - Santo Amaro                0.011850   

                                                   valLiquidado  valPagoTotal  
txtDescricaoUnidade                                                            
Gabinete do Secretário                               101.774629    203.592974  
Diretoria Regional de Educação - Penha                 0.017870      0.017870  
Diretoria Regional de Educação  Capela do Socorro      0.015924      0.015924  
Diretoria Regional de Educação - Ipiranga              0.005071      0.013064  
Diretoria Regional de Educação - Santo Amaro           0.011850      0.011850

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          300.02518    101.825344    203.651681

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              300.02518    101.825344    203.651681

valTotalEmpenhado  \
txtRazaoSocial                                                               
EBN COMERCIO IMPORTACAO E EXPORTACAO S/A                        107.089565   
NILCATEX TEXTIL LTDA                                             94.554172   
BRINK MOBIL EQUIPAMENTOS EDUCACIONAIS LTDA                       38.947337   
R.R.INDUSTRIA E COMERCIO DE MALHAS LTDA                          19.607706   
LT GLOBAL COMERCIO E SERVIÇOS EIRELI - ME                        18.161577   
LOTUS COMERCIO LTDA - ME                                         16.330650   
BRASILSUL INDUSTRIA E COMERCIO LTDA - EPP                         3.799922   
PLANETA EDUCACIONAL COMERCIO E CONFECCAO LTDA                     0.598229   
SPEZIA COMERCIAL DE MATERIAIS E SUPRIMENTOS EIRELI - ME           0.016258   
GIMED CONFECÇÕES HOSPITALARES LTDA - EPP                          0.008000   
PERSIANAS NOVA AMERICA LTDA                                       0.007997   
JOÃO ROMERA MORENO INFORMÁTICA - ME                               0.007992   
ORION VISION - COMERCIAL LTDA - EPP                               0.007926   
HELDE EWERTON ALMEIDA DE AZEVEDO 05612426402                      0.006990   
LUZIÂNIA COMÉRCIO E SERVIÇOS EIRELI - EPP                         0.005164   
FERNANDO UNIFORMES EIRELI - EPP                                   0.005071   
GHC UNIFORMES PROFISSIONAIS LTDA - EPP                            0.002880   
THONY PRINT EDITORA GRAFICA LTDA - ME                             0.867742   

                                                         valLiquidado  \
txtRazaoSocial                                                          
EBN COMERCIO IMPORTACAO E EXPORTACAO S/A                    36.572437   
NILCATEX TEXTIL LTDA                                        24.173376   
BRINK MOBIL EQUIPAMENTOS EDUCACIONAIS LTDA                  19.286998   
R.R.INDUSTRIA E COMERCIO DE MALHAS LTDA                      9.709875   
LT GLOBAL COMERCIO E SERVIÇOS EIRELI - ME                    6.253990   
LOTUS COMERCIO LTDA - ME                                     4.312548   
BRASILSUL INDUSTRIA E COMERCIO LTDA - EPP                    1.240188   
PLANETA EDUCACIONAL COMERCIO E CONFECCAO LTDA                0.215644   
SPEZIA COMERCIAL DE MATERIAIS E SUPRIMENTOS EIRELI - ME      0.016258   
GIMED CONFECÇÕES HOSPITALARES LTDA - EPP                     0.008000   
PERSIANAS NOVA AMERICA LTDA                                  0.007997   
JOÃO ROMERA MORENO INFORMÁTICA - ME                          0.000000   
ORION VISION - COMERCIAL LTDA - EPP                          0.007926   
HELDE EWERTON ALMEIDA DE AZEVEDO 05612426402                 0.006990   
LUZIÂNIA COMÉRCIO E SERVIÇOS EIRELI - EPP                    0.005164   
FERNANDO UNIFORMES EIRELI - EPP                              0.005071   
GHC UNIFORMES PROFISSIONAIS LTDA - EPP                       0.002880   
THONY PRINT EDITORA GRAFICA LTDA - ME                        0.000000   

                                                         valPagoTotal  
txtRazaoSocial                                                         
EBN COMERCIO IMPORTACAO E EXPORTACAO S/A                    72.334200  
NILCATEX TEXTIL LTDA                                        48.606697  
BRINK MOBIL EQUIPAMENTOS EDUCACIONAIS LTDA                  38.947337  
R.R.INDUSTRIA E COMERCIO DE MALHAS LTDA                     19.607706  
LT GLOBAL COMERCIO E SERVIÇOS EIRELI - ME                   12.450629  
LOTUS COMERCIO LTDA - ME                                     8.613858  
BRASILSUL INDUSTRIA E COMERCIO LTDA - EPP                    2.621697  
PLANETA EDUCACIONAL COMERCIO E CONFECCAO LTDA                0.401277  
SPEZIA COMERCIAL DE MATERIAIS E SUPRIMENTOS EIRELI - ME      0.016258  
GIMED CONFECÇÕES HOSPITALARES LTDA - EPP                     0.008000  
PERSIANAS NOVA AMERICA LTDA                                  0.007997  
JOÃO ROMERA MORENO INFORMÁTICA - ME                          0.007992  
ORION VISION - COMERCIAL LT

txtObjetoContrato
361                                                                                   Aquisição de tecidos
4689                                                                   INSTALAÇÃO E  CONFECÇÃO DE CORTINAS
4721                                                                         Aquisição de uniforme escolar
4793                                                            Aquisição de uniforme escolar lote 04 e 06
4846                                                                     Aquisição de kit uniforme escolar
4986                                                                        aquisição de camiseta e colete
8353                                        CONFECÇÃO DE CAMISETAS PARA O TORNEIO DE XADREZ – DRE IPIRANGA
9311                                               AQUISIÇÃO DE KITS DE UNIFORME ESCOLAR LOTES 01, 03 E 05
9314                                               Aquisição de Kits de uniforme escolar lotes 01, 03 e 05
9324                                               Aquisição de kits de uniforme escolar lotes 01, 03 e 05
9586                                                   Aquisição de kits de uniforme escolar lotes 04 e 06
14713                                      Contratação de empresa especializada em reformas de colchonetes
34040  DL- Serviços para confecção de material de apoio ao evento Clube do Xadrez, Movimento Educativo ...
40009                                                                 Aquisição de Kit de Uniforme Escolar
40057                                                                    AQUISIÇÃO DE KIT UNIFORME ESCOLAR
40096                                                                Aquisição de Kit de Uniforme Escolar 
46696                                                aquisição de camisetas e polos para torneio de xadrez
46793  DL- Aquisição de materiais e serviços para os Eventos FESTGIN, Movimento Educativo de Xadrez e T...
47089                                                                               AQUISIÇÃO DE BABADORES
52359                                 AQUISIÇÃO DE TOUCA DESCARTÁVEL, ATRAVES DA ATA DE RP135/2015  SMS-G.
53344                                                                CONFECÇÃO  DE COLETES, LONAS E XADREZ
57483                                                AQUISIÇÃO DE KITS DE UNIFORME ESCOLAR - LOTES 04 E 06
59456                               Aquisição de kits de material escolar individual lotes 01, 02, 03 e 04
59485                                                        Aquisição de kits de uniforme escolar lote 02

## 4.2. Materiais

#### (escolares, esportivos, educativos, didáticos, artísticos... como subdividir?)

In [604]:
materiais_filter = (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('materia', case=False))
    &
    (~empenhos_df['txtDescricaoItemDespesa'].str.contains('comun', case=False))
    &
    (~empenhos_df['txtDescricaoItemDespesa'].str.contains('uniforme', case=False))
)
materiais = (empenhos_df[materiais_filter])
empenhos_df.loc[materiais_filter, 'cat_1'] = 'uniforme_materiais'
empenhos_df.loc[materiais_filter, 'cat_2'] = 'materiais'
groupSum(materiais)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          58.755042     26.113732   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     55.646292

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             58.755042     26.113732     55.646292

valTotalEmpenhado  \
txtDescricaoElemento                                                     
Material, Bem ou Serviço para Distribuição Gratuita          47.821169   
Material de Consumo                                          10.783596   
Despesas de Exercícios Anteriores                             0.150277   

                                                     valLiquidado  \
txtDescricaoElemento                                                
Material, Bem ou Serviço para Distribuição Gratuita     21.005472   
Material de Consumo                                      4.957983   
Despesas de Exercícios Anteriores                        0.150277   

                                                     valPagoTotal  
txtDescricaoElemento                                               
Material, Bem ou Serviço para Distribuição Gratuita     45.638596  
Material de Consumo                                      9.857419  
Despesas de Exercícios Anteriores                        0.150277

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 58.755042     26.113732     55.646292

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                  
Material Escolar                                             47.743602   
Material Educativo                                            3.883992   
Materiais Didáticos                                           2.476033   
Diversos Materiais de Limpeza e Higienização                  1.362784   
Diversos Materiais de Cama, Mesa e Banho                      0.875004   
Diversos Materiais de Expediente                              0.412113   
Material Esportivo                                            0.207774   
Diversos Materiais Farmacológicos                             0.187762   
Outros Materiais de Consumo                                   0.150277   
Materiais para Impressão e Encadernação                       0.671882   
Diversos Materiais Elétricos e Eletrônicos                    0.109332   
Diversos Materiais de Proteção e Segurança                    0.095710   
Material de Proteção e Segurança de Pessoas                   0.084674   
Material Médico-Hospitalar                                    0.077567   
Oxigênio Industrial, Acetileno e Outros Materiais             0.132571   
Diversos Materiais de Copa e Cozinha                          0.068489   
Diversos Materiais Bibliográficos Não Imobilizáveis           0.058830   
Diversos Materiais de Acondicionamento e Embalagens           0.032493   
Materiais para Desenho, Topografia e Cartografia              0.028355   
Diversos Materiais de Sinalização Visual e Afins              0.025747   
Diversos Materiais para Manutenção de Bens Imóveis            0.015373   
Diversos Materiais Hospitalares                               0.015233   
Materiais para Montagem de Exposição                          0.007991   
Diversos Materiais para Manutenção de Bens Móveis             0.007955   
Diversos Materiais para Uso na Área de Informática            0.007694   
Diversos Materiais Odontológicos                              0.006948   
Materiais para Pintura e Acabamento                           0.004868   
Diversos Materiais Festividades e Homenagens                  0.001048   
Materiais Fotográficos                                        0.000499   
Diversos Materiais Químicos                                   0.000607   
Material de Proteção e Segurança de Bens Públicos             0.000378   
Diversos Materiais para Áudio, Vídeo e Foto                   0.001455   

                                                     valLiquidado  \
txtDescricaoItemDespesa                                             
Material Escolar                                        20.931055   
Material Educativo                                       0.302317   
Materiais Didáticos                                      2.040071   
Diversos Materiais de Limpeza e Higienização             0.871918   
Diversos Materiais de Cama, Mesa e Banho                 0.402524   
Diversos Materiais de Expediente                         0.360387   
Material Esportivo                                       0.155505   
Diversos Materiais Farmacológicos                        0.109750   
Outros Materiais de Consumo                              0.150277   
Materiais para Impressão e Encadernação                  0.142865   
Diversos Materiais Elétricos e Eletrônicos               0.105353   
Diversos Materiais de Proteção e Segurança               0.095710   
Material de Proteção e Segurança de Pessoas              0.084674   
Material Médico-Hospitalar                               0.074417   
Oxigênio Industrial, Acetileno e Outros Materiais        0.069719   
Diversos Materiais de Copa e Cozinha                     0.068489   
Diversos Materiais Bibliográficos Não Imobilizáveis      0.001230   
Diversos Materiais de Acondicionamento e Embalagens      0.032493   
Materiais para Desenho, Topografia e Cartografia         0.028355   
Diversos Materiais de Sinalização Visual e Afins         0.025653   
Diversos Materiais

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Gabinete do Secretário                                          55.147769   
Diretoria Regional de Educação  Capela do Socorro                0.561995   
Diretoria Regional de Educação - Penha                           0.348548   
Diretoria Regional de Educação - Jaçanã/Tremembé                 0.344580   
Diretoria Regional de Educação - Campo Limpo                     0.321241   
Diretoria Regional de Educação - São Miguel                      0.557414   
Diretoria Regional de Educação - Ipiranga                        0.270690   
Diretoria Regional de Educação - São Mateus                      0.258059   
Diretoria Regional de Educação - Butantã                         0.246324   
Diretoria Regional de Educação - Guaianases                      0.196260   
Diretoria Regional de Educação - Santo Amaro                     0.132567   
Diretoria Regional de Educação - Pirituba                        0.172685   
Diretoria Regional de Educação - Freguesia/Brasilândia           0.096355   
Diretoria Regional de Educação - Itaquera                        0.098168   
Departamento de Alimentação Escolar                              0.002387   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Gabinete do Secretário                                     23.660507   
Diretoria Regional de Educação  Capela do Socorro           0.542368   
Diretoria Regional de Educação - Penha                      0.345548   
Diretoria Regional de Educação - Jaçanã/Tremembé            0.232654   
Diretoria Regional de Educação - Campo Limpo                0.133224   
Diretoria Regional de Educação - São Miguel                 0.306702   
Diretoria Regional de Educação - Ipiranga                   0.041031   
Diretoria Regional de Educação - São Mateus                 0.138259   
Diretoria Regional de Educação - Butantã                    0.236285   
Diretoria Regional de Educação - Guaianases                 0.121262   
Diretoria Regional de Educação - Santo Amaro                0.118212   
Diretoria Regional de Educação - Pirituba                   0.097073   
Diretoria Regional de Educação - Freguesia/Brasilândia      0.094152   
Diretoria Regional de Educação - Itaquera                   0.044067   
Departamento de Alimentação Escolar                         0.002387   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Gabinete do Secretário                                     52.407251  
Diretoria Regional de Educação  Capela do Socorro           0.544408  
Diretoria Regional de Educação - Penha                      0.345548  
Diretoria Regional de Educação - Jaçanã/Tremembé            0.339332  
Diretoria Regional de Educação - Campo Limpo                0.321236  
Diretoria Regional de Educação - São Miguel                 0.316511  
Diretoria Regional de Educação - Ipiranga                   0.261515  
Diretoria Regional de Educação - São Mateus                 0.253259  
Diretoria Regional de Educação - Butantã                    0.243174  
Diretoria Regional de Educação - Guaianases                 0.196260  
Diretoria Regional de Educação - Santo Amaro                0.132567  
Diretoria Regional de Educação - Pirituba                   0.127355  
Diretoria Regional de Educação - Freguesia/Brasilândia      0.094330  
Diretoria Regional de Educação - Itaquera                   0.061160  
Departamento de Alimentação Escolar                         0.002387

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          58.755042     26.113732     55.646292

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              58.755042     26.113732     55.646292

valTotalEmpenhado  \
txtRazaoSocial                                                                         
BRINK MOBIL EQUIPAMENTOS EDUCACIONAIS LTDA                                 28.010818   
ATAKA BRASIL COMERCIO E SERVIÇOS EIRELI                                     9.892844   
LOGPRESS SOLUCOES GRAFICAS LTDA                                             4.026539   
DUAL SYSTEM PRODUTOS E SERVIÇOS LTDA                                        3.523019   
GRAFICA PRINT INDUSTRIA E EDITORA LTDA                                      2.779470   
FUTURA COMERCIO DE MATERIAIS EDUCACIONAIS LTDA - EPP                        1.904316   
THONY PRINT EDITORA GRAFICA LTDA - ME                                       2.717415   
ONLINE PAPELARIA E INFORMATICA EIRELI - EPP                                 1.191670   
INDUSTRIA E COMERCIO COLCHOES ORTHOVIDA LTDA - EPP                          0.678929   
SPEZIA COMERCIAL DE MATERIAIS E SUPRIMENTOS EIRELI - ME                     0.540511   
PRIME STOP COMERCIAL LTDA - ME                                              0.377421   
MOMILLI COMERCIAL LTDA - EPP                                                0.574658   
INFO-SIG COMÉRCIO DE SUPRIMENTOS DE INFORMÁTICA LTDA.                       0.301925   
INNOVARY FUTURE COMERCIAL LTDA - ME                                         0.157742   
INDUSTRIA E COMERCIO DE COLCHOES POLAR LTDA                                 0.124355   
RELAFLEX INDUSTRIA E COMERCIO DE COLCHOES EIRELI - EPP                      0.106500   
MEDPOA COMERCIO DE MATERIAL HOSPITALAR LTDA                                 0.101206   
AMÉRICA SERVE LIMPEZA E SERVIÇOS LTDA.                                      0.097586   
FEIRA LIVRO COMERCIO LTDA                                                   0.089070   
COMERCIAL CENTER VALLE LTDA                                                 0.084009   
LUMINUS COMERCIAL ELETRICA LTDA - EPP                                       0.075000   
METALPLAY INDÚSTRIA E COMÉRCIO LTDA EPP                                     0.071267   
TERRÃO COMÉRCIO E REPRESENTAÇÕES EIRELI                                     0.063353   
TONI CARLOS PEREIRA COMERCIO DE LIVROS                                      0.061207   
PATRICIA C R MUCEDULA BRINQUEDOS PEDAGOGICOS ME                             0.056832   
AMAD-COMERCIO E TRANSPORTE DE GÁS LTDA - EPP                                0.107859   
IMPRENSA OFICIAL DO ESTADO S/A IMESP                                        0.054590   
CTIS TECNOLOGIA S.A.                                                        0.049812   
MAROUN SLEIMAN MOVEIS E COLCHOES LTDA - EPP                                 0.046956   
ML RODRIGUES COMERCIAL LTDA. - ME                                           0.046176   
...                                                                              ...   
SANDRA REGINA MIQUE DA SILVA - ME                                           0.000750   
JOSINALDO EPIFANIO DA SILVA ME                                              0.000735   
JOAO MATOS DA SILVA 07555612879                                             0.000700   
AGUIA COMERCIO DE EQUIPAMENTOS EIRELI - ME                                  0.000684   
MED SHAPE COMERCIO E PRODUTOS PARA SAUDE EIRELI                             0.000594   
R SUPRIMENTOS LTDA-ME                                                       0.000559   
JOCEAN INDUSTRIA GRAFICA LTDA - ME                                          0.000555   
CKW ELECTRIC INDUSTRIA E COMERCIO DE MATERIAL ELETRICO LTDA - EPP           0.000533   
BSI BRASIL SOLUCOES INTELIGENTES LTDA-ME                                    0.000509   
IDEAL INDUSTRIA E COMERCIO DE MATERIAIS ELETRICOS EIRELI - EPP              0.000489   
RICARDO DOS SANTOS MOTTA 42365546587                                        0.000469   
JEAN CARLO SIQUEIRA 40227943805                                             0.000453   
LUCRATT COMER CIO E TURISMO LTDA - ME                                       0.000452   
IDPROMO COMERCIAL E

txtObjetoContrato
352                 DL- Aquisição de materiais de Papelaria para o RECREIO NAS FÉRIAS, edição janeiro/2018
368                      Materiais de higiene e saúde para o uso com os alunos com necessidades especiais.
379                                                                       Aquisição de brinquedos diversos
451                                            Aquisição de cartazes para divulgação do Recreio nas Férias
570                                              DL- RECREIO NAS FÉRIAS - Aquisição de Brinquedos diversos
578                                                               AQUISIÇÃO DE FRALDAS PARA USO NOS CEI'S 
596                                 LOTE DE MATERIAL PEDAGÓGICO PARA O PROGRMA RECREIO NAS FÉRIAS JAN-2018
602                                      lote de material artístico RECREIO NAS FÉRIAS-EDIÇÃO DE JAN 2018 
693                                           AQUISIÇÃO DE MATERIAIS ESPORTIVOS  PARA O RECREIO NAS FÉRIAS
883                                                               Impressão dos CADERNOS DA CIDADE - ALUNO
988                                                 DL- RECREIO NAS FÉRIAS - Aquisição de Jogos Educativos
999                              AQUISIÇÃO DE MATERIAL DIDÁTICO - RECREIO NAS FÉRIAS - EDIÇÃO JANEIRO/2018
1111                                    Aquisição de 100 colchonetes de repouso através da Ata 01/SME/2017
1131                                                                        Aquisição de garrafas térmicas
1422   AQUISIÇÃO DE LUVAS DESCARTAVÉIS, CONFORME ATA DE RP 41/SME/2016 - VOLPI DISTRIBUIDORA DE DROGAS ...
1437   AQUISIÇÃO DE LENÇOIS PARA MACA, CONFORME ATA DE RP, 43/SME/2016 - BEM MED COMERCIO ATACADISTA DE...
1438   AQUISIÇÃO DE ÁLCOOL GEL, CONFORME ATA DE RP 40/SME/2016 - MEDPOA COMERCIO DE MATERIAL HOSPITALAR...
2834                                                                    Aquisição de materiais de elétrica
3331   Aquisição de Gás Liquefeito de Petróleo - G.L.P., Botijão de 13KG e Cilindro de 45Kg, através da...
3416                                                                              AQUISIÇÃO DE COLCHONETES
3506   contratação através de dispensa de licitação a empresa Innovary Future Comercial Ltda - ME, insc...
3532   contratação através de dispensa de licitação a empresa Spezia Comercial de Materiais e Supriment...
3550                                     AQUISIÇÃO DE MATERIAIS DE CONSUMO - RECREIO NAS FÉRIAS JULHO/2017
3700                                 AQUISIÇÃO DE MATERIAL DIDÁTICO - RECREIO NAS FÉRIAS EDIÇÃO JULHO/2017
3727                       AQUISIÇÃO DE MATERIAL DIDÁTICO - RECREIO NAS FÉRIAS-EDIÇÃO JULHO/2017 - ITEM 11
3801                             Aquisição de Material Esportivo - Recreio nas Férias - Edição Julho/2017.
4028                                                 AQUISIÇÃO DE MATERIAL DE EXPEDIENTE I - EMPRESA GHAIA
4060                                          AQUISIÇÃO DE MATERIAL DE EXPEDIENTE II - EMPRESA RT COMÉRCIO
4064                          AQUISIÇÃO DE MATERIAL DE EXPEDIENTE - CORDÃO PARA CRACHÁ - EMPRESA ID PROMO 
4111                                                 AQUISIÇÃO DE MATERIAL DE EXPEDIENTE IV - EMPRESA SLIM
...                                                                                                    ...
53847                                                         MATERIAL ESPORTIVO PARA O RECREIO NAS FERIAS
53909                                                      MATERIAL DE PAPELARIA PARA O RECREIO NAS FÉRIAS
53912  SP/SR - AQUISIÇÃO DE MATERIAL DE EXPEDIENTE PARA O PROGRAMA RECREIO NAS FÉRIAS - COTAÇÃO Nº 017/...
53966  contratação através de dispensa de licitação a empresa Spezia Comercial de Materiais e Supriment...
54125                                 Aquisição de Jogos Educativos para o Recreio nas Férias - Julho/2017
54149                                                             AQUISIÇÃO DE ROLOS DE ALGODÃO HIDRÓFILO.
54157                  

# 5. Parcerias

In [605]:
parcerias_filter = (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('convênio', case=False))
    &
    ~(empenhos_df['txtDescricaoItemDespesa'].str.contains('qualificação profissional', case=False))
    &
    ~(empenhos_df['txtDescricaoItemDespesa'].str.contains('conferências', case=False))
)
parcerias = (empenhos_df[parcerias_filter])
empenhos_df.loc[parcerias_filter, 'cat_1'] = 'parcerias'
# empenhos_df.loc[parcerias_filter, 'cat_2'] = ''
groupSum(parcerias)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação        2292.424092   2004.240927   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação   2013.787685

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes           2292.424092   2004.240927   2013.787685

valTotalEmpenhado  \
txtDescricaoElemento                                                
Outros Serviços de Terceiros - Pessoa Jurídica        2292.424092   

                                                valLiquidado  valPagoTotal  
txtDescricaoElemento                                                        
Outros Serviços de Terceiros - Pessoa Jurídica   2004.240927   2013.787685

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal               2283.978007   2001.647192   2011.023143
Transferências Federais            8.446086      2.593735      2.764542

valTotalEmpenhado  valLiquidado  \
txtDescricaoItemDespesa                                                         
Convênio - Creche                                   2230.700574   1955.371328   
Convênios - Alfabetização, Educação e Outros          46.247443     40.399999   
Convênios - Portadores de Deficiência                 15.476076      8.469600   

                                              valPagoTotal  
txtDescricaoItemDespesa                                     
Convênio - Creche                              1964.544610  
Convênios - Alfabetização, Educação e Outros     40.655594  
Convênios - Portadores de Deficiência             8.587481

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Diretoria Regional de Educação - Campo Limpo                   211.128657   
Diretoria Regional de Educação - Guaianases                    273.353338   
Diretoria Regional de Educação - São Miguel                    191.131776   
Diretoria Regional de Educação - Pirituba                      173.658696   
Diretoria Regional de Educação - Freguesia/Brasilândia         193.370990   
Diretoria Regional de Educação - Ipiranga                      162.784893   
Diretoria Regional de Educação - Itaquera                      185.470959   
Diretoria Regional de Educação - Penha                         149.866191   
Diretoria Regional de Educação - São Mateus                    148.360836   
Diretoria Regional de Educação - Santo Amaro                   117.123047   
Diretoria Regional de Educação - Jaçanã/Tremembé               118.685536   
Diretoria Regional de Educação - Capela do Socorro             103.449359   
Diretoria Regional de Educação  Capela do Socorro               88.768512   
Diretoria Regional de Educação - Butantã                        90.626633   
Gabinete do Secretário                                          84.644668   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Diretoria Regional de Educação - Campo Limpo              198.508353   
Diretoria Regional de Educação - Guaianases               195.805506   
Diretoria Regional de Educação - São Miguel               187.042496   
Diretoria Regional de Educação - Pirituba                 167.766596   
Diretoria Regional de Educação - Freguesia/Brasilândia    161.123885   
Diretoria Regional de Educação - Ipiranga                 157.419697   
Diretoria Regional de Educação - Itaquera                 156.606269   
Diretoria Regional de Educação - Penha                    142.346145   
Diretoria Regional de Educação - São Mateus               118.086611   
Diretoria Regional de Educação - Santo Amaro              111.536157   
Diretoria Regional de Educação - Jaçanã/Tremembé          109.266639   
Diretoria Regional de Educação - Capela do Socorro         87.027545   
Diretoria Regional de Educação  Capela do Socorro          81.217267   
Diretoria Regional de Educação - Butantã                   79.185193   
Gabinete do Secretário                                     51.302568   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Diretoria Regional de Educação - Campo Limpo              199.366757  
Diretoria Regional de Educação - Guaianases               195.783704  
Diretoria Regional de Educação - São Miguel               187.524018  
Diretoria Regional de Educação - Pirituba                 167.828934  
Diretoria Regional de Educação - Freguesia/Brasilândia    161.123885  
Diretoria Regional de Educação - Ipiranga                 157.556162  
Diretoria Regional de Educação - Itaquera                 156.914577  
Diretoria Regional de Educação - Penha                    142.346145  
Diretoria Regional de Educação - São Mateus               118.126438  
Diretoria Regional de Educação - Santo Amaro              111.755805  
Diretoria Regional de Educação - Jaçanã/Tremembé          109.273212  
Diretoria Regional de Educação - Capela do Socorro         87.027545  
Diretoria Regional de Educação  Capela do Socorro          81.367174  
Diretoria Regional de Educação - Butantã                   79.189233  
Gabinete do Secretário                                     58.604096

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes        2292.424092   2004.240927   2013.787685

valTotalEmpenhado  \
txtModalidadeAplicacao                                                          
Transferências a Instituições Privadas sem Fins Lucrativos        2292.424092   

                                                            valLiquidado  \
txtModalidadeAplicacao                                                     
Transferências a Instituições Privadas sem Fins Lucrativos   2004.240927   

                                                            valPagoTotal  
txtModalidadeAplicacao                                                    
Transferências a Instituições Privadas sem Fins Lucrativos   2013.787685

valTotalEmpenhado  \
txtRazaoSocial                                                                                                         
SOCIEDADE BENEFICIENTE EQUILIBRIO DE INTERLAGOS                                                            42.737749   
CRUZADA PRO INFANCIA                                                                                       33.450280   
SPDM-ASSOCIAÇÃO PAULISTA PARA O DESENVOLVIMENTO DA MEDICINA                                                32.364774   
CENTRO SOCIAL NOSSA SENHORA DO BOM PARTO                                                                   28.229937   
CARITAS DIOCESANA DE CAMPO LIMPO-CDCL                                                                      23.977510   
UNAS - UNIAO DE NUCLEOS ASSOCIACOES DOS MORADORES DE HELIOPOLIS E REGIAO                                   22.568385   
INSTITUTO CRIANÇA CIDADÂ                                                                                   18.914968   
CENTRO DE ASSISTÊNCIA E PROMOÇÃO SOCIAL NOSSO LAR                                                          20.532360   
SOCIEDADE BENEFICENTE SÃO CAMILO                                                                           20.752715   
C.A.S.A.S. - CENTRO DE APOIO A SAUDE E ASSISTENCIA SOCIAL                                                  16.627836   
ASSOCIAÇÃO SÃO SABAS DE FILANTROPIA                                                                        15.965346   
SOCIEDADE EDUCATIVA E BENEFICENTE ESTRELA DA ESPERANÇA                                                     16.445365   
CEDEJI - CENTRO EDUCACIONAL DE DESENVOLVIMENTO JUVENIL E INFANTIL                                          14.837746   
ASSOCIAÇÃO CEDRO DO LIBANO DE PROTEÇÃO À INFÂNCIA                                                          12.928359   
ASSOCIAÇÃO SEARA NORTE                                                                                     14.273992   
ICEDEH-INSTITUTO EDUCACIONAL E DE DEFESA DOS DIREITOS HUMANOS - CORA CORALINA                              12.380065   
OBRA ASSISTENCIAL NOSSA SENHORA DO O                                                                       12.514542   
NUCLEO ASSISTENCIAL FRATERNO                                                                               15.484831   
LIGA DAS SENHORAS CATOLICAS DE SÃO PAULO                                                                   12.743511   
INSTITUTO BENEFICENTE PERSIO GUIMARAES AZEVEDO                                                             10.568354   
ASSOCIAÇÃO ÁGUAS MARINHA                                                                                   11.705560   
ASSOCIAÇÃO CENTRO SOCIAL BROOKLIN PAULISTA                                                                 10.593808   
ACAO SOCIAL COMUNITARIA DO LAGEADO JOILSON DE JESUS                                                        15.076075   
INSTITUTO EDUCACIONAL PAIS E FILHOS                                                                         9.393201   
GREMIO AMIGOS DIAS FELIZES                                                                                  9.349912   
GALPÃO ATRIA BRASIL                                                                                        11.906963   
IESP - INSTITUTO EDUCAR DE SÃO PAULO                                                                       10.435716   
INSTITUTO CEM POR CENTO SOCIAL                                                                             10.418738   
ASSOCIAÇÃO EVANGELICA BENEFICENTE                                                                           9.098005   
ACRIA - ASSOCIAÇÃO AMIGA DA CRIANÇA E DO ADOLESCENTE                                                       10.221343   
...                                                                                                              ...   
ASSOCIAÇÃO ANJOS DA PAZ DA VILA SANTISTA                                                                    0.024243   
A ALTERNATIVA ASSOC

txtObjetoContrato
0                                                   Contratação de Agente Recreativo - Edição Janeiro 2017
1                                                               RECREIO NAS FÉRIAS JANEIRO / 2017 - DRE/IQ
2                                      2º REPASSE PTRF/2017 – DRE-G – CUSTEIO – APM – CEU EMEF LAJEADO  \t
3      Celebração do Termo de Convênio nº 013/DRE-PJ/2015-RP para atendimento de 178 crianças, sendo 84...
4                                                                                                      NaN
5                                                PRORROGAÇÃO DE VIGÊNCIA- CEI EUGêNIO FRANCISCO DE SANTANA
9                                Repasse de Recursos do PNAE para o CEI SANTA ANGELA- CÓD. INEP 35181560\n
12     \r\nCONTRATAÇÃO DE AGENTES DE RECREAÇÃO PARA O RECREIO NAS FÉRIAS JANEIRO DE 2017 NO PERÍODO DE ...
15                                                                   CEI PRIMEIRO LAPIS - JANEIRO A AGOSTO
20                                                    PRORROGAÇÃO DE VIGÊNCIA - CEI VIRTUDE DA CRIANÇA III
23                                                                          CEI ADALGIZA COELHO DOS SANTOS
24     Repasses de recursos à APM, de acordo com a Lei Federal 9394/1996 e Portarias da SME indicando o...
27                                                               CELEBRAÇÃO DE CONVÊNIO- CEI ABC AURORA II
28                                                 CELEBRAÇÃO DE CONVÊNIO- CEI JARDIM IPANEMA I - 29/05/17
32                                 Repasse de Recursos do PNAE para o CEI AVES GALHANI- CÓD. INEP 35305534
33                                                     TERMO DE COLABORAÇÃO- CEI VITÓRIA- EM CONTINUIDADE 
34                                                              TERMO DE COLABORAÇÃO - CEI FLOR DO ORIENTE
37                                                               TERMO DE COLABORAÇÃO- CEI GALPÃO ATRIA II
38                                            CELEBRAÇÃO DE TERMO DE COLABORAÇÃO- CEI REINO DOS PEQUENINOS
39                                                                CELEBRAÇÃO DE PARCERIA- CEI TRINDADE III
42                                                     CELEBRAÇÃO DE PARCERIA- CEI ESPAÇO DA COMUNIDADE VI
43                                                               CELEBRAÇÃO DE PARCERIA- CEI MARAVILHA III
46                                  CELEBRAÇÃO TERMO DE COLABORAÇÃO/PARCERIA - CEI CIDADE A.E. CARVALHO II
50                 TERMO DE COLABORAÇÃO PARA A MANUTENÇÃO DO CEI PIRAJUCARA NOS TERMOS DA PORTARIA 4548/17
55                                                                RECREIO NAS FÉRIAS JULHO / 2017 - DRE/IQ
59     Manutenção do CEI Vovó Joaninha, para atendimento de 70 crianças de 0 a 3 anos, sendo 25 de berç...
63     PROGRAMA RECREIO NAS FÉRIAS - JANEIRO/2017 - DE ACORDO COM O EDITAL DE CREDENCIAMENTO Nº 004/201...
64                          Contratação de empresa especializada em correção de redação - Simulado do ENEM
65                   520.000 Kg de Feijão Comum de Cores Carioca - Tipo 1 - ATA de RP nº 02/SME/DAE/2016\n
66     Aditamento contratual referente a prorrogação de vigência visando o atendimento a 74 crianças, s...
...                                                                                                    ...
52332                                                CONVENIO -CEI  BRILHO DO SOL V - CONTRATO EMERGENCIAL
52474                                                                   CELEBRAÇÃO DE CONVÊNIO/ CEI KAIRÓS
53212  Termo de Colaboração com a Organização da Sociedade Civil Instituto Criança Cidadã que tem por o...
53453                                                       Convênio Creche - CEI Salesiano Domingos Sávio
53949  AUTORIZO empresa Amazônia Ambiental Cons.Serv. e Constr. LTDA - ME - CNPJ nº 00.935.969/0001-54,...
54625                         CELEBRAÇÃO DE PARCERIA PARA ATENDIMENTO DE 114 CRIANÇAS, SENDO 0 DE BERÇARIO
55043                  

## 5.1. Convênios com creches

#### Checar filtro

In [606]:
creches_filter = parcerias_filter & (
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('Operação e Manutenção de CEIs e Creches da rede conveniada e outras mo', case=False))
)
creches = (empenhos_df[creches_filter])
empenhos_df.loc[creches_filter, 'cat_1'] = 'parcerias'
empenhos_df.loc[creches_filter, 'cat_2'] = 'creches'
groupSum(creches)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação        2228.235843   1954.064406   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação   1962.607936

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes           2228.235843   1954.064406   1962.607936

valTotalEmpenhado  \
txtDescricaoElemento                                                
Outros Serviços de Terceiros - Pessoa Jurídica        2228.235843   

                                                valLiquidado  valPagoTotal  
txtDescricaoElemento                                                        
Outros Serviços de Terceiros - Pessoa Jurídica   1954.064406   1962.607936

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal               2219.789757   1951.470672   1959.843394
Transferências Federais            8.446086      2.593735      2.764542

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoItemDespesa                                               
Convênio - Creche              2228.235843   1954.064406   1962.607936

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Diretoria Regional de Educação - Campo Limpo                   208.947509   
Diretoria Regional de Educação - Guaianases                    272.658228   
Diretoria Regional de Educação - São Miguel                    189.632871   
Diretoria Regional de Educação - Pirituba                      171.742631   
Diretoria Regional de Educação - Freguesia/Brasilândia         191.832897   
Diretoria Regional de Educação - Ipiranga                      162.083622   
Diretoria Regional de Educação - Itaquera                      184.584608   
Diretoria Regional de Educação - Penha                         149.310823   
Diretoria Regional de Educação - São Mateus                    147.244224   
Diretoria Regional de Educação - Santo Amaro                   116.346984   
Diretoria Regional de Educação - Jaçanã/Tremembé               118.394451   
Diretoria Regional de Educação - Capela do Socorro             101.587511   
Diretoria Regional de Educação  Capela do Socorro               87.260484   
Diretoria Regional de Educação - Butantã                        90.330234   
Gabinete do Secretário                                          36.278766   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Diretoria Regional de Educação - Campo Limpo              196.493778   
Diretoria Regional de Educação - Guaianases               195.139340   
Diretoria Regional de Educação - São Miguel               185.791027   
Diretoria Regional de Educação - Pirituba                 165.975216   
Diretoria Regional de Educação - Freguesia/Brasilândia    159.690220   
Diretoria Regional de Educação - Ipiranga                 156.809580   
Diretoria Regional de Educação - Itaquera                 155.914009   
Diretoria Regional de Educação - Penha                    141.828572   
Diretoria Regional de Educação - São Mateus               117.174850   
Diretoria Regional de Educação - Santo Amaro              110.812911   
Diretoria Regional de Educação - Jaçanã/Tremembé          109.012656   
Diretoria Regional de Educação - Capela do Socorro         85.465696   
Diretoria Regional de Educação  Capela do Socorro          80.222002   
Diretoria Regional de Educação - Butantã                   78.915637   
Gabinete do Secretário                                     14.818912   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Diretoria Regional de Educação - Campo Limpo              197.352182  
Diretoria Regional de Educação - Guaianases               195.117538  
Diretoria Regional de Educação - São Miguel               186.245709  
Diretoria Regional de Educação - Pirituba                 165.975216  
Diretoria Regional de Educação - Freguesia/Brasilândia    159.690220  
Diretoria Regional de Educação - Ipiranga                 156.942643  
Diretoria Regional de Educação - Itaquera                 156.196343  
Diretoria Regional de Educação - Penha                    141.828572  
Diretoria Regional de Educação - São Mateus               117.174850  
Diretoria Regional de Educação - Santo Amaro              110.981458  
Diretoria Regional de Educação - Jaçanã/Tremembé          109.012656  
Diretoria Regional de Educação - Capela do Socorro         85.465696  
Diretoria Regional de Educação  Capela do Socorro          80.336411  
Diretoria Regional de Educação - Butantã                   78.915637  
Gabinete do Secretário                                     21.372805

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes        2228.235843   1954.064406   1962.607936

valTotalEmpenhado  \
txtModalidadeAplicacao                                                          
Transferências a Instituições Privadas sem Fins Lucrativos        2228.235843   

                                                            valLiquidado  \
txtModalidadeAplicacao                                                     
Transferências a Instituições Privadas sem Fins Lucrativos   1954.064406   

                                                            valPagoTotal  
txtModalidadeAplicacao                                                    
Transferências a Instituições Privadas sem Fins Lucrativos   1962.607936

valTotalEmpenhado  \
txtRazaoSocial                                                                                     
SOCIEDADE BENEFICIENTE EQUILIBRIO DE INTERLAGOS                                        42.737749   
CRUZADA PRO INFANCIA                                                                   33.450280   
CENTRO SOCIAL NOSSA SENHORA DO BOM PARTO                                               28.229937   
CARITAS DIOCESANA DE CAMPO LIMPO-CDCL                                                  23.759583   
UNAS - UNIAO DE NUCLEOS ASSOCIACOES DOS MORADORES DE HELIOPOLIS E REGIAO               22.288221   
INSTITUTO CRIANÇA CIDADÂ                                                               18.914968   
CENTRO DE ASSISTÊNCIA E PROMOÇÃO SOCIAL NOSSO LAR                                      20.532360   
SOCIEDADE BENEFICENTE SÃO CAMILO                                                       20.622715   
ASSOCIAÇÃO SÃO SABAS DE FILANTROPIA                                                    15.965346   
C.A.S.A.S. - CENTRO DE APOIO A SAUDE E ASSISTENCIA SOCIAL                              14.353111   
SOCIEDADE EDUCATIVA E BENEFICENTE ESTRELA DA ESPERANÇA                                 16.445365   
CEDEJI - CENTRO EDUCACIONAL DE DESENVOLVIMENTO JUVENIL E INFANTIL                      14.837746   
ASSOCIAÇÃO CEDRO DO LIBANO DE PROTEÇÃO À INFÂNCIA                                      12.928359   
ASSOCIAÇÃO SEARA NORTE                                                                 14.273992   
ICEDEH-INSTITUTO EDUCACIONAL E DE DEFESA DOS DIREITOS HUMANOS - CORA CORALINA          12.380065   
OBRA ASSISTENCIAL NOSSA SENHORA DO O                                                   12.514542   
NUCLEO ASSISTENCIAL FRATERNO                                                           15.484831   
LIGA DAS SENHORAS CATOLICAS DE SÃO PAULO                                               12.691966   
INSTITUTO BENEFICENTE PERSIO GUIMARAES AZEVEDO                                         10.568354   
ASSOCIAÇÃO ÁGUAS MARINHA                                                               11.705560   
ASSOCIAÇÃO CENTRO SOCIAL BROOKLIN PAULISTA                                             10.593808   
ACAO SOCIAL COMUNITARIA DO LAGEADO JOILSON DE JESUS                                    15.076075   
INSTITUTO EDUCACIONAL PAIS E FILHOS                                                     9.393201   
GREMIO AMIGOS DIAS FELIZES                                                              9.349912   
GALPÃO ATRIA BRASIL                                                                    11.906963   
IESP - INSTITUTO EDUCAR DE SÃO PAULO                                                   10.435716   
INSTITUTO CEM POR CENTO SOCIAL                                                         10.418738   
ASSOCIAÇÃO EVANGELICA BENEFICENTE                                                       9.058178   
ACRIA - ASSOCIAÇÃO AMIGA DA CRIANÇA E DO ADOLESCENTE                                   10.221343   
FUNDAÇÃO COMUNIDADE DA GRAÇA                                                           10.350552   
...                                                                                          ...   
ASSOCIAÇÃO LIVRE DA TERCEIRA IDADE DA ZONA NORTE DE SÃO PAULO                           0.093131   
INSTITUTO EDUCACIONAL NOVA ALIANÇA                                                      0.151089   
INSTITUTO AÇÃO E PROTEÇÃO                                                               0.161030   
FRATERNIDADE FREI FREDERICO                                                             0.089981   
ASSOCIAÇÃO EDUCACIONAL PITAGORAS                                                        0.131185   
ASSOCIAÇÃO BENEFICENTE CAMINHO BRILHANTE                                                0.074561   
ASSOCIAÇÃO COMUNITÁRIA RENASCER DO JARDIM SÃO PEDRO                                     0.124526   
ASSOCIAÇÃO FAMILIA UNIDA EM CRISTO FUEC                                        

txtObjetoContrato
0                                                   Contratação de Agente Recreativo - Edição Janeiro 2017
1                                                               RECREIO NAS FÉRIAS JANEIRO / 2017 - DRE/IQ
2                                      2º REPASSE PTRF/2017 – DRE-G – CUSTEIO – APM – CEU EMEF LAJEADO  \t
3      Celebração do Termo de Convênio nº 013/DRE-PJ/2015-RP para atendimento de 178 crianças, sendo 84...
4                                                                                                      NaN
5                                                PRORROGAÇÃO DE VIGÊNCIA- CEI EUGêNIO FRANCISCO DE SANTANA
9                                Repasse de Recursos do PNAE para o CEI SANTA ANGELA- CÓD. INEP 35181560\n
12     \r\nCONTRATAÇÃO DE AGENTES DE RECREAÇÃO PARA O RECREIO NAS FÉRIAS JANEIRO DE 2017 NO PERÍODO DE ...
15                                                                   CEI PRIMEIRO LAPIS - JANEIRO A AGOSTO
20                                                    PRORROGAÇÃO DE VIGÊNCIA - CEI VIRTUDE DA CRIANÇA III
23                                                                          CEI ADALGIZA COELHO DOS SANTOS
24     Repasses de recursos à APM, de acordo com a Lei Federal 9394/1996 e Portarias da SME indicando o...
27                                                               CELEBRAÇÃO DE CONVÊNIO- CEI ABC AURORA II
28                                                 CELEBRAÇÃO DE CONVÊNIO- CEI JARDIM IPANEMA I - 29/05/17
32                                 Repasse de Recursos do PNAE para o CEI AVES GALHANI- CÓD. INEP 35305534
33                                                     TERMO DE COLABORAÇÃO- CEI VITÓRIA- EM CONTINUIDADE 
34                                                              TERMO DE COLABORAÇÃO - CEI FLOR DO ORIENTE
37                                                               TERMO DE COLABORAÇÃO- CEI GALPÃO ATRIA II
38                                            CELEBRAÇÃO DE TERMO DE COLABORAÇÃO- CEI REINO DOS PEQUENINOS
39                                                                CELEBRAÇÃO DE PARCERIA- CEI TRINDADE III
42                                                     CELEBRAÇÃO DE PARCERIA- CEI ESPAÇO DA COMUNIDADE VI
43                                                               CELEBRAÇÃO DE PARCERIA- CEI MARAVILHA III
46                                  CELEBRAÇÃO TERMO DE COLABORAÇÃO/PARCERIA - CEI CIDADE A.E. CARVALHO II
50                 TERMO DE COLABORAÇÃO PARA A MANUTENÇÃO DO CEI PIRAJUCARA NOS TERMOS DA PORTARIA 4548/17
55                                                                RECREIO NAS FÉRIAS JULHO / 2017 - DRE/IQ
59     Manutenção do CEI Vovó Joaninha, para atendimento de 70 crianças de 0 a 3 anos, sendo 25 de berç...
63     PROGRAMA RECREIO NAS FÉRIAS - JANEIRO/2017 - DE ACORDO COM O EDITAL DE CREDENCIAMENTO Nº 004/201...
64                          Contratação de empresa especializada em correção de redação - Simulado do ENEM
65                   520.000 Kg de Feijão Comum de Cores Carioca - Tipo 1 - ATA de RP nº 02/SME/DAE/2016\n
66     Aditamento contratual referente a prorrogação de vigência visando o atendimento a 74 crianças, s...
...                                                                                                    ...
50043                                                                   CONVÊNIO CEI TURMA DO BALÃO MÁGICO
50111                                                                               CEI DAMARIS CASTILHO I
50993  Celebração de Parceria em Continuidade , de acordo com a portaria 4548/2017, do Cei Noite Encant...
51059  ATENDIMENTO A CRIANÇAS NA FAIXA ETÁRIA DE 0 A 3 ANOS POR MEIO DE CRECHE/CENTRO DE EDUCAÇÃO INFAN...
51308                                                             TERMO DE COLABORAÇÃO - CEI BELEZINHA III
51646  CELEBRAÇÃO DE PARCERIA PARA ATENDIMENTO DE 113 CRIANÇAS NA FAIXA ETÁRIA DE 0 A 3 ANOS, SENDO 32 ...
51711  Atendimento por 

## 5.2. Educação especial

In [607]:
ed_especial_filter = parcerias_filter & (
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('Convênios para Atendimento de Crianças e Adolescentes com necessidades', case=False))
    |
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('Educação Especial', case=False))
)
ed_especial = (empenhos_df[ed_especial_filter])
empenhos_df.loc[ed_especial_filter, 'cat_1'] = 'parcerias'
empenhos_df.loc[ed_especial_filter, 'cat_2'] = 'ed_especial'
groupSum(ed_especial)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação           47.55023     36.483657   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     36.601538

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes              47.55023     36.483657     36.601538

valTotalEmpenhado  \
txtDescricaoElemento                                                
Outros Serviços de Terceiros - Pessoa Jurídica           47.55023   

                                                valLiquidado  valPagoTotal  
txtDescricaoElemento                                                        
Outros Serviços de Terceiros - Pessoa Jurídica     36.483657     36.601538

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                  47.55023     36.483657     36.601538

valTotalEmpenhado  valLiquidado  \
txtDescricaoItemDespesa                                                         
Convênios - Alfabetização, Educação e Outros          32.364774     28.047264   
Convênios - Portadores de Deficiência                 15.185455      8.436392   

                                              valPagoTotal  
txtDescricaoItemDespesa                                     
Convênios - Alfabetização, Educação e Outros     28.047264  
Convênios - Portadores de Deficiência             8.554274

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário           47.55023     36.483657     36.601538

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes           47.55023     36.483657     36.601538

valTotalEmpenhado  \
txtModalidadeAplicacao                                                          
Transferências a Instituições Privadas sem Fins Lucrativos           47.55023   

                                                            valLiquidado  \
txtModalidadeAplicacao                                                     
Transferências a Instituições Privadas sem Fins Lucrativos     36.483657   

                                                            valPagoTotal  
txtModalidadeAplicacao                                                    
Transferências a Instituições Privadas sem Fins Lucrativos     36.601538

valTotalEmpenhado  \
txtRazaoSocial                                                                                              
SPDM-ASSOCIAÇÃO PAULISTA PARA O DESENVOLVIMENTO DA MEDICINA                                     32.364774   
ASSOCIAÇÃO DE PAIS E AMIGOS DOS EXCEPCIONAIS DE SÃO PAULO                                        3.939519   
ASSOCIAÇÃO OBRAS SOCIAIS SANTA CRUZ                                                              0.891831   
ASSOCIAÇAO NANY APPLE EM BENEFICIO DO OBESO E CARENTE                                            0.943445   
AHIMSA ASSOC EDUC PARA MULT DEFIC                                                                0.795604   
INSTITUTO SEVERINO FABRIANI PARA CRIANÇAS SURDAS                                                 1.735683   
ASSOCIAÇÃO FILHAS DE SANTA MARIA DA PROVIDENCIA                                                  0.756604   
ADEFAV - CENTRO DE RECURSOS EM DEFICIENCIA MULTIPLA SURDOCEGUEIRA E DEFICIENCIA VISUAL           0.684021   
ASSOCIAÇÃO DA CASA DOS DEFICIENTES  DE ERMELINO MATARAZZO                                        0.595999   
CENTRO SOCIAL NOSSA SENHORA DA PENHA - CENHA                                                     0.459374   
CAMINHANDO NUCLEO DE EDUCAÇÃO E AÇÃO SOCIAL                                                      0.410467   
ASSOCIAÇÃO DE ASSISTÊNCIA A CRIANÇA DEFICIENTE                                                   0.999677   
INSTITUTO MATER DEI                                                                              0.275569   
LAR MÃE DO DIVINO AMOR                                                                           0.263433   
INST. EFORT ACAO SOCIAL, CUL.EDUC.P. DES.ENER.INF.M.AMB. REC.H.TELECOM                           0.432143   
CENTRO DE ACAO SOCIAL ESPACO LIVRE                                                               0.240206   
INSTITUICAO BENEFICENTE NOSSO LAR                                                                0.260157   
ASSOCIAÇÃO NOVA PROJETO EDUCAÇÃO E TRABALHO PARA PESSOA ESPECIAL                                 0.186335   
ASSOCIACAO BENEFICENTE GUAINUMBI                                                                 0.271216   
LARAMARA ASSOCIAÇÃO BRASILEIRA ASSISTÊNCIA DEFIC VISUAL                                          0.547947   
GRUPO BRASIL DE  APOIO AO SURDOCEGO E AO MULTIPLO DEFICIENTE SENSORIAL                           0.183750   
SHALOM LIGA ISRAELITA DO BRASIL                                                                  0.122733   
ASSOCIAÇÃO NOSSA ESCOLA                                                                          0.129823   
A ALTERNATIVA ASSOCIAÇÃO DE  ASSISTÊNCIA  AO EXCEPCIONAL                                         0.059918   

                                                                                        valLiquidado  \
txtRazaoSocial                                                                                         
SPDM-ASSOCIAÇÃO PAULISTA PARA O DESENVOLVIMENTO DA MEDICINA                                28.047264   
ASSOCIAÇÃO DE PAIS E AMIGOS DOS EXCEPCIONAIS DE SÃO PAULO                                   1.886311   
ASSOCIAÇÃO OBRAS SOCIAIS SANTA CRUZ                                                         0.658792   
ASSOCIAÇAO NANY APPLE EM BENEFICIO DO OBESO E CARENTE                                       0.638419   
AHIMSA ASSOC EDUC PARA MULT DEFIC                                                           0.598979   
INSTITUTO SEVERINO FABRIANI PARA CRIANÇAS SURDAS                                            0.576806   
ASSOCIAÇÃO FILHAS DE SANTA MARIA DA PROVIDENCIA                                             0.519410   
ADEFAV - CENTRO DE RECURSOS EM DEFICIENCIA MULTIPLA SURDOCEGUEIRA E DEFICIENCIA VISUAL      0.468102   
ASSOCIAÇÃO DA CASA DOS DEFICIENTES  DE ERMELINO MATARAZZO                                   0.416625   
CENTRO SOCIAL NOSSA SENHORA DA PENHA - CENHA                                                0.395203   
CAMIN

txtObjetoContrato
2238                                                                                                   NaN
8128                  CELEBRAÇÃO DE CONV. EDUCAÇÃO ESPECIAL - ASSOC. FILHAS DE SANTA MARIA DA PROVIDENCIA 
8297   CELEBRAÇÃO DE CONVÊNIO EDUC. ESPECIAL - INST. SEVERINO FABRIANI PARA VRIANÇAS SURDAS (29/04/2017...
16006                     CELEBRAÇÃO DE CONVÊNIO EM CONTINUIDADE - EDUCAÇÃO ESPECIAL INSTITURTO MATER DEI 
16017                          PAGTO MENSAL - INSTITUIÇÃO BENEFICENTE NOSSO LAR  (13/04/2017 À 31/12/2017)
16271                               CELEBRAÇÃO DE CONV. EM CONTINUIDADE - ADEFAV (20/04/2017 À 31/12/2017)
16478                                   CELEBRAÇÃO DE CONV. EM CONTINUIDADE - E.E. LAR MÃE DO DIVINO AMOR

## 5.3 EJA

In [608]:
eja_filter = parcerias_filter & (
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('Alfabetização de Jovens e Adultos', case=False))
)
eja = (empenhos_df[eja_filter])
empenhos_df.loc[eja_filter, 'cat_1'] = 'parcerias'
empenhos_df.loc[eja_filter, 'cat_2'] = 'eja'
groupSum(eja)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          11.937817     10.687166   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     10.942761

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             11.937817     10.687166     10.942761

valTotalEmpenhado  \
txtDescricaoElemento                                                
Outros Serviços de Terceiros - Pessoa Jurídica          11.937817   

                                                valLiquidado  valPagoTotal  
txtDescricaoElemento                                                        
Outros Serviços de Terceiros - Pessoa Jurídica     10.687166     10.942761

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 11.937817     10.687166     10.942761

valTotalEmpenhado  valLiquidado  \
txtDescricaoItemDespesa                                                         
Convênios - Alfabetização, Educação e Outros          11.825031     10.616516   
Convênio - Creche                                      0.112786      0.070650   

                                              valPagoTotal  
txtDescricaoItemDespesa                                     
Convênios - Alfabetização, Educação e Outros     10.872111  
Convênio - Creche                                 0.070650

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Diretoria Regional de Educação - Campo Limpo                     2.181148   
Diretoria Regional de Educação - Freguesia/Brasilândia           1.538093   
Diretoria Regional de Educação - São Miguel                      1.354749   
Diretoria Regional de Educação - São Mateus                      1.097055   
Diretoria Regional de Educação - Santo Amaro                     0.776063   
Diretoria Regional de Educação - Itaquera                        0.861663   
Diretoria Regional de Educação - Pirituba                        0.727280   
Diretoria Regional de Educação - Guaianases                      0.695110   
Diretoria Regional de Educação - Ipiranga                        0.633720   
Diretoria Regional de Educação - Penha                           0.541717   
Diretoria Regional de Educação - Capela do Socorro               0.416224   
Diretoria Regional de Educação  Capela do Socorro                0.527509   
Diretoria Regional de Educação - Butantã                         0.296400   
Diretoria Regional de Educação - Jaçanã/Tremembé                 0.291085   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Diretoria Regional de Educação - Campo Limpo                2.014575   
Diretoria Regional de Educação - Freguesia/Brasilândia      1.433665   
Diretoria Regional de Educação - São Miguel                 1.251469   
Diretoria Regional de Educação - São Mateus                 0.892205   
Diretoria Regional de Educação - Santo Amaro                0.723247   
Diretoria Regional de Educação - Itaquera                   0.692260   
Diretoria Regional de Educação - Pirituba                   0.623614   
Diretoria Regional de Educação - Guaianases                 0.666166   
Diretoria Regional de Educação - Ipiranga                   0.610117   
Diretoria Regional de Educação - Penha                      0.503922   
Diretoria Regional de Educação - Capela do Socorro          0.416224   
Diretoria Regional de Educação  Capela do Socorro           0.336165   
Diretoria Regional de Educação - Butantã                    0.269555   
Diretoria Regional de Educação - Jaçanã/Tremembé            0.253983   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Diretoria Regional de Educação - Campo Limpo                2.014575  
Diretoria Regional de Educação - Freguesia/Brasilândia      1.433665  
Diretoria Regional de Educação - São Miguel                 1.278309  
Diretoria Regional de Educação - São Mateus                 0.932032  
Diretoria Regional de Educação - Santo Amaro                0.774348  
Diretoria Regional de Educação - Itaquera                   0.718234  
Diretoria Regional de Educação - Pirituba                   0.685952  
Diretoria Regional de Educação - Guaianases                 0.666166  
Diretoria Regional de Educação - Ipiranga                   0.613519  
Diretoria Regional de Educação - Penha                      0.503922  
Diretoria Regional de Educação - Capela do Socorro          0.416224  
Diretoria Regional de Educação  Capela do Socorro           0.371663  
Diretoria Regional de Educação - Butantã                    0.273596  
Diretoria Regional de Educação - Jaçanã/Tremembé            0.260556

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          11.937817     10.687166     10.942761

valTotalEmpenhado  \
txtModalidadeAplicacao                                                          
Transferências a Instituições Privadas sem Fins Lucrativos          11.937817   

                                                            valLiquidado  \
txtModalidadeAplicacao                                                     
Transferências a Instituições Privadas sem Fins Lucrativos     10.687166   

                                                            valPagoTotal  
txtModalidadeAplicacao                                                    
Transferências a Instituições Privadas sem Fins Lucrativos     10.942761

valTotalEmpenhado  \
txtRazaoSocial                                                                                     
ASSOCIAÇÃO EDUCACIONAL E CULTURAL PADRE LUIZ SUTTER                                     0.720612   
SOCIEDADE AMIGOS  DISTRITO DE PERUS  SADIP                                              0.498359   
AVIB -  ASSOCIAÇÃO DE VOLUNTÁRIOS INTEGRADOS NO BRASIL                                  0.425335   
ASSOCIAÇÃO SÃO JUDAS TADEU E CENTRO COMUNITÁRIO DO JD. IBIRAPUERA                       0.420784   
CENTRO DE EDUCAÇÃO DA ZONA LESTE                                                        0.398305   
INSTITUTO SOCIAL SANTA LUCIA                                                            0.426844   
CETEAC  CENTRO DE ESTUDOS E TRABALHOS EM EDUCAÇÃO  ARTE E CULTURA                       0.289109   
ASSOC A CRIANCA ADOLES JOV. ICARAI                                                      0.270133   
UNAS - UNIAO DE NUCLEOS ASSOCIACOES DOS MORADORES DE HELIOPOLIS E REGIAO                0.280163   
ASSOCIACAO CANTAREIRA                                                                   0.290912   
CENTRO COMUNITARIO JARDIM AUTODROMO                                                     0.228574   
ASSOCIAÇÃO  COMUNITARIA JARDIM IDEAL                                                    0.382688   
ACEB-ASSOCIAÇÃO CULTURAL ESPORTIVA E BENEF.DE VILA NOVA CACHOEIRINHA                    0.245024   
CLUBE DE MAES RAIOS DE LUAR                                                             0.306612   
CARITAS DIOCESANA DE CAMPO LIMPO-CDCL                                                   0.217927   
ASSOCIACAO TRÊS IRMAOS                                                                  0.204331   
INSTITUTO DE EDUCACAO E CULTURA ALUTHA                                                  0.314505   
SOCIEDADE SANTOS MARTIRES                                                               0.216452   
SOCIEDADE AMIGA E ESPORTIVA JARDIM COPACABANA                                           0.195237   
SOCIEDADE AMIGOS DE VILA MARA JARDIM MAIA E VILAS ADJACENTES                            0.180088   
OBRAS SOCIAIS DE VISTA ALEGRE                                                           0.145456   
UNIAO MORADORES DO JARDIM ANTONIETA, PQ. SANTO ANTONIO E ADJACÊNCIAS                    0.145456   
CENTRO POP. DEFESA DOS D. H.  FREI TITO DE ALENCAR LIMA                                 0.145456   
CAPES - CENTRO ANHANGUERA DE PROMOÇÃO E EDUCAÇÃO SOCIAL                                 0.145456   
ASSOCIAÇÃO COOP. DE FAMÍLIAS CARENTES DO JARDIM SENICE                                  0.124677   
INSTITUTO OIKOS                                                                         0.124677   
INSTITUTO ALEGRIA DE VIVER                                                              0.124677   
CLUBE DE MÃES DO JARDIM TURQUESA                                                        0.124677   
ENTIDADE DE PROMOÇÃO E ASSISTÊNCIA SOCIAL ESPAÇO ABERTO                                 0.124676   
ASSOCIAÇÃO COMUNITÁRIA SEMPRE VIVA                                                      0.139915   
...                                                                                          ...   
ASSOCIAÇÃO SÓCIO CULTURAL MADRE TERESA DE JESUS                                         0.062338   
ASSOCIAÇÃO DOS MUTUARIOS E MORADORES COHAB I                                            0.056350   
ASSOCIAÇÃO CULTURAL NOSSA SENHORA                                                       0.075325   
LIGA DAS SENHORAS CATOLICAS DE SÃO PAULO                                                0.051545   
SOCIEDADE AMIGOS DO BAIRRO SICILIANO ANGLO BRASILEIRA                                   0.041559   
ASSOCIAÇÃO SANTA CECILIA                                                                0.041559   
ASSOCIAÇÃO DE MORADORES DO JARDIM COMERCIAL E ADJACÊNCIAS                               0.041559   
ASSOCIAÇÃO VIVER MELHOR DO JARDIM MIRIAM                                       

txtObjetoContrato
377                                                                                                    NaN
1085                                                           SERVIÇO DE ELÉTRICA - EMEI MARIA DE LOURDES
1258   Programa Movimento de Alfabetização de Jovens e Adultos do município de São Paulo – MOVA / SP,  ...
1345                                                                    Aquisição de Certificados Digitais
1362                                                      TERMO DE CONVENIO - ADITAMENTO DE 5 SALAS (MOVA)
1379                             2º REPASSE PTRF/2017 - CUSTEIO - DRE G - CEI PEDRO BRASIL BANDECCHI, VER.
1448                                                                                CONVÊNIO MOVA / ALUTHA
1734   Aquisição de 140.000 Kg de Extrato de Tomate - ATA de RP n 31/SME/CODAE/2016 - PNAE/FNDE - DECRE...
1744   CONTRATAÇÃO DE AGENTE RECREATIVO PARA RECREIO NAS FÉRIAS - EDIÇÃO JULHO/2017 - PERIODO DE 10/07 ...
1746                   Repasse de Recursos do PNAE para o CEI  Familia Nova Aliança - CÓD. INEP 35578307\n
1747   PR-SM(S.MATEUS) – PR-VP/SB (SAPOPEMBA) – CONTRATAÇÃO DE AGENTE DE RECREAÇÃO -  RECREIO NAS FÉRIA...
4071                                                                                      PAGAMENTO DE DEA
4073   Celebração de Convênio MOVA - Centro Anhanguera de Promoção e Educação Social - CAPES para funci...
4075   Celebração de Convênio MOVA - Sociedade Amigos do Bairro Siciliano - ANGLO BRASILEIRA para funci...
4079        REPASSE DO PTRF PARA AS APMs e APMSUACs DE ACORDO COM A LEI 9394/1996 E PORTARIA SME 4128/2017
4599                                                                                    CONVENIO MOVA AVIB
4605                                                                            CONVÊNIO MOVA VILA SOLANGE
4947            2º REPASSE PTRF/2017 – DRE-G – CUSTEIO – APM – EMEF\tMARIA APARECIDA DO NASCIMENTO, PROFª 
4959                                                               CONVENIO EM CONTINUIDADE - MOVA LAREIRA
9132                                                                                  REF 07 SALAS DE MOVA
9186   Aquisição de 12.000 Kg de Flocos de Milho Açucarados - ATA de RP nº 017/SME/CODAE/2017 - FNDE/PNAE.
9211   PROGRAMA RECREIO NAS FÉRIAS - JANEIRO/2017 - DE ACORDO COM O EDITAL DE CREDENCIAMENTO Nº 004/201...
11598  CELEBRAÇÃO CONVÊNIO MOVA - SAVIC - 06 SALAS A PARTIR DE 23.11.2017 (Objeto da Contratação: Repub...
11773  ATENDIMENTO A CRIANÇA POR MEIO DO CENTRO DE EDUCAÇÃO INFANTIL CEI NOVOS RUMOS COM CAPACIDADE CON...
11777                                                                          Aquisição de passagem aérea
12051                                                                                  REF 01 SALA DE MOVA
12542                           CELEBRAÇÃO DE CONVÊNIO MOVA - ASSOCIAÇÃO CULTURAL NOSSA SENHORA DAS GRAÇAS
15590                                                            TERMO DE CONVÊNIO /MOVA CASP Nº 055/2015 
15599                                CELEBRAÇÃO EM CONTINUIDADE MOVA COMUNIDADE CRISTÃ DO AVIVAMENTO PLENO
15602                                          2º REPASSE PTRF/2017 - CUSTEIO -  APM EMEI MARIO BENI, DEP.
15607  CONVÊNIO MOVA - CONSENHO COMUNITÁRIO DE EDUCAÇÃO, CULTURA, SAÚDE E AÇÃO SOCIAL DE VILA SOLANGE E...
19031                                                                                        CONVENIO MOVA
19041                                                                               MOVA - JARDIM TURQUESA
22312                              PARCERIA DE 03 SALAS DE MOVA - LIGA DAS SENHORAS CATÓLICAS DE SÃO PAULO
22334                 PR/SM - PR/VP-SB - CONTRATAÇÃO DE OFICINEIROS PARA O PROGRAMA DE EXTENSÃO DE JORNADA
24698  PAGAMENTO INDENIZATÓRIO CENTRO COMUNITÁRIORAPOSO TAVARES - MOVA - 03 DE ABRIL DE 2017 À 21 DE MA...
25436                           AQUISIÇÃO DE MATERIAL EDUCATIVO - PROGRAMA RECREIO NAS FÉRIAS - JULHO/2017
30391                  

## 5.3. MOVA

#### Como filtrar?

## 5.4. Outros?

# 6. Obras e reformas

## 6.1. Obras e reformas (talvez devesse passar para a categoria de operação das unidades?)

#### (possível subdividir em unidades educacionais e outros?) 

#### Checar filtro

In [609]:
(empenhos_df[empenhos_df['txtDescricaoProjetoAtividade'].str.contains('reforma', case=False)]
    .txtDescricaoProjetoAtividade.unique())

array(['Construção, reforma e ampliação de equipamentos educacionais',
       'Reformas de Equipamentos Educacionais'], dtype=object)

In [610]:
# obras_reformas_filter = (
#     (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('constru', case=False))
#     |
#     (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('reforma', case=False))
# )
# obras_reformas = (empenhos_df[obras_reformas_filter])
# empenhos_df.loc[obras_reformas_filter, 'cat_1'] = 'obras_reformas'
# empenhos_df.loc[obras_reformas_filter, 'cat_2'] = 'obras_reformas'
# groupSum(obras_reformas)

# 7. Alimentação

#### Checar filtro

In [611]:
(empenhos_df[
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('alimenta', case=False))
    |
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('leite', case=False))
]
.txtDescricaoProjetoAtividade.unique())

array(['Programa Nacional de Alimentação Escolar - PNAE/ FNDE',
       'Alimentação Escolar', 'Leve-Leite'], dtype=object)

In [612]:
alimentacao_filter = (
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('alimenta', case=False))
    |
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('leite', case=False))
)
alimentacao = (empenhos_df[alimentacao_filter])
empenhos_df.loc[alimentacao_filter, 'cat_1'] = 'alimentacao'
# empenhos_df.loc[alimentacao_filter, 'cat_2'] = ''
groupSum(alimentacao)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação        1026.362386    646.263529   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação    707.817315

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes           1026.362386    646.263529    707.817315

valTotalEmpenhado  \
txtDescricaoElemento                                                     
Outros Serviços de Terceiros -Pessoa Jurídica               700.795726   
Material de Consumo                                         258.694712   
Material, Bem ou Serviço para Distribuição Gratuita          42.994545   
Contribuições                                                23.877403   

                                                     valLiquidado  \
txtDescricaoElemento                                                
Outros Serviços de Terceiros -Pessoa Jurídica          392.613835   
Material de Consumo                                    194.498042   
Material, Bem ou Serviço para Distribuição Gratuita     39.280542   
Contribuições                                           19.871110   

                                                     valPagoTotal  
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica          414.062018  
Material de Consumo                                    231.123712  
Material, Bem ou Serviço para Distribuição Gratuita     42.909846  
Contribuições                                           19.721738

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Transferências Federais          922.274282    581.286497    632.832297
Tesouro Municipal                104.088104     64.977033     74.985018

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                                     
Refeições Prontas                                                              593.326962   
Diversos Gêneros Alimentícios                                                  159.069208   
Leite e Achocolatados                                                           42.994545   
Preparo e Distribuição de Alimentos                                             33.367069   
Carnes em Geral                                                                 30.159054   
Armazenagem de Alimentos                                                        37.534199   
Outras Instituições de Caráter Assistencial, Cultural ou Educacional            23.877403   
Pães, Doces, Biscoitos e Salgados                                               20.711276   
Laticínios em Geral                                                             15.931271   
Transporte e Remessa de Encomendas                                              36.567497   
Grãos em Geral                                                                  12.048248   
Frutas Naturais                                                                 10.804552   
Leite em Pó ou Natural                                                           2.847350   
Óleos, Gorduras e Azeites Comestíveis, Condimentos e Temperos em Geral           4.226210   
Massas Alimentícias                                                              1.560750   
Bebidas em Geral                                                                 1.216395   
Farináceos                                                                       0.120400   

                                                                        valLiquidado  \
txtDescricaoItemDespesa                                                                
Refeições Prontas                                                         328.161845   
Diversos Gêneros Alimentícios                                             118.266813   
Leite e Achocolatados                                                      39.280542   
Preparo e Distribuição de Alimentos                                        29.668550   
Carnes em Geral                                                            23.368220   
Armazenagem de Alimentos                                                   23.237049   
Outras Instituições de Caráter Assistencial, Cultural ou Educacional       19.871110   
Pães, Doces, Biscoitos e Salgados                                          15.177323   
Laticínios em Geral                                                        15.732020   
Transporte e Remessa de Encomendas                                         11.546391   
Grãos em Geral                                                              9.668589   
Frutas Naturais                                                             4.785197   
Leite em Pó ou Natural                                                      2.847350   
Óleos, Gorduras e Azeites Comestíveis, Condimentos e Temperos em Geral      1.855835   
Massas Alimentícias                                                         1.459940   
Bebidas em Geral                                                            1.216355   
Farináceos                                                                  0.120400   

                                                                        valPagoTotal  
txtDescricaoItemDespesa                                                               
Refeições Prontas                                                         344.783132  
Diversos Gêneros Alimentícios                                             144.727754  
Leite e Achocolatados                                                      42.909846  
Preparo e Distribuição de Alimentos                                        32.019037  
Carnes em Geral                                                            27.439776  
Armazenagem de Aliment

...

valTotalEmpenhado  valLiquidado  \
txtDescricaoUnidade                                                     
Departamento de Alimentação Escolar          862.147511    553.323166   
Coordenadoria de Alimentação Escolar         164.214876     92.940363   

                                      valPagoTotal  
txtDescricaoUnidade                                 
Departamento de Alimentação Escolar     568.961843  
Coordenadoria de Alimentação Escolar    138.855472

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes        1026.362386    646.263529    707.817315

valTotalEmpenhado  \
txtModalidadeAplicacao                                                          
Aplicações Diretas                                                1002.484983   
Transferências a Instituições Privadas sem Fins Lucrativos          23.877403   

                                                            valLiquidado  \
txtModalidadeAplicacao                                                     
Aplicações Diretas                                            626.392419   
Transferências a Instituições Privadas sem Fins Lucrativos     19.871110   

                                                            valPagoTotal  
txtModalidadeAplicacao                                                    
Aplicações Diretas                                            688.095577  
Transferências a Instituições Privadas sem Fins Lucrativos     19.721738

valTotalEmpenhado  \
txtRazaoSocial                                                                                                            
SHA COMERCIO DE ALIMENTOS LTDA                                                                               190.741737   
COMERCIAL MILANO BRASIL LTDA                                                                                  92.039220   
DENJUD REFEIÇÕES COLETIVAS ADMINISTRAÇÃO E SERVIÇOS LTDA                                                     144.606175   
APETECE SISTEMAS DE ALIMENTACAO S/A                                                                          161.392758   
TANGARÁ IMP.E EXP.S/A                                                                                         61.845260   
BASE SISTEMA SERVIÇOS DE ADMINISTRAÇÃO E COMERCIO LTDA                                                        65.781097   
P.R.M. SERVIÇOS E MAO DE OBRA ESPECIALIZADA EIRELI                                                            44.011233   
SERBOM ARMAZENS GERAIS FRIGORIFICOS LTDA                                                                      37.534199   
CASTOR ALIMENTOS LTDA                                                                                         22.742754   
FRESKITO PRODUTOS ALIMENTICIOS LTDA                                                                           17.755644   
ATV ASSESSORIA TÉCNICA EM VENDAS LTDA                                                                         17.002894   
PRO ATIVA ALIMENTOS LTDA - EPP                                                                                14.265284   
EMPRESA BRASILEIRA DE CORREIOS E TELÉGRAFOS                                                                   36.567497   
ALNUTRI ALIMENTOS LTDA                                                                                        10.571033   
BONISSIMA COMERCIO E SERVIÇOS LTDA. EPP                                                                        9.920076   
MULTICOM COMERCIO MULTIPLO DE ALIMENTOS LTDA                                                                   9.510698   
AEX ALIMENTA COMERCIO DE REFEIÇÕES E SERVIÇOS LTDA                                                             8.983506   
GONÇALVES & TORTOLA S/A                                                                                        4.788000   
G NOVA COMERCIO DE PRODUTOS ALIMENTICIOS EIRELI - ME                                                           3.225500   
VIGOR ALIMENTOS /A                                                                                             3.087080   
ARIS ALIMENTOS LTDA. ME                                                                                        2.866500   
OURO PRETO ALIMENTOS COMÉRCIO LTDA - EPP.                                                                      2.740899   
COOPERATIVA DOS SUINICULTORES DO CAÍ SUPERIOR LTDA                                                             2.709900   
COOPERATIVA DE PRODUCAO INDUSTRIALIZACAO E COMERCIALIZACAO AGROPECUARIA DOS ASSENTADOS E AGRICULTORE           2.464280   
COMERCIAL DE ALIMENTOS NUTRIVIP DO BRASIL LTDA                                                                 3.944960   
SUPPORT PRODUTOS NUTRICIONAIS LTDA                                                                             2.040898   
SOMA ALIMENTOS DO BRASIL EIRELI                                                                                1.764000   
ALIMENTOS DALLAS INDÚSTRIA E COMÉRCIO LTDA                                                                     1.667753   
COOPERATIVA DE PRODUÇÃO E CONSUMO FAMILIAR NOSSA TERRA LTDA                                                    1.588860   
CRIALIMENTOS INDÚSTRIA E COMÉRCIO LTDA                                                                         1.407950   
...                                                                                                                 ...   
INSTITUIÇÃO AQUARELA                       

txtObjetoContrato
31     Aquisição de 87.500 Kg de Composto Lácteo Sabor Chocolate - ATA de RP nº 008/SME/CODAE/2017 - FN...
450                                  Repasse de Recursos do PNAE para o CEI CANTINHO AMAC - INEP 3531467\n
601             Repasse de Recursos do PNAE para o CEI PINGO DE GENTE  - CÓD. INEP 35127929 - 2º REPASSE\n
606                   Repasse de Recursos do PNAE para o CEI IPIRANGA  - CÓD. INEP 35391918 - 2º REPASSE\n
613                           REPASSE DE RECURSOS DO PNAE PARA O CEI PRIMEIROS PASSOS - COD. INEP 35811725
753                     Repasse de Recursos do PNAE para o CEI MARIAMA - CÓD. INEP 35580934 - 2º REPASSE\n
759                Repasse de Recursos do PNAE para o CEI REI SALOMÃO  - CÓD. INEP 35183751 - 2º REPASSE\n
862                                                                                                    NaN
1001                             Repasse de Recursos do PNAE para o CEI Aldair Maria - Cód. INEP: 35445071
1002                       Repasse de Recursos do PNAE para o CEI Principe Encantado - Cód. INEP: 35564308
1087                          Repasse de Recursos do PNAE para o CEI Estrela Dourada - Cód. INEP: 35563742
1091                        Repasse do Recurso do PNAE para o CEI Crescer e Aprender - Cód. INEP: 35580983
1093                                 Repasse do Recurso do PNAE para o CEI Irineu II - Cód. INEP: 35584548
1109                          Repasse de Recursos do PNAE para o CEI Cantinho Mágico - Cód. INEP: 35566676
1121                           Repasse de Recursos do PNAE para o CEI Luar do Sertão - Cód. INEP: 35128235
1142                                    Repasse de Recursos do PNAE para o CEI EFATA-  CÓD. INEP: 35579981
1143                           Repasse de Recursos do PNAE para o CEI Nelson Mandela - Cód. INEP: 35578940
1144                           Repasse de Recursos do PNAE para o CEI Parque do Lago - Cód. INEP: 35579841
1145                             Repasse de Recursos do PNAE para o CEI Família Sião - Cód. INEP: 35579312
1146                            Repasse de Recursos do PNAE para o CEI Elohim Kadosh - Cód. INEP: 35581773
1147                         Repasse de Recursos do PNAE para o CEI Cecilia Meireles - Cód. INEP: 35578150
1148                           Repasse de Recursos do PNAE para o CEI Novos Caminhos - Cód. INEP: 35584496
1152                                Repasse do Recurso do PNAE para o CEI Vovó Vanda - Cód. INEP: 35581070
1154                               Repasse de Recurso do PNAE para o CEI Amor Eterno - Cód. INEP: 35569434
1167                            Repasse do Recurso do PNAE para o CEI Cantinho Feliz - Cód. INEP: 35393061
1168                                                                             02 SALAS DE CONVENIO MOVA
1171                               Repasse de Recursos do PNAE para o CEI Rei Arthur - Cód. INEP: 35583327
1172                             Repasse de Recursos do PNAE para o CEI CASTILHO - CÓD. INEP 355811611\r\n
1173                    Repasse de Recursos do PNAE para o CEI UNIÃO DA VILA NOVA - CÓD. INEP 35439101\r\n
1175                       Repasse de Recursos do PNAE para o CEI PALAVRA CANTADA - CÓD. INEP 35578290\r\n
...                                                                                                    ...
53620                  Repasse de Recursos do PNAE para o CEI SELMO MARTINS DOS SANTOS Cód. INEP  35444923
53628  Aquisição 73.440 kg de FÓRMULA INFANTIL EM PÓ PARA LACTANTE A PARTIR DOS 6 MESES –  Ata de RP nº...
53630                       Repasse de Recursos do PNAE para o CEI JARDIM DA CONQUISTA Cód. INEP  35181912
53631              Repasse de Recursos do PNAE para o CEI JULIO FRANCISCO DE SOUZA III- CÓD. INEP 35443736
53632                              Repasse de Recursos do PNAE para o CEI AVES GALHANI- CÓD. INEP 35305534
53633               Repasse de Recursos do PNAE para o CEI Brincando Também se Aprende- CÓD. INEP 35183143
53634                  

## 7.1. Refeições prontas

#### Checar filtro e filtro anterior

In [613]:
refeicoes_filter = alimentacao_filter & (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Refeições Prontas', case=False))
    &
    ~(empenhos_df['txtDescricaoProjetoAtividade'].str.contains('leite', case=False))
)
refeicoes = (empenhos_df[refeicoes_filter])
empenhos_df.loc[refeicoes_filter, 'cat_1'] = 'alimentacao'
empenhos_df.loc[refeicoes_filter, 'cat_2'] = 'refeicoes'
groupSum(refeicoes)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação         593.326962    328.161845   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação    344.783132

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes            593.326962    328.161845    344.783132

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica         593.326962   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica    328.161845    344.783132

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Transferências Federais          593.326962    328.161845    344.783132

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoItemDespesa                                               
Refeições Prontas               593.326962    328.161845    344.783132

...

valTotalEmpenhado  valLiquidado  \
txtDescricaoUnidade                                                     
Departamento de Alimentação Escolar          586.456048    326.603238   
Coordenadoria de Alimentação Escolar           6.870914      1.558606   

                                      valPagoTotal  
txtDescricaoUnidade                                 
Departamento de Alimentação Escolar     338.306574  
Coordenadoria de Alimentação Escolar      6.476558

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes         593.326962    328.161845    344.783132

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas             593.326962    328.161845    344.783132

valTotalEmpenhado  \
txtRazaoSocial                                                                
SHA COMERCIO DE ALIMENTOS LTDA                                   163.581916   
DENJUD REFEIÇÕES COLETIVAS ADMINISTRAÇÃO E SERVIÇOS LTDA         143.268568   
APETECE SISTEMAS DE ALIMENTACAO S/A                              161.392758   
BASE SISTEMA SERVIÇOS DE ADMINISTRAÇÃO E COMERCIO LTDA            60.911457   
P.R.M. SERVIÇOS E MAO DE OBRA ESPECIALIZADA EIRELI                44.011233   
COMERCIAL MILANO BRASIL LTDA                                      11.177524   
AEX ALIMENTA COMERCIO DE REFEIÇÕES E SERVIÇOS LTDA                 8.983506   

                                                          valLiquidado  \
txtRazaoSocial                                                           
SHA COMERCIO DE ALIMENTOS LTDA                               93.378398   
DENJUD REFEIÇÕES COLETIVAS ADMINISTRAÇÃO E SERVIÇOS LTDA     76.278551   
APETECE SISTEMAS DE ALIMENTACAO S/A                          73.424133   
BASE SISTEMA SERVIÇOS DE ADMINISTRAÇÃO E COMERCIO LTDA       36.579694   
P.R.M. SERVIÇOS E MAO DE OBRA ESPECIALIZADA EIRELI           34.421740   
COMERCIAL MILANO BRASIL LTDA                                  7.877897   
AEX ALIMENTA COMERCIO DE REFEIÇÕES E SERVIÇOS LTDA            6.201431   

                                                          valPagoTotal  
txtRazaoSocial                                                          
SHA COMERCIO DE ALIMENTOS LTDA                               96.694435  
DENJUD REFEIÇÕES COLETIVAS ADMINISTRAÇÃO E SERVIÇOS LTDA     79.746704  
APETECE SISTEMAS DE ALIMENTACAO S/A                          76.517002  
BASE SISTEMA SERVIÇOS DE ADMINISTRAÇÃO E COMERCIO LTDA       40.244883  
P.R.M. SERVIÇOS E MAO DE OBRA ESPECIALIZADA EIRELI           36.242098  
COMERCIAL MILANO BRASIL LTDA                                  8.508958  
AEX ALIMENTA COMERCIO DE REFEIÇÕES E SERVIÇOS LTDA            6.829052

txtObjetoContrato
3586                            CONSUMO DE ÁGUA E SERVIÇO DE ÁGUA E ESGOTO-UNIDADES ESCOLARES E DRESA
4962                                                                                              NaN
6471                                                  MANUTENÇÃO PREDIAL - CEI VILA LIBANESA ELETRICA
8437                                   PAGAMENTO DE SERVIÇO DE FORNECIMENTO DE ÁGUA E ESGOTO - SABESP
30048           Contratação de serviços de nutrição e alimentação escolar  - Lote 5 - FREGUESIA DO O.
30056             Contratação de serviços de nutrição e alimentação escola - Lote 4 - FREGUESIA DO O.
30060               Contratação de serviços de nutrição e alimentação escolar - Lote 7A - IPIRANGA I.
30063                Contratação de seviços e nutrição e alimentação escolar - LOTE 7B - IPIRANGA II.
30110                Contratação de serviços de nutrição e alimentação escolar - LOTE 6 - GUAIANAZES.
30117       Contratação de serviços de nutrição e alimentação escolar - LOTE 8 - ITAQUERA/GUAIANAZES.
30128            Contratação de serviços de nutrição e alimentação escolar - LOTE 10A - SÃO MIGUEL I.
30134           Contratação de serviços de nutrição e alimentação escolar - LOTE 10B - SÃO MIGUEL II.
30210                   Contratação de serviços de nutrição e alimentação escolar - LOTE 11A - PENHA.
30293                    Contratação de serviços de nutrição e alimentação - LOTE 14A - SÃO MATEUS I.
30403            Contratação de serviços de nutrição e alimentação escolar - LOTE 5 - FREGUESIA DO Ó.
30422        \r\nContratação de serviços de nutrição e alimentação escolar – LOTE 6 - GUAIANAZES.\r\n
30426               Contratação de serviços de nutrição e alimentação escolar – LOTE  7A - IPIRANGA I
30439     Contratação de serviços de nutrição e alimentação escolar – LOTE  7B - IPIRANGA II.\r\n\r\n
30483           Contratação de serviços de nutrição e alimentação escolar – LOTE  9 - JAÇANA/TREMEMBÉ
30489                  Contratação de serviços de nutrição e alimentação escolar – LOTE  8 - ITAQUERA
30523           Contratação de serviços de nutrição e alimentação escolar – LOTE  10A - SÃO MIGUEL I.
30533      \r\nContratação de serviços de nutrição e alimentação escolar – LOTE  10B - SÃO MIGUEL II.
30544                  Contratação de serviços de nutrição e alimentação escolar – LOTE  11A - PENHA.
30554               Contratação de serviços de nutrição e alimentação escolar – LOTE  11B - PENHA II.
30572           Contratação de serviços de nutrição e alimentação escolar – LOTE  14A - SÃO MATEUS I.
30580      \r\nContratação de serviços de nutrição e alimentação escolar – LOTE  14B - SÃO MATEUS II.
51330          Contratação de serviços de nutrição e alimentação escolar- Lote 4 - CAPELA DO SOCORRO.
52422  Serviço de nutrição e alimentação escolar - Região Jãçanã-Tremembé - Contrataçãqo emergencial.
55762             Serviços de Nutrição e Alimentação Escolar - Região da FREGUESIA DO Ó e SÃO MATEUS 
55795       Serviços de Nutrição e Alimentação Escolar - Regiões de GUAIANASES, ITAQUERA e PENHA \n\n
55821                   Serviços de Nutrição e Alimentação Escolar - Regiões - IPIRANGA E SÃO MIGUEL

## 7.2. Leve-Leite

In [614]:
leve_leite_filter = alimentacao_filter & (
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('leite', case=False))
)
leve_leite = (empenhos_df[leve_leite_filter])
empenhos_df.loc[leve_leite_filter, 'cat_1'] = 'alimentacao'
empenhos_df.loc[leve_leite_filter, 'cat_2'] = 'leve_leite'
groupSum(leve_leite)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          79.562042     50.826933   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     54.456454

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             79.562042     50.826933     54.456454

valTotalEmpenhado  \
txtDescricaoElemento                                                     
Material, Bem ou Serviço para Distribuição Gratuita          42.994545   
Outros Serviços de Terceiros -Pessoa Jurídica                36.567497   

                                                     valLiquidado  \
txtDescricaoElemento                                                
Material, Bem ou Serviço para Distribuição Gratuita     39.280542   
Outros Serviços de Terceiros -Pessoa Jurídica           11.546391   

                                                     valPagoTotal  
txtDescricaoElemento                                               
Material, Bem ou Serviço para Distribuição Gratuita     42.909846  
Outros Serviços de Terceiros -Pessoa Jurídica           11.546607

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 79.562042     50.826933     54.456454

valTotalEmpenhado  valLiquidado  \
txtDescricaoItemDespesa                                               
Leite e Achocolatados                       42.994545     39.280542   
Transporte e Remessa de Encomendas          36.567497     11.546391   

                                    valPagoTotal  
txtDescricaoItemDespesa                           
Leite e Achocolatados                  42.909846  
Transporte e Remessa de Encomendas     11.546607

...

valTotalEmpenhado  valLiquidado  \
txtDescricaoUnidade                                                     
Departamento de Alimentação Escolar           61.083896     37.872368   
Coordenadoria de Alimentação Escolar          18.478146     12.954565   

                                      valPagoTotal  
txtDescricaoUnidade                                 
Departamento de Alimentação Escolar      37.872368  
Coordenadoria de Alimentação Escolar     16.584085

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          79.562042     50.826933     54.456454

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              79.562042     50.826933     54.456454

valTotalEmpenhado  valLiquidado  \
txtRazaoSocial                                                                 
TANGARÁ IMP.E EXP.S/A                                35.921819     32.575381   
EMPRESA BRASILEIRA DE CORREIOS E TELÉGRAFOS          36.567497     11.546391   
BONISSIMA COMERCIO E SERVIÇOS LTDA. EPP               7.072726      6.705161   

                                             valPagoTotal  
txtRazaoSocial                                             
TANGARÁ IMP.E EXP.S/A                           35.841094  
EMPRESA BRASILEIRA DE CORREIOS E TELÉGRAFOS     11.546607  
BONISSIMA COMERCIO E SERVIÇOS LTDA. EPP          7.068752

txtObjetoContrato
4827   Prestação de serviços e venda de produtos / Prestação de serviços de logística integrada: Entreg...
12081  Aquisição de 70.154 Kg de Leite em Pó  Integral - PROGRAMA LEVE-LEITE -  Lote 1 e 2 - ATA DE RP ...
12349  Aquisição de 80.677 Kg de Leite em Pó Integral - Lote 9 - PROGRAMA LEVE-LEITE - ATA de RP nº 09/...
12406  Aquisição de 196.431Kg de Leite em Pó  Integral – Lote 5 e 6 - PROGRAMA LEVE-LEITE - ATA DE RP N...
12538  Aquisição de 189.415 Kg de leite em Pó Integral - Lote 8 - PROGRAMA LEVE-LEITE - ATA de RP 07/SM...
12549  Aquisição 87.692 Kg de Leite em Pó Integral - Lote 4 - PROGRAMA LEVE-LEITE - ATA de RP nº 07/SME...
12610  Aquisição 63.138 Kg de Leite em Pó Integral - Lote 7 - PROGRAMA LEVE-LEITE - ATA de RP 09/SME/CO...
12637  Aquisição de 224.493 Kg de Leite em Pó Integral - Lote 10 - PROGRAMA LEVE-LEITE - ATA de RP nº 0...
31418  OBJETO: Aquisição 146.178 kg de Leite em Pó Integral – PROGRAMA LEVE-LEITE – Lote 4 - ATA de RP ...
31422  Aquisição 394.681 kg de Leite em Pó Integral – PROGRAMA LEVE-LEITE – Lote 8 - ATA de RP 07/SME/C...
31425  Aquisição 36.545  kg de Leite em Pó Integral – PROGRAMA LEVE-LEITE – referente a 75% da necessid...
31426  Aquisição 12.182 kg de Leite em Pó Integral – PROGRAMA LEVE-LEITE – referente a 25% da necessida...
31678  Aquisição 146.178 kg de Leite em Pó Integral – PROGRAMA LEVE-LEITE – Lotes 1 e 2 - ATA de RP 07/...
31679  Aquisição 409.299 kg de Leite em Pó Integral – PROGRAMA LEVE-LEITE – Lotes 5 e 6 - ATA de RP 07/...
31680  Aquisição 467.770 kg de Leite em Pó Integral – PROGRAMA LEVE-LEITE – Lote 10 - ATA de RP 07/SME/...
32372                                                                                                  NaN
52416  Aquisição 155.923 kg de Leite em Pó Integral – PROGRAMA LEVE-LEITE – Lote 9 - 25% - ATA de RP 09...
52419  Aquisição 131.560 kg de Leite em Pó Integral – PROGRAMA LEVE-LEITE – Lote 7 - ATA de RP 09/SME/C...

## 7.3. Preparo, distribuição e armazenagem

#### Checar filtro alimentação

In [615]:
prep_dist_filter = alimentacao_filter & (
    (
        (empenhos_df['txtDescricaoItemDespesa'].str.contains('Preparo e Distribuição de Alimentos', case=False))
        |
        (empenhos_df['txtDescricaoItemDespesa'].str.contains('Armazenagem de Alimentos', case=False))
    )
    &
    ~(empenhos_df['txtDescricaoProjetoAtividade'].str.contains('leite', case=False))
)
prep_dist = (empenhos_df[prep_dist_filter])
empenhos_df.loc[prep_dist_filter, 'cat_1'] = 'alimentacao'
empenhos_df.loc[prep_dist_filter, 'cat_2'] = 'prep_dist'
groupSum(prep_dist)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          70.901268     52.905599   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     57.732279

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             70.901268     52.905599     57.732279

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica          70.901268   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica     52.905599     57.732279

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Transferências Federais           70.901268     52.905599     57.732279

valTotalEmpenhado  valLiquidado  \
txtDescricaoItemDespesa                                                
Preparo e Distribuição de Alimentos          33.367069     29.668550   
Armazenagem de Alimentos                     37.534199     23.237049   

                                     valPagoTotal  
txtDescricaoItemDespesa                            
Preparo e Distribuição de Alimentos     32.019037  
Armazenagem de Alimentos                25.713242

...

valTotalEmpenhado  valLiquidado  \
txtDescricaoUnidade                                                     
Departamento de Alimentação Escolar           58.967661     47.529303   
Coordenadoria de Alimentação Escolar          11.933606      5.376297   

                                      valPagoTotal  
txtDescricaoUnidade                                 
Departamento de Alimentação Escolar      47.529303  
Coordenadoria de Alimentação Escolar     10.202976

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          70.901268     52.905599     57.732279

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              70.901268     52.905599     57.732279

valTotalEmpenhado  \
txtRazaoSocial                                                                
SHA COMERCIO DE ALIMENTOS LTDA                                    27.159821   
SERBOM ARMAZENS GERAIS FRIGORIFICOS LTDA                          37.534199   
BASE SISTEMA SERVIÇOS DE ADMINISTRAÇÃO E COMERCIO LTDA             4.869640   
DENJUD REFEIÇÕES COLETIVAS ADMINISTRAÇÃO E SERVIÇOS LTDA           1.337607   

                                                          valLiquidado  \
txtRazaoSocial                                                           
SHA COMERCIO DE ALIMENTOS LTDA                               24.799884   
SERBOM ARMAZENS GERAIS FRIGORIFICOS LTDA                     23.237049   
BASE SISTEMA SERVIÇOS DE ADMINISTRAÇÃO E COMERCIO LTDA        3.629595   
DENJUD REFEIÇÕES COLETIVAS ADMINISTRAÇÃO E SERVIÇOS LTDA      1.239071   

                                                          valPagoTotal  
txtRazaoSocial                                                          
SHA COMERCIO DE ALIMENTOS LTDA                               27.150370  
SERBOM ARMAZENS GERAIS FRIGORIFICOS LTDA                     25.713242  
BASE SISTEMA SERVIÇOS DE ADMINISTRAÇÃO E COMERCIO LTDA        3.629595  
DENJUD REFEIÇÕES COLETIVAS ADMINISTRAÇÃO E SERVIÇOS LTDA      1.239071

txtObjetoContrato
6472                                                                     NaN
31492  CONSUMO DE ÁGUA E SERVIÇO DE ÁGUA E ESGOTO-UNIDADES ESCOLARES E DRESA
32395         PAGAMENTO DE SERVIÇO DE FORNECIMENTO DE ÁGUA E ESGOTO - SABESP

## 7.4. Insumos 

#### (para refeições preparadas pela própria SME? Como subdividir?)

#### Checar filtro alimentação e filtros anteriores

In [616]:
insumos_regex = 'Diversos Gêneros Alimentícios|Carnes em Geral|Laticínios em Geral|Pães, Doces, Biscoitos e Salgados|Grãos em Geral|Frutas Naturais|Leite em Pó ou Natural|Óleos, Gorduras e Azeites Comestíveis, Condimentos e Temperos em Geral|Massas Alimentícias|Bebidas em Geral|Farináceos'
insumos_filter = alimentacao_filter & (
    (
        (empenhos_df['txtDescricaoItemDespesa'].str.contains(insumos_regex, case=False))
    )
    &
    ~(empenhos_df['txtDescricaoProjetoAtividade'].str.contains('leite', case=False))
)
insumos = (empenhos_df[insumos_filter])
empenhos_df.loc[insumos_filter, 'cat_1'] = 'alimentacao'
empenhos_df.loc[insumos_filter, 'cat_2'] = 'insumos'
groupSum(insumos)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação         258.694712    194.498042   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação    231.123712

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes            258.694712    194.498042    231.123712

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoElemento                                               
Material de Consumo          258.694712    194.498042    231.123712

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Transferências Federais          234.168650    180.347942    210.595148
Tesouro Municipal                 24.526063     14.150100     20.528564

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                                     
Diversos Gêneros Alimentícios                                                  159.069208   
Carnes em Geral                                                                 30.159054   
Pães, Doces, Biscoitos e Salgados                                               20.711276   
Laticínios em Geral                                                             15.931271   
Grãos em Geral                                                                  12.048248   
Frutas Naturais                                                                 10.804552   
Leite em Pó ou Natural                                                           2.847350   
Óleos, Gorduras e Azeites Comestíveis, Condimentos e Temperos em Geral           4.226210   
Massas Alimentícias                                                              1.560750   
Bebidas em Geral                                                                 1.216395   
Farináceos                                                                       0.120400   

                                                                        valLiquidado  \
txtDescricaoItemDespesa                                                                
Diversos Gêneros Alimentícios                                             118.266813   
Carnes em Geral                                                            23.368220   
Pães, Doces, Biscoitos e Salgados                                          15.177323   
Laticínios em Geral                                                        15.732020   
Grãos em Geral                                                              9.668589   
Frutas Naturais                                                             4.785197   
Leite em Pó ou Natural                                                      2.847350   
Óleos, Gorduras e Azeites Comestíveis, Condimentos e Temperos em Geral      1.855835   
Massas Alimentícias                                                         1.459940   
Bebidas em Geral                                                            1.216355   
Farináceos                                                                  0.120400   

                                                                        valPagoTotal  
txtDescricaoItemDespesa                                                               
Diversos Gêneros Alimentícios                                             144.727754  
Carnes em Geral                                                            27.439776  
Pães, Doces, Biscoitos e Salgados                                          19.138145  
Laticínios em Geral                                                        15.870590  
Grãos em Geral                                                              9.675717  
Frutas Naturais                                                             5.938649  
Leite em Pó ou Natural                                                      2.847350  
Óleos, Gorduras e Azeites Comestíveis, Condimentos e Temperos em Geral      2.588235  
Massas Alimentícias                                                         1.560740  
Bebidas em Geral                                                            1.216355  
Farináceos                                                                  0.120400

...

valTotalEmpenhado  valLiquidado  \
txtDescricaoUnidade                                                     
Departamento de Alimentação Escolar          143.758840    133.062779   
Coordenadoria de Alimentação Escolar         114.935873     61.435264   

                                      valPagoTotal  
txtDescricaoUnidade                                 
Departamento de Alimentação Escolar     137.033216  
Coordenadoria de Alimentação Escolar     94.090496

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes         258.694712    194.498042    231.123712

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas             258.694712    194.498042    231.123712

valTotalEmpenhado  \
txtRazaoSocial                                                                                                            
COMERCIAL MILANO BRASIL LTDA                                                                                  80.861696   
TANGARÁ IMP.E EXP.S/A                                                                                         25.923441   
CASTOR ALIMENTOS LTDA                                                                                         22.742754   
FRESKITO PRODUTOS ALIMENTICIOS LTDA                                                                           17.755644   
ATV ASSESSORIA TÉCNICA EM VENDAS LTDA                                                                         17.002894   
PRO ATIVA ALIMENTOS LTDA - EPP                                                                                14.265284   
ALNUTRI ALIMENTOS LTDA                                                                                        10.571033   
MULTICOM COMERCIO MULTIPLO DE ALIMENTOS LTDA                                                                   9.510698   
GONÇALVES & TORTOLA S/A                                                                                        4.788000   
G NOVA COMERCIO DE PRODUTOS ALIMENTICIOS EIRELI - ME                                                           3.225500   
VIGOR ALIMENTOS /A                                                                                             3.087080   
ARIS ALIMENTOS LTDA. ME                                                                                        2.866500   
BONISSIMA COMERCIO E SERVIÇOS LTDA. EPP                                                                        2.847350   
OURO PRETO ALIMENTOS COMÉRCIO LTDA - EPP.                                                                      2.740899   
COOPERATIVA DOS SUINICULTORES DO CAÍ SUPERIOR LTDA                                                             2.709900   
COOPERATIVA DE PRODUCAO INDUSTRIALIZACAO E COMERCIALIZACAO AGROPECUARIA DOS ASSENTADOS E AGRICULTORE           2.464280   
COMERCIAL DE ALIMENTOS NUTRIVIP DO BRASIL LTDA                                                                 3.944960   
SUPPORT PRODUTOS NUTRICIONAIS LTDA                                                                             2.040898   
SOMA ALIMENTOS DO BRASIL EIRELI                                                                                1.764000   
ALIMENTOS DALLAS INDÚSTRIA E COMÉRCIO LTDA                                                                     1.667753   
COOPERATIVA DE PRODUÇÃO E CONSUMO FAMILIAR NOSSA TERRA LTDA                                                    1.588860   
CRIALIMENTOS INDÚSTRIA E COMÉRCIO LTDA                                                                         1.407950   
NOVA CITRICOLA BRASIL EIRELLI - EPP                                                                            1.245000   
COOPERATIVA VINICOLA GARIBALDI LTDA                                                                            1.216395   
NUTRI-ALI COMERCIO E REPRESENTAÇÕES LTDA                                                                       1.170000   
COOPERATIVA DA AGRICULTURA FAMILIAR DE SETE BARRAS                                                             2.035536   
COOPERATIVA DOS BANANICULTORES E AGRICULTORES DE MIRACATU - COOBAM                                             2.019370   
COOPERATIVA AGROPECUARIA DE PRODUTOS SUSTENTAVEIS DO GUAPIRUVU - COOPERAGUA                                    1.127871   
PREDILECTA ALIMENTOS LTDA                                                                                      1.235400   
ASSOCIAÇÃO DE BANANICULTORES DO MUNICÍPIO DE MIRACATU - ABAM                                                   1.788645   
LUAM INDUSTRIA E COMÉRCIO DE ALIMENTOS LTDA.                                                                   1.041500   
ITAMBÉ ALIMENTOS S/A.                      

txtObjetoContrato
31     Aquisição de 87.500 Kg de Composto Lácteo Sabor Chocolate - ATA de RP nº 008/SME/CODAE/2017 - FN...
862                                                                                                    NaN
1168                                                                             02 SALAS DE CONVENIO MOVA
5366   Aquisição de 125.000 Kg de Composto Lácteo Sabor Chocolate - ATA de RP nº 008/SME/CODAE/2017 - F...
8294      Aquisição 117.000 kg de Macarrão de Sêmola Sopa tipo Conchinha – Ata de RP nº 14/SME/CODAE/2016.
8420   Aquisição de 1.790.000 Kg de Arroz  Longo Fino Tipo I – item 1 da Ata de RP nº 13/SME/CODAE/2016...
10149  Aquisição de 219.375 Kg de Carne Bovina Congelada em Peça - Corte Coxão Duro - ATA de RP nº 022/...
12016  Aquisição de 600.000 Unid. (200ml) Bebida Láctea U.A.T ou U.H.T Chocolate - ATA de RP nº 29/SME/...
12521  Aquisição de 222.500 Kg de Macarrão Curto de Sêmola sem ovos para Macarronada Tipo Caracolino - ...
12996  Aquisição de 180.000 Kg de Filé de Polaca do Alasca - ATA de RP 25/SME/CODAE/2016 - PNAE/FNDE - ...
15075  Aquisição de 30.000 Kg de Proteína Texturizada de Soja Granulada - ATA de RP nº 002/SME/CODAE/20...
15089  Aquisição de  125.000 KG de Composto Lácteo Sabor Café - ATA de RP nº 010/SME/CODAE/2017 - FNDE/...
15094  Aquisição de 160.000 Kg de Carne Bovina Congelada em Peças Cortada ao meio Corte Coxão Duro -  d...
15172          OBJETO: Aquisição de 180.000 Kg de Leite em Pó Integral  da ATA de RP nº 020/SME/CODAE/2017
15244  OBJETO: Aquisição de 300.000 de Feijão Comum de Cores – Carioca Tipo 1 -l  da ATA de RP nº 004/S...
15306  Aquisição de 30.000 Kg de Macarrão de Sêmola para Sopa - Cortes Tipo Alfabeto ou Letrinhas e/ou ...
15401           Aquisição de 54.000 KG de polpa de Acerola – da CHAMADA PÚBLICA de  nº 008/SME/CODAE/2017.
15710      Aquisição de 375.000 Kg de Composto Lácteo Sabor Chocolate  da ATA de RP nº 009/SME/CODAE/2017.
15782  Aquisição de 150.000 unidades (500 g)  de Margarina Sem Sal - ATA de RP nº 005/SME/CODAE/2017 - ...
15871  Aquisição de 194.000 LT de Suco de Uva integral  - Agricultura Familiar - Chamada Pública nº 004...
15886  Aquisição de 120.000 K  de Macarrão Curto Integral sem ovos para macarronada - Tipo Parafuso ou ...
18194         Aquisição 27.000 Kg de Flocos de Milho Açúcarados - ATA de RP 22/SME/CODAE/2016 - PNAE/FNDE.
18841  Aquisição de 1.650.000 Unid. de 40 grs. de Bolo em Embalagem Individual Diversos Sabores - ATA d...
18911  Aquisição de 140.000 Kg de Extrato de Tomate - ATA de RP n 31/SME/CODAE/2016 - PNAE/FNDE - DECRE...
19851  Aquisição de 1.570.546 unidades de Banana Nanica e 813.980 unidades de Banana Prata - AF - Chama...
19939  Aquisição – 1.524.008 und.de Banana Nanica - 632.160 und. de  Banana Prata  - 46.512 und de Bana...
19941  Aquisição de 2.000.000 unidades de Banana Nanica - AF - CHAMDA PUBLICA Nº 003/SME/CODAE/2017 - F...
19963  Aquisição de 505.555 unidades de Banana Nanica  e 210.811 unidades de Banana Prata - AF - CHAMAD...
19982  Aquisição – 777.777 und.de Banana Nanica – 324.325 und. de  Banana Prata – AGRICULTURA FAMILIAR ...
20970             Aquisição de 443.720 kg de Pão Hot Dog Tradicional – ATA de RP nº 12/SME/CODAE/2016.\r\n
...                                                                                                    ...
40901           Aquisição de Hortaliças e Verduras – 14.555,00 Kg da Chamada Pública nº 014/SME/CODAE/2017
42026  OBJETO: Aquisição – 1.141.120  unidades de Banana Nanica  - 813.981 unidades de Banana Prata - A...
42071  Aquisição de 972.222 unidades de Banana Nanica  e 541.068 unidades de Banana Prata - AF - CHAMAD...
42308  OBJETO: Aquisição – 279.000 Kg de Iogurte com Polpa de Morango- AGRICULTURA FAMILIAR – CHAMADA P...
42389  Aquisição de 1524.036 unidades de Banana Nanica, 632.161 unidades de Banana Prata, 46.511 unidad...
43196  Aquisição de 170.000 unidades (400 grs) de Biscoito Doce Tipo Maisena - ATA de RP  Nº 003/SME/CO...
43283  Aquisição de 85.

## 7.5. Transferencias PNAE

In [617]:
pnae_filter = alimentacao_filter & (
    (
        (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('Programa Nacional de Alimentação Escolar - PNAE/ FNDE', case=False))
        &
        (empenhos_df['txtDescricaoItemDespesa'].str.contains('Outras instituições', case=False))
    )
    &
    ~(empenhos_df['txtDescricaoProjetoAtividade'].str.contains('leite', case=False))
)
pnae = (empenhos_df[pnae_filter])
empenhos_df.loc[pnae_filter, 'cat_1'] = 'alimentacao'
empenhos_df.loc[pnae_filter, 'cat_2'] = 'pnae'
groupSum(pnae)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          23.877403      19.87111   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     19.721738

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             23.877403      19.87111     19.721738

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoElemento                                               
Contribuições                 23.877403      19.87111     19.721738

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Transferências Federais           23.877403      19.87111     19.721738

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                                   
Outras Instituições de Caráter Assistencial, Cultural ou Educacional          23.877403   

                                                                      valLiquidado  \
txtDescricaoItemDespesa                                                              
Outras Instituições de Caráter Assistencial, Cultural ou Educacional      19.87111   

                                                                      valPagoTotal  
txtDescricaoItemDespesa                                                             
Outras Instituições de Caráter Assistencial, Cultural ou Educacional     19.721738

...

valTotalEmpenhado  valLiquidado  \
txtDescricaoUnidade                                                     
Coordenadoria de Alimentação Escolar          11.996337     11.615632   
Departamento de Alimentação Escolar           11.881066      8.255478   

                                      valPagoTotal  
txtDescricaoUnidade                                 
Coordenadoria de Alimentação Escolar     11.501356  
Departamento de Alimentação Escolar       8.220382

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          23.877403      19.87111     19.721738

valTotalEmpenhado  \
txtModalidadeAplicacao                                                          
Transferências a Instituições Privadas sem Fins Lucrativos          23.877403   

                                                            valLiquidado  \
txtModalidadeAplicacao                                                     
Transferências a Instituições Privadas sem Fins Lucrativos      19.87111   

                                                            valPagoTotal  
txtModalidadeAplicacao                                                    
Transferências a Instituições Privadas sem Fins Lucrativos     19.721738

valTotalEmpenhado  \
txtRazaoSocial                                                                             
SOCIEDADE BENEFICENTE EQUILIBRIO DE INTERLAGOS                                  0.940530   
CENTRO DE ASSISTÊNCIA E PROMOÇÃO SOCIAL NOSSO LAR                               0.496266   
CRUZADA PRÓ INFÂNCIA                                                            0.460956   
CENTRO SOCIAL NOSSA SENHORA DO BOM PARTO                                        0.401250   
AÇÃO SOCIAL COMUNITÁRIA DO LAGEADO JOILSON DE JESUS                             0.279270   
INSTITUTO CEM POR CENTO SOCIAL                                                  0.222346   
FUNDAÇÃO COMUNIDADE DA GRAÇA                                                    0.219564   
ASSOCIAÇÃO SANTA EDWIGES                                                        0.185966   
OBRA ASSISTENCIAL JESUS MENINO                                                  0.185324   
AÇÃO SOCIAL SÃO MATEUS                                                          0.183398   
INSTITUTO EDUCACIONAL PAIS E FILHOS                                             0.214000   
CRUZADA PRO INFANCIA                                                            0.170986   
ASSOCIAÇÃO BENEFICENTE COMUNITÁRIA CRIANÇAS DE DEUS                             0.170558   
ASSOCIACAO CEDRO DO LIBANO DE PROTECAO A INFANCIA                               0.306234   
ONG PLENO VIVER                                                                 0.148944   
INSTITUTO CRIANÇA CIDADÃ                                                        0.143380   
ASSOCIAÇÃO SEARA NORTE                                                          0.247598   
SOCIEDADE INSTRUÇÃO E SOCORROS                                                  0.272636   
CENTRO SOCIAL DE PARELHEIROS                                                    0.136104   
CENTRO INTERESCOLAR DA JUVENTUDE                                                0.127758   
NUCLEO ASSISTENCIAL FRATERNO                                                    0.255516   
TURMA DA TOUCA ACRS                                                             0.189069   
CENTRO SOCIAL SANTA CATARINA                                                    0.120696   
INSTITUTO KWARAY                                                                0.188533   
ASSOCIACAO BENEFICENTE SANTA FILOMENA                                           0.118128   
ORGANIZAÇÃO TALENTO JOVEM                                                       0.115346   
ASSET - ASSOCIAÇÃO EDUCAR PARA TRANSFORMAR                                      0.148730   
ASSOCIAÇÃO SÃO GABRIEL                                                          0.112778   
ASSOCIAÇÃO AGUAS MARINHA                                                        0.111494   
ASSOCIAÇÃO DE MORADORES JACINTO PAZ                                             0.108926   
...                                                                                  ...   
ASSOCIAÇÃO DE VOLUNTÁRIOS EDUCADORES SOCIAIS - AVES                             0.016906   
CARITAS DIOCESANA DE CAMPO LIMPO -CDCL                                          0.016906   
ASSOCIAÇÃO DE VOLUNTARIOS EDUCADORES SOCIAIS - AVES                             0.016478   
ASSOC. COMUN. E BENEF. PE.  JOSÉ A. M. MOREIRA                                  0.016050   
INSTITUIÇÃO AQUARELA                                                            0.015622   
ASSOCIACAO EDUCACIONAL DE BRACOS ABERTOS                                        0.015622   
ASSOCIAÇÃO NOVOS HORIZONTES A COMUNIDADE                                        0.014980   
IHDI - INSTITUTO HUMANIZAÇÃO E DESENVOLVIMENTO  INTEGRAL                        0.014980   
GRUPO DE MAES COMUNIDADE FELIZ                                                  0.014980   
CRECHE NOSSA SENHORA MAE DA IGREJA                                              0.014980   
ASSOCIAÇÃO DOS MORADORES DO JARDIM AUREA                                        0.014980   
ASSOCIACAO FEMININA DAS

txtObjetoContrato
450                                  Repasse de Recursos do PNAE para o CEI CANTINHO AMAC - INEP 3531467\n
601             Repasse de Recursos do PNAE para o CEI PINGO DE GENTE  - CÓD. INEP 35127929 - 2º REPASSE\n
606                   Repasse de Recursos do PNAE para o CEI IPIRANGA  - CÓD. INEP 35391918 - 2º REPASSE\n
613                           REPASSE DE RECURSOS DO PNAE PARA O CEI PRIMEIROS PASSOS - COD. INEP 35811725
753                     Repasse de Recursos do PNAE para o CEI MARIAMA - CÓD. INEP 35580934 - 2º REPASSE\n
759                Repasse de Recursos do PNAE para o CEI REI SALOMÃO  - CÓD. INEP 35183751 - 2º REPASSE\n
1001                             Repasse de Recursos do PNAE para o CEI Aldair Maria - Cód. INEP: 35445071
1002                       Repasse de Recursos do PNAE para o CEI Principe Encantado - Cód. INEP: 35564308
1087                          Repasse de Recursos do PNAE para o CEI Estrela Dourada - Cód. INEP: 35563742
1091                        Repasse do Recurso do PNAE para o CEI Crescer e Aprender - Cód. INEP: 35580983
1093                                 Repasse do Recurso do PNAE para o CEI Irineu II - Cód. INEP: 35584548
1109                          Repasse de Recursos do PNAE para o CEI Cantinho Mágico - Cód. INEP: 35566676
1121                           Repasse de Recursos do PNAE para o CEI Luar do Sertão - Cód. INEP: 35128235
1142                                    Repasse de Recursos do PNAE para o CEI EFATA-  CÓD. INEP: 35579981
1143                           Repasse de Recursos do PNAE para o CEI Nelson Mandela - Cód. INEP: 35578940
1144                           Repasse de Recursos do PNAE para o CEI Parque do Lago - Cód. INEP: 35579841
1145                             Repasse de Recursos do PNAE para o CEI Família Sião - Cód. INEP: 35579312
1146                            Repasse de Recursos do PNAE para o CEI Elohim Kadosh - Cód. INEP: 35581773
1147                         Repasse de Recursos do PNAE para o CEI Cecilia Meireles - Cód. INEP: 35578150
1148                           Repasse de Recursos do PNAE para o CEI Novos Caminhos - Cód. INEP: 35584496
1152                                Repasse do Recurso do PNAE para o CEI Vovó Vanda - Cód. INEP: 35581070
1154                               Repasse de Recurso do PNAE para o CEI Amor Eterno - Cód. INEP: 35569434
1167                            Repasse do Recurso do PNAE para o CEI Cantinho Feliz - Cód. INEP: 35393061
1171                               Repasse de Recursos do PNAE para o CEI Rei Arthur - Cód. INEP: 35583327
1172                             Repasse de Recursos do PNAE para o CEI CASTILHO - CÓD. INEP 355811611\r\n
1173                    Repasse de Recursos do PNAE para o CEI UNIÃO DA VILA NOVA - CÓD. INEP 35439101\r\n
1175                       Repasse de Recursos do PNAE para o CEI PALAVRA CANTADA - CÓD. INEP 35578290\r\n
1176                       Repasse de Recursos do PNAE para o CEI CECILIA MEIRELES- CÓD. INEP 35578236\r\n
1177    Repasse de Recursos do PNAE para o CEI PROFESSORA RITA DE CÁSSIA SOBRAL LAZER- CÓD. INEP 355784...
1179                Repasse de Recursos do PNAE para o CE DONA MARIA FONSECA LAGO - CÓD. INEP 35483060\r\n
...                                                                                                    ...
53473                           Repasse de Recursos do PNAE para o CEI BERNARDO SANTANA CÓD. INEP 35417348
53474                      Repasse de Recursos do PNAE para o CEI LUIZA SOPHIA ROSCHEL- CÓD. INEP 35468988
53475           Repasse de Recursos do PNAE para o CEI VEREADOR MIGUEL FRANCHINI NETTO- CÓD. INEP 35183775
53477                             Repasse de Recursos do PNAE para o CEI FIM DE SEMANA- CÓD. INEP 35481129
53481                             Repasse de Recursos do PNAE para o CEI PLENITUDE- CÓD. INEP 35470466\r\n
53488                                  Repasse de Recursos do PNAE para o CEI MMDC- CÓD. INEP 35180166\r\n
53547                  

# 8. Pedagógico e formação

## 8.1. Cursos e formação

In [618]:
formacao_filter = (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Cursos de Especialização e Treinamento', case=False))
    |
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Convênios - Qualificação Profissional', case=False))
)
formacao = (empenhos_df[formacao_filter])
empenhos_df.loc[formacao_filter, 'cat_1'] = 'pedagogico'
empenhos_df.loc[formacao_filter, 'cat_2'] = 'formacao'
groupSum(formacao)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação           1.595121      1.449761   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação      1.486303

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes              1.595121      1.449761      1.486303

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica           1.595121   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica      1.449761      1.486303

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                  1.595121      1.449761      1.486303

valTotalEmpenhado  valLiquidado  \
txtDescricaoItemDespesa                                                   
Cursos de Especialização e Treinamento           1.011638      0.889933   
Convênios - Qualificação Profissional            0.583483      0.559827   

                                        valPagoTotal  
txtDescricaoItemDespesa                               
Cursos de Especialização e Treinamento      0.926476  
Convênios - Qualificação Profissional       0.559827

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário           1.595121      1.449761      1.486303

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes           1.595121      1.449761      1.486303

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas               1.595121      1.449761      1.486303

valTotalEmpenhado  \
txtRazaoSocial                                                              
INSTITUTO VLADIMIR HERZOG                                        0.583483   
FUNDACAO DE DESENVOLVIMENTO DA PESQUISA                          0.471951   
FUNDACAO SAO PAULO                                               0.509797   
FUNDACAO PARA O DESENVOLVIMENTO DA UNESP  -  FUNDUNESP           0.027890   
RL ASSESSORIA E TREINAMENTO EDUCACIONAL EIRELI - ME              0.002000   

                                                        valLiquidado  \
txtRazaoSocial                                                         
INSTITUTO VLADIMIR HERZOG                                   0.559827   
FUNDACAO DE DESENVOLVIMENTO DA PESQUISA                     0.471951   
FUNDACAO SAO PAULO                                          0.390092   
FUNDACAO PARA O DESENVOLVIMENTO DA UNESP  -  FUNDUNESP      0.027890   
RL ASSESSORIA E TREINAMENTO EDUCACIONAL EIRELI - ME         0.000000   

                                                        valPagoTotal  
txtRazaoSocial                                                        
INSTITUTO VLADIMIR HERZOG                                   0.559827  
FUNDACAO DE DESENVOLVIMENTO DA PESQUISA                     0.471951  
FUNDACAO SAO PAULO                                          0.426635  
FUNDACAO PARA O DESENVOLVIMENTO DA UNESP  -  FUNDUNESP      0.027890  
RL ASSESSORIA E TREINAMENTO EDUCACIONAL EIRELI - ME         0.000000

txtObjetoContrato
6734   Contratação de instituição para ministrar curso d3e especialização na área de surdez. Esta contr...
6794   Contratação de instituição para realização de curso de especialização na área de altas habilidad...
13300                                                                                                  NaN
16902                                                                           Contratação de Palestrante
26001  Contratação de instituição de ensino para desenvolvimento de Curso de Mestrado. Esta contratação...

## 8.2. Elaboração de materiais didáticos

## 8.3. Outros?

# 9. Tecnologia da informação

#### Checar filtros

In [619]:
ti_filter = (
    (empenhos_df['txtDescricaoSubFuncao'].str.contains('tecnologia da inf', case=False))
)
ti = (empenhos_df[ti_filter])
empenhos_df.loc[ti_filter, 'cat_1'] = 'ti'
groupSum(ti)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação         108.087883      40.89734   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     86.059425

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             66.708423     40.613301     45.753647
Despesas de Capital            41.379460      0.284038     40.305778

valTotalEmpenhado  \
txtDescricaoElemento                                                
Outros Serviços de Terceiros -Pessoa Jurídica           66.705633   
Equipamentos e Material Permanente                      41.019460   
Outros Serviços de Terceiros - Pessoa Jurídica           0.360000   
Material de Consumo                                      0.002790   

                                                valLiquidado  valPagoTotal  
txtDescricaoElemento                                                        
Outros Serviços de Terceiros -Pessoa Jurídica      40.610511     45.750857  
Equipamentos e Material Permanente                  0.104038     40.125778  
Outros Serviços de Terceiros - Pessoa Jurídica      0.180000      0.180000  
Material de Consumo                                 0.002790      0.002790

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                108.087883      40.89734     86.059425

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                                     
Outros Aparelhos e Equipamentos de Comunicação                                  40.021740   
Serviço de Instalação, Ampliação de Sist. de Telefonia/Teleinformática          15.368131   
PRODAM                                                                          15.912125   
Outros Serviços de Apoio Administrativo, Técnico e Operacional                   9.316095   
Manutenção e Conservação de Equipamentos de Processamento de Dados               9.195115   
Manutenção de Software                                                           8.605008   
Supervisão, Acompanhamento e Suporte de Serviços Técnicos                        2.559587   
Equipamentos de Processamento de Dados                                           0.583397   
Outras Máquinas e Equipamentos                                                   0.552979   
Guarda e Gerenciamento de Documentos                                             4.603634   
Aquisição de Softwares - Intangível                                              0.360000   
Outras Máquinas e Equipamentos Energéticos                                       0.075294   
Switch                                                                           0.033226   
Pesquisa em Geral                                                                0.007813   
Toner e Cartuchos de Tinta                                                       0.002790   
Certificado Digital                                                              0.001747   
Hardware                                                                         0.889200   

                                                                        valLiquidado  \
txtDescricaoItemDespesa                                                                
Outros Aparelhos e Equipamentos de Comunicação                              0.000000   
Serviço de Instalação, Ampliação de Sist. de Telefonia/Teleinformática     11.271799   
PRODAM                                                                      9.824414   
Outros Serviços de Apoio Administrativo, Técnico e Operacional              6.581965   
Manutenção e Conservação de Equipamentos de Processamento de Dados          5.937811   
Manutenção de Software                                                      3.876742   
Supervisão, Acompanhamento e Suporte de Serviços Técnicos                   1.771597   
Equipamentos de Processamento de Dados                                      0.522691   
Outras Máquinas e Equipamentos                                              0.460816   
Guarda e Gerenciamento de Documentos                                        0.361129   
Aquisição de Softwares - Intangível                                         0.180000   
Outras Máquinas e Equipamentos Energéticos                                  0.070812   
Switch                                                                      0.033226   
Pesquisa em Geral                                                           0.000000   
Toner e Cartuchos de Tinta                                                  0.002790   
Certificado Digital                                                         0.001547   
Hardware                                                                    0.000000   

                                                                        valPagoTotal  
txtDescricaoItemDespesa                                                               
Outros Aparelhos e Equipamentos de Comunicação                             40.021740  
Serviço de Instalação, Ampliação de Sist. de Telefonia/Teleinformática     13.518565  
PRODAM                                                                     11.357797  
Outros Serviços de Apoio Administrativo, Técnico e Operacional              7.106000  
Manutenção e Conservação de Equipamentos de Processamento de Dados          6.459788  
Manutenção de Software

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário         108.087883      40.89734     86.059425

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          66.708423     40.613301     45.753647
Investimentos                      41.379460      0.284038     40.305778

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas             108.087883      40.89734     86.059425

valTotalEmpenhado  \
txtRazaoSocial                                                                                                   
POSITIVO TECNOLOGIA S.A.                                                                             40.910940   
PRIMESYS SOLUÇÕES EMPRESARIAIS S.A.                                                                  14.698120   
EMPRESA DE TECNOLOGIA DA INFORMAÇÃO E COMUNICAÇÃO DO MUNICÍPIO DE SÃO PAULO - PRODAM-SP S/A          15.912125   
GOLDEN DISTRIBUIDORA LTDA.                                                                            9.334915   
G&P PROJETOS E SISTEMAS LTDA                                                                          9.320045   
MSTECH EDUCACAO E TECNOLOGIA EIRELI                                                                   7.853286   
AYNIL SOLUÇÕES S/A                                                                                    2.634882   
TELEFÔNICA BRASIL S.A.                                                                                0.670011   
ACECO TI S.A.                                                                                         0.583397   
GARTNER DO BRASIL SERVIÇOS DE PESQUISAS LTDA.                                                         0.534159   
COMPWIRE INFORMATICA S/A                                                                              0.528122   
NC COMERCIO E SERVIÇOS LTDA - ME                                                                      4.603634   
GEOAMBIENTE SENSORIAMENTO REMOTO LTDA                                                                 0.360000   
LIFE TECNOLOGIA E CONSULTORIA LTDA - ME                                                               0.098670   
H L P COMERCIO ELETRO-FONIA LTDA - EPP                                                                0.033226   
MERCER HUMAN RESOURCE CONSULTING LTDA                                                                 0.007813   
SÉRGIO LUIZ SCHOGOR JUNIOR - ME                                                                       0.002100   
SERASA S.A.                                                                                           0.001747   
VITOR EDE RODRIGUES GUERIERI 45633605896                                                              0.000690   

                                                                                             valLiquidado  \
txtRazaoSocial                                                                                              
POSITIVO TECNOLOGIA S.A.                                                                         0.000000   
PRIMESYS SOLUÇÕES EMPRESARIAIS S.A.                                                             10.708426   
EMPRESA DE TECNOLOGIA DA INFORMAÇÃO E COMUNICAÇÃO DO MUNICÍPIO DE SÃO PAULO - PRODAM-SP S/A      9.824414   
GOLDEN DISTRIBUIDORA LTDA.                                                                       6.538447   
G&P PROJETOS E SISTEMAS LTDA                                                                     5.895701   
MSTECH EDUCACAO E TECNOLOGIA EIRELI                                                              3.335047   
AYNIL SOLUÇÕES S/A                                                                               1.842409   
TELEFÔNICA BRASIL S.A.                                                                           0.563374   
ACECO TI S.A.                                                                                    0.522691   
GARTNER DO BRASIL SERVIÇOS DE PESQUISAS LTDA.                                                    0.504334   
COMPWIRE INFORMATICA S/A                                                                         0.492444   
NC COMERCIO E SERVIÇOS LTDA - ME                                                                 0.361129   
GEOAMBIENTE SENSORIAMENTO REMOTO LTDA                                                            0.180000   
LIFE TECNOLOGIA E CONSULTORIA LTDA - ME                        

txtObjetoContrato
2927                                                                                 Aquisição de switches
5062                                                                                                   NaN
8123                    Repasse de Recursos do PNAE para o CEI MORRO GRANDE CT VIDA - CÓD. INEP 35403118\n
8749   Aquisição de pesquisa salarial referente a cargos de tecnologia da informação para utilização co...
9017                                                                        Serviços de Manutenção Predial
11088  Repasse de recursos para APM de acordo com a Lei Federal nº 9.394/1996, Lei Municipal nº 13.991/...
15268                                                                   Aquisição de Certificados Digitais
18004                                                   Serviço de suporte técnico e manutenção p/hardware
22368                                     Contratação Emergencial - Suporte Técnico e Manutenção "On Site"
32760  PRESTAÇÃO DE SERVIÇOS DE PROCESSAMENTO, ARMAZENAMENTO, E VISUALIZAÇÃO DE DADOS GEORREFERENCIADOS...
33699                                           REPASSE DE RECURSOS A APM - PTRF: CUSTEIO E CAPITAL / 2017
40093                                                                                Aquisição de notebook
40224                                                                       Aquisição de microcomputadores
51184            \r\n\r\nAquisição de cartuchos de tinta para a impressota jato de tinta CANON iP 7210\r\n
51186                                   Cartuchos de tinta para a impressora jato de tinta CANON iP 7210. 
53831           PRESTAÇÃO DE SERVIÇOS DE AGENTE DE RECREAÇÃO NO PROGRAMA RECREIO NAS FÉRIAS - JANEIRO/2017

## 9.0 Compra de notebooks (2017)

In [620]:
compra_notebooks_filter = ti_filter & (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Outros Aparelhos e Equipamentos de Comunicação', case=False))
)
compra_notebooks = (empenhos_df[compra_notebooks_filter])
empenhos_df.loc[compra_notebooks_filter, 'cat_1'] = 'ti'
empenhos_df.loc[compra_notebooks_filter, 'cat_2'] = 'compra_notebooks'
groupSum(compra_notebooks)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação           40.02174           0.0   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação      40.02174

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas de Capital             40.02174           0.0      40.02174

valTotalEmpenhado  valLiquidado  \
txtDescricaoElemento                                                  
Equipamentos e Material Permanente           40.02174           0.0   

                                    valPagoTotal  
txtDescricaoElemento                              
Equipamentos e Material Permanente      40.02174

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                  40.02174           0.0      40.02174

valTotalEmpenhado  \
txtDescricaoItemDespesa                                             
Outros Aparelhos e Equipamentos de Comunicação           40.02174   

                                                valLiquidado  valPagoTotal  
txtDescricaoItemDespesa                                                     
Outros Aparelhos e Equipamentos de Comunicação           0.0      40.02174

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário           40.02174           0.0      40.02174

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                               
Investimentos             40.02174           0.0      40.02174

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas               40.02174           0.0      40.02174

valTotalEmpenhado  valLiquidado  valPagoTotal
txtRazaoSocial                                                         
POSITIVO TECNOLOGIA S.A.           40.02174           0.0      40.02174

txtObjetoContrato
40093  Aquisição de notebook

## 9.1. Fornecimento de internet

#### Checar filtro

In [621]:
internet_filter = ti_filter & (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Serviço de Instalação, Ampliação de Sist. de Telefonia/Teleinformática', case=False))
    |
#   # cabeamento elétrico e lógico
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Supervisão, Acompanhamento e Suporte de Serviços Técnicos', case=False))
)
internet = (empenhos_df[internet_filter])
empenhos_df.loc[internet_filter, 'cat_1'] = 'ti'
empenhos_df.loc[internet_filter, 'cat_2'] = 'internet'
groupSum(internet)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          17.927718     13.043396   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     15.388038

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             17.927718     13.043396     15.388038

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica          17.927718   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica     13.043396     15.388038

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 17.927718     13.043396     15.388038

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                                     
Serviço de Instalação, Ampliação de Sist. de Telefonia/Teleinformática          15.368131   
Supervisão, Acompanhamento e Suporte de Serviços Técnicos                        2.559587   

                                                                        valLiquidado  \
txtDescricaoItemDespesa                                                                
Serviço de Instalação, Ampliação de Sist. de Telefonia/Teleinformática     11.271799   
Supervisão, Acompanhamento e Suporte de Serviços Técnicos                   1.771597   

                                                                        valPagoTotal  
txtDescricaoItemDespesa                                                               
Serviço de Instalação, Ampliação de Sist. de Telefonia/Teleinformática     13.518565  
Supervisão, Acompanhamento e Suporte de Serviços Técnicos                   1.869473

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário          17.927718     13.043396     15.388038

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          17.927718     13.043396     15.388038

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              17.927718     13.043396     15.388038

valTotalEmpenhado  valLiquidado  \
txtRazaoSocial                                                         
PRIMESYS SOLUÇÕES EMPRESARIAIS S.A.          14.698120     10.708426   
AYNIL SOLUÇÕES S/A                            2.559587      1.771597   
TELEFÔNICA BRASIL S.A.                        0.670011      0.563374   

                                     valPagoTotal  
txtRazaoSocial                                     
PRIMESYS SOLUÇÕES EMPRESARIAIS S.A.     12.848554  
AYNIL SOLUÇÕES S/A                       1.869473  
TELEFÔNICA BRASIL S.A.                   0.670011

txtObjetoContrato
5362                                                                                  NaN
8123   Repasse de Recursos do PNAE para o CEI MORRO GRANDE CT VIDA - CÓD. INEP 35403118\n

## 9.2. Manutenção de equipamentos -> suporte de TI

In [622]:
manutencao_equip_ti_filter = ti_filter & (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Manutenção e Conservação de Equipamentos de Processamento de Dados', case=False))
)
manutencao_equip_ti = (empenhos_df[manutencao_equip_ti_filter])
empenhos_df.loc[manutencao_equip_ti_filter, 'cat_1'] = 'ti'
empenhos_df.loc[manutencao_equip_ti_filter, 'cat_2'] = 'manutencao_equip_ti'
groupSum(manutencao_equip_ti)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação           9.195115      5.937811   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação      6.459788

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes              9.195115      5.937811      6.459788

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica           9.195115   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica      5.937811      6.459788

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                  9.195115      5.937811      6.459788

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                                 
Manutenção e Conservação de Equipamentos de Processamento de Dados           9.195115   

                                                                    valLiquidado  \
txtDescricaoItemDespesa                                                            
Manutenção e Conservação de Equipamentos de Processamento de Dados      5.937811   

                                                                    valPagoTotal  
txtDescricaoItemDespesa                                                           
Manutenção e Conservação de Equipamentos de Processamento de Dados      6.459788

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário           9.195115      5.937811      6.459788

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes           9.195115      5.937811      6.459788

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas               9.195115      5.937811      6.459788

valTotalEmpenhado  valLiquidado  valPagoTotal
txtRazaoSocial                                                             
G&P PROJETOS E SISTEMAS LTDA           8.666993      5.445367      5.934092
COMPWIRE INFORMATICA S/A               0.528122      0.492444      0.525696

txtObjetoContrato
18005                Serviço de suporte técnico e manutenção p/hardware
22374  Contratação Emergencial - Suporte Técnico e Manutenção "On Site"
33699        REPASSE DE RECURSOS A APM - PTRF: CUSTEIO E CAPITAL / 2017
38489                                                               NaN

## 9.3. Manutenção de software e sistemas PRODAM

In [623]:
prodam_filter = ti_filter & (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('PRODAM', case=False))
    |
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Manutenção de Software', case=False))
)
prodam = (empenhos_df[prodam_filter])
empenhos_df.loc[prodam_filter, 'cat_1'] = 'ti'
empenhos_df.loc[prodam_filter, 'cat_2'] = 'manutencao_software_sistemas'
groupSum(prodam)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          24.517133     13.701156   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação     15.273364

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             24.517133     13.701156     15.273364

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica          24.517133   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica     13.701156     15.273364

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 24.517133     13.701156     15.273364

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoItemDespesa                                               
PRODAM                           15.912125      9.824414     11.357797
Manutenção de Software            8.605008      3.876742      3.915567

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário          24.517133     13.701156     15.273364

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          24.517133     13.701156     15.273364

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas              24.517133     13.701156     15.273364

valTotalEmpenhado  \
txtRazaoSocial                                                                                                   
EMPRESA DE TECNOLOGIA DA INFORMAÇÃO E COMUNICAÇÃO DO MUNICÍPIO DE SÃO PAULO - PRODAM-SP S/A          15.912125   
MSTECH EDUCACAO E TECNOLOGIA EIRELI                                                                   7.853286   
G&P PROJETOS E SISTEMAS LTDA                                                                          0.653052   
LIFE TECNOLOGIA E CONSULTORIA LTDA - ME                                                               0.098670   

                                                                                             valLiquidado  \
txtRazaoSocial                                                                                              
EMPRESA DE TECNOLOGIA DA INFORMAÇÃO E COMUNICAÇÃO DO MUNICÍPIO DE SÃO PAULO - PRODAM-SP S/A      9.824414   
MSTECH EDUCACAO E TECNOLOGIA EIRELI                                                              3.335047   
G&P PROJETOS E SISTEMAS LTDA                                                                     0.450335   
LIFE TECNOLOGIA E CONSULTORIA LTDA - ME                                                          0.091360   

                                                                                             valPagoTotal  
txtRazaoSocial                                                                                             
EMPRESA DE TECNOLOGIA DA INFORMAÇÃO E COMUNICAÇÃO DO MUNICÍPIO DE SÃO PAULO - PRODAM-SP S/A     11.357797  
MSTECH EDUCACAO E TECNOLOGIA EIRELI                                                              3.335047  
G&P PROJETOS E SISTEMAS LTDA                                                                     0.481850  
LIFE TECNOLOGIA E CONSULTORIA LTDA - ME                                                          0.098670

txtObjetoContrato
5062                                                                                          NaN
18004                                          Serviço de suporte técnico e manutenção p/hardware
22368                            Contratação Emergencial - Suporte Técnico e Manutenção "On Site"
53831  PRESTAÇÃO DE SERVIÇOS DE AGENTE DE RECREAÇÃO NO PROGRAMA RECREIO NAS FÉRIAS - JANEIRO/2017

## 9.4. Manutenção de equipamentos de impressão e insumos

In [624]:
outros_ti_filter = ti_filter & (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Supervisão, Acompanhamento e Suporte de Serviços Técnicos', case=False))
)
outros_ti = (empenhos_df[outros_ti_filter])
empenhos_df.loc[outros_ti_filter, 'cat_1'] = 'ti'
empenhos_df.loc[outros_ti_filter, 'cat_2'] = 'manutencao_impressao'
groupSum(outros_ti)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação           2.559587      1.771597   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação      1.869473

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes              2.559587      1.771597      1.869473

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica           2.559587   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica      1.771597      1.869473

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                  2.559587      1.771597      1.869473

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                        
Supervisão, Acompanhamento e Suporte de Serviços Técnicos           2.559587   

                                                           valLiquidado  \
txtDescricaoItemDespesa                                                   
Supervisão, Acompanhamento e Suporte de Serviços Técnicos      1.771597   

                                                           valPagoTotal  
txtDescricaoItemDespesa                                                  
Supervisão, Acompanhamento e Suporte de Serviços Técnicos      1.869473

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário           2.559587      1.771597      1.869473

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes           2.559587      1.771597      1.869473

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas               2.559587      1.771597      1.869473

valTotalEmpenhado  valLiquidado  valPagoTotal
txtRazaoSocial                                                   
AYNIL SOLUÇÕES S/A           2.559587      1.771597      1.869473

txtObjetoContrato
8123   Repasse de Recursos do PNAE para o CEI MORRO GRANDE CT VIDA - CÓD. INEP 35403118\n

# 10. Transferência de recursos PTRF

## 10.1 Geral

In [625]:
# mapear?

In [626]:
ptrf_filter = (
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Programa Transferência Recursos Financeiros', case=False))
)
ptrf = (empenhos_df[ptrf_filter])
empenhos_df.loc[ptrf_filter, 'cat_1'] = 'transferencias'
empenhos_df.loc[ptrf_filter, 'cat_2'] = 'ptrf'
groupSum(ptrf)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          42.878479      41.84657   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação      41.84657

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             38.034370     37.074281     37.074281
Despesas de Capital             4.844109      4.772288      4.772288

valTotalEmpenhado  \
txtDescricaoElemento                                                
Outros Serviços de Terceiros - Pessoa Jurídica          38.034370   
Equipamentos e Material Permanente                       4.844109   

                                                valLiquidado  valPagoTotal  
txtDescricaoElemento                                                        
Outros Serviços de Terceiros - Pessoa Jurídica     37.074281     37.074281  
Equipamentos e Material Permanente                  4.772288      4.772288

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 42.878479      41.84657      41.84657

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                                    
Programa Transferência Recursos Financeiros - Assoc de Pais e Mestres          38.034370   
Programa Transferência Recursos Financeiros - PTRF - APM                        4.844109   

                                                                       valLiquidado  \
txtDescricaoItemDespesa                                                               
Programa Transferência Recursos Financeiros - Assoc de Pais e Mestres     37.074281   
Programa Transferência Recursos Financeiros - PTRF - APM                   4.772288   

                                                                       valPagoTotal  
txtDescricaoItemDespesa                                                              
Programa Transferência Recursos Financeiros - Assoc de Pais e Mestres     37.074281  
Programa Transferência Recursos Financeiros - PTRF - APM                   4.772288

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Diretoria Regional de Educação - Campo Limpo                     6.001994   
Diretoria Regional de Educação - São Miguel                      4.253045   
Diretoria Regional de Educação - Pirituba                        4.297259   
Diretoria Regional de Educação - São Mateus                      3.886844   
Diretoria Regional de Educação  Capela do Socorro                3.087856   
Diretoria Regional de Educação - Guaianases                      2.931090   
Diretoria Regional de Educação - Penha                           2.909953   
Diretoria Regional de Educação - Jaçanã/Tremembé                 2.881946   
Diretoria Regional de Educação - Freguesia/Brasilândia           2.737565   
Diretoria Regional de Educação - Itaquera                        2.775872   
Diretoria Regional de Educação - Ipiranga                        2.689750   
Diretoria Regional de Educação - Santo Amaro                     2.277907   
Diretoria Regional de Educação - Butantã                         2.147399   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Diretoria Regional de Educação - Campo Limpo                5.582000   
Diretoria Regional de Educação - São Miguel                 4.150001   
Diretoria Regional de Educação - Pirituba                   4.004503   
Diretoria Regional de Educação - São Mateus                 3.847700   
Diretoria Regional de Educação  Capela do Socorro           3.071113   
Diretoria Regional de Educação - Guaianases                 2.899841   
Diretoria Regional de Educação - Penha                      2.888076   
Diretoria Regional de Educação - Jaçanã/Tremembé            2.881946   
Diretoria Regional de Educação - Freguesia/Brasilândia      2.710469   
Diretoria Regional de Educação - Itaquera                   2.697746   
Diretoria Regional de Educação - Ipiranga                   2.687871   
Diretoria Regional de Educação - Santo Amaro                2.277907   
Diretoria Regional de Educação - Butantã                    2.147399   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Diretoria Regional de Educação - Campo Limpo                5.582000  
Diretoria Regional de Educação - São Miguel                 4.150001  
Diretoria Regional de Educação - Pirituba                   4.004503  
Diretoria Regional de Educação - São Mateus                 3.847700  
Diretoria Regional de Educação  Capela do Socorro           3.071113  
Diretoria Regional de Educação - Guaianases                 2.899841  
Diretoria Regional de Educação - Penha                      2.888076  
Diretoria Regional de Educação - Jaçanã/Tremembé            2.881946  
Diretoria Regional de Educação - Freguesia/Brasilândia      2.710469  
Diretoria Regional de Educação - Itaquera                   2.697746  
Diretoria Regional de Educação - Ipiranga                   2.687871  
Diretoria Regional de Educação - Santo Amaro                2.277907  
Diretoria Regional de Educação - Butantã                    2.147399

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          38.034370     37.074281     37.074281
Investimentos                       4.844109      4.772288      4.772288

valTotalEmpenhado  \
txtModalidadeAplicacao                                                          
Transferências a Instituições Privadas sem Fins Lucrativos          42.878479   

                                                            valLiquidado  \
txtModalidadeAplicacao                                                     
Transferências a Instituições Privadas sem Fins Lucrativos      41.84657   

                                                            valPagoTotal  
txtModalidadeAplicacao                                                    
Transferências a Instituições Privadas sem Fins Lucrativos      41.84657

valTotalEmpenhado  \
txtRazaoSocial                                                                                                            
APM EMEF PADRE JOSE PEGORARO                                                                                   0.065233   
APM DA EMEFM ANTONIO A.VERISSIMO                                                                               0.064433   
APM DA EMEFM  PROF.  LINNEU PRESTES                                                                            0.063803   
APM DA EMEF FAGUNDES VARELLA                                                                                   0.062930   
ASSOCIAÇÃO DE PAIS E MESTRES DA EMEF PADRE LEONEL FRANCA                                                       0.096381   
A. P. M. DA EMEF CEU SAPOPEMBA                                                                                 0.060248   
APM DO CEU EMEF MARIA APARECIDA DE SOUZA CAMPOS                                                                0.059965   
APM DA EMEF FREI DAMIAO                                                                                        0.059521   
APM DO CEU  EMEF MANOEL VIEIRA DE QUEIROZ FILHO                                                                0.059013   
APM DA EMEF PROF. MARIA RITA DE CASSIA PINHEIRO SIMOES BRAGA                                                   0.058199   
ASSOCIAÇÃO DE PAIS E MESTRES SERVIDORES USUÁRIOS E AMIGOS DO CENTRO EDUC UNIFICADO VILA DO SOL                 0.056785   
APM DA EMEF EZEQUIEL RAMOS JUNIOR                                                                              0.056265   
ASSOCIAÇÃO DE PAIS E MESTRES DO CEU EMEF JAGUARÉ                                                               0.088643   
ASSOCIAÇÃO DE PAIS E METRES SERVIDORES USUARIOS E AMIGOS DO CENTRO EDUCACIONAL UNIFICADO TRES PONTES           0.055082   
APM DA EMEFM PROFESSOR DERVILLE ALLEGRETTI                                                                     0.054890   
APM. SERVIDORES. USUÁR. E AMIGOS CEU INACIO MONTEIRO (APMSUAC)                                                 0.054342   
ASSOCIAÇÃO DE PAIS E MESTRES DO CEU EMEF VILA DO SOL                                                           0.075946   
APM SERVIDORES USUARIOS AMIGOS DO CEU NAVEGANTES PROF JOSE EVERARDO RODRIGUES COSME                            0.054183   
APM DA EMEF HIPÓLITO JOSÉ DA COSTA                                                                             0.054003   
APM DA EMEF PROF. ANDRE RODRIGUES DE ALCKMIN                                                                   0.053998   
APM DA EMEF PROF CARLOS PASQUALE                                                                               0.053934   
ASSOCIACAO DE PAIS E MESTRES DA EMEF JORNALISTA MILLOR FERNANDES                                               0.053765   
ASSOCIAÇÃO DE PAIS E MESTRES DO CEU EMEF TRÊS PONTES                                                           0.053679   
ASSOCIAÇÃO DE PAIS E MESTRES DA EMEF DR JOÃO AUGUSTO BREVES                                                    0.053594   
ASSOCIAÇÃO DE PAIS E MESTRES DO CEU EMEF CAPÃO REDONDO                                                         0.080031   
ASSOCIAÇAO PAIS MESTRES SERVIDORES USUARIOS AMIGOS DO CENTRO EDUCACIONAL UNIFICADO PARELHEIROS                 0.053269   
ASSOCIAÇÃO DE PAIS E MESTRES DA EMEF CASTOR                                                                    0.052977   
APM DA EMEF FRANCISCO ALVES MENDES FILHO - CHICO MENDES                                                        0.052908   
APM DA EMEF PROF AROLDO DE AZEVEDO                                                                             0.059166   
APM DA ESCOLA MUNICIPAL DE ENSINO FUDAMENTAL CASSIANO RICARDO                                                  0.052498   
...                                                                                                                 ...   
ASSOCIAÇÃO DE PAIS E MESTRES DO CEI VEREADO

txtObjetoContrato
1000   REPASSES DO RECURSO PARA  A APM DE ACORDO COM A LEI FEDERAL 9394/96, LEI MUNICIPAL 13991/05, DEC...
1003    REPASSES DO RECURSO PARA A APM DE ACORDO  COM A LEI FEDERAL 9394/96, LEI MUNICIPAL 13991/05, DE...
1004   IT - 1º REPASSE PARA APM DA EMEF PROFº FERNANDO DE AZEVEDO - DE ACORDO COM A LEI Nº 9394//96, LE...
1005   IT - 1º REPASSE PARA APM DA EMEF DR. HELLIO TAVARES  - DE ACORDO COM A LEI Nº 9394//96, LEI MUNI...
1006   IT- 1º REPASSE PARA APM DA EMEF HENRIQUE FELIPE DA COSTA HENRICAO- DE ACORDO COM A LEI Nº 9394//...
1007   IT - 1º REPASSE PARA APM DA EMEF JOSEFA NICÁCIO DE ARAUJO, PROFª  - DE ACORDO COM A LEI Nº 9394/...
1008   IT- 1º REPASSE PARA APM DA EMEF PROFª IZABEL APARECIDA CRISTOVÃO DA LUZ - DE ACORDO COM A LEI Nº...
1009   IT- 1º REPASSE PARA APM DA EMEF JOSE HONORIO RODRIGUES - DE ACORDO COM A LEI Nº 9394//96, LEI MU...
1011   IT - 1º REPASSE PARA APM DA EMEF DR. JOSE PEDRO LEITE CORDEIRO - DE ACORDO COM A LEI Nº 9394//96...
1015   IT- 1º REPASSE PARA APM DA EMEF COM.VICENTE AMATO SOBRINHO - DE ACORDO COM A LEI Nº 9394//96, LE...
1017   IT- 1º REPASSE PARA APM DA EMEF PROFª WANDA OVIDIO GONÇALVES - DE ACORDO COM A LEI Nº 9394//96, ...
1021   IT- 1º REPASSE PARA APM DA EMEF CEU MARIA CLARA MACHADO - DE ACORDO COM A LEI Nº 9394//96, LEI M...
1023   IT - 1º REPASSE PTRF PARA APM DA EMEF CEU VILA CURUÇA   - DE ACORDO COM A LEI Nº 9394//96, LEI M...
1025   IT - 1º REPASSE PTRF PARA APM DA EMEF JARDIM BARTIRA   - DE ACORDO COM A LEI Nº 9394//96, LEI MU...
1038   MP - 1º REPASSE PTRF PARA APM DA EMEF JOSÉ AMÉRICO DE ALMEIDA   - DE ACORDO COM A LEI Nº 9394//9...
1039   MP - 1º REPASSE PTRF PARA APM DA EMEF PROFº JOSE BENTO DE ASSIS   - DE ACORDO COM A LEI Nº 9394/...
1040   MP - 1º REPASSE PTRF PARA APM DA EMEF PE JOSE DE ANCHIETA   - DE ACORDO COM A LEI Nº 9394//96, L...
1041   MP - 1º REPASSE PTRF PARA APM DA EMEF SEN. JOSE ERMIRIO DE MORAES   - DE ACORDO COM A LEI Nº 939...
1042   MP - 1º REPASSE PTRF PARA APM DA EMEF SEN. LINO DE MATTOS  - DE ACORDO COM A LEI Nº 9394//96, LE...
1043   MP - 1º REPASSE PTRF PARA APM DA EMEF MURURES  - DE ACORDO COM A LEI Nº 9394//96, LEI MUNICIPAL ...
1044   MP - 1º REPASSE PTRF PARA APM DA EMEF D. PAULO ROLIM LOUREIRO  - DE ACORDO COM A LEI Nº 9394//96...
1045   MP- 1º REPASSE PTRF PARA APM DA EMEF DR. PEDRO ALEIXO - DE ACORDO COM A LEI Nº 9394//96, LEI MUN...
1047   REPASSES DO RECURSO PARA A APM DE ACORDO COM A LEI FEDERAL 9394/06, LEI MUNICIPAL 13991/05, DECR...
1191   REPASSES DE RECURSOS PARA APM DE ACORDO COM A LEI FEDERAL Nº 9394/1996, LEI MUNICIPAL Nº 13.991/...
1192    REPASSES DE RECURSOS PARA APM DE ACORDO COM A LEI FEDERAL Nº 9394/1996, LEI MUNICIPAL Nº 13.991...
1196    REPASSES DE RECURSOS PARA APM DE ACORDO COM A LEI FEDERAL Nº 9394/1996, LEI MUNICIPAL Nº 13.991...
1200   Repasse de Recursos para  APM de acordo com A LEI FEDERAL Nº 9394/1996, LEI MUNICIPAL Nº 13.991/...
1223   Repasse de Recursos para  APM de acordo com A LEI FEDERAL Nº 9394/1996, LEI MUNICIPAL Nº 13.991/...
1233    REPASSES DE RECURSOS PARA APM DE ACORDO COM A LEI FEDERAL Nº 9394/1996, LEI MUNICIPAL Nº 13.991...
1236   REPASSES DE RECURSOS PARA APM DE ACORDO COM A LEI FEDERAL Nº 9394/1996, LEI MUNICIPAL Nº 13.991/...
...                                                                                                    ...
44010  MP - 1º REPASSE PTRF PARA APM DA EMEF ARQ. LUIS SAIA   - DE ACORDO COM A LEI Nº 9394//96, LEI MU...
44028  MP - 1º REPASSE PARA APM DA EMEF ALM. PEDRO DE FRONTIN - DE ACORDO COM A LEI Nº 9394//96, LEI MU...
44033  MP - 1º REPASSE PARA APM DA EMEF  PEDRO TEIXEIRA - DE ACORDO COM A LEI Nº 9394//96, LEI MUNICIPA...
47414                         2º REPASSE PTRF/2017 - CUSTEIO - DRE G - CEI ALICE APARECIDA DE SOUZA, PROFA
47415                     2º REPASSE PTRF/2017 - CAPITAL - DRE G - CEI ALICE APARECIDA DE SOUZA, PROFA\r\n
47417                                        2º REPASSE PTRF/2017 - CUSTEIO - DRE G - APM SUAC CEU LAJEADO
47418                  

# Identificando categorias faltantes

In [627]:
faltantes = empenhos_df[(
#     empenhos_df['cat_2'].isnull()
#     |
    empenhos_df['cat_1'].isnull()
)]
groupSum(faltantes)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação          51.879332     36.663468   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação      41.89032

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes             51.370645     36.531052     41.638142
Despesas de Capital             0.508687      0.132416      0.252178

valTotalEmpenhado  \
txtDescricaoElemento                                                                     
Outros Serviços de Terceiros -Pessoa Jurídica                                37.512911   
Outros Serviços de Terceiros - Pessoa Física                                  5.815730   
Locação de Mão-de-Obra                                                        2.827289   
Obrigações Tributárias e Contributivas                                        2.076094   
Auxílio-Alimentação                                                           1.252159   
Material de Consumo                                                           1.256918   
Equipamentos e Material Permanente                                            0.253903   
Despesas de Exercícios Anteriores                                             0.222071   
Premiações Culturais, Artísticas, Científicas, Desportivas e Outras           0.107596   
Auxílio-Transporte                                                            0.072710   
Passagens e Despesas com Locomoção                                            0.215488   
Diárias - Civil                                                               0.011680   
Obras e Instalações                                                           0.254784   

                                                                     valLiquidado  \
txtDescricaoElemento                                                                
Outros Serviços de Terceiros -Pessoa Jurídica                           26.427119   
Outros Serviços de Terceiros - Pessoa Física                             4.323230   
Locação de Mão-de-Obra                                                   1.705485   
Obrigações Tributárias e Contributivas                                   1.321706   
Auxílio-Alimentação                                                      1.248434   
Material de Consumo                                                      1.106857   
Equipamentos e Material Permanente                                       0.132416   
Despesas de Exercícios Anteriores                                        0.211834   
Premiações Culturais, Artísticas, Científicas, Desportivas e Outras      0.090112   
Auxílio-Transporte                                                       0.072710   
Passagens e Despesas com Locomoção                                       0.015372   
Diárias - Civil                                                          0.008193   
Obras e Instalações                                                      0.000000   

                                                                     valPagoTotal  
txtDescricaoElemento                                                               
Outros Serviços de Terceiros -Pessoa Jurídica                           31.145670  
Outros Serviços de Terceiros - Pessoa Física                             4.524359  
Locação de Mão-de-Obra                                                   1.740714  
Obrigações Tributárias e Contributivas                                   1.398307  
Auxílio-Alimentação                                                      1.248434  
Material de Consumo                                                      1.146958  
Equipamentos e Material Permanente                                       0.252178  
Despesas de Exercícios Anteriores                                        0.211834  
Premiações Culturais, Artísticas, Científicas, Desportivas e Outras      0.099867  
Auxílio-Transporte                                                       0.072710  
Passagens e Despesas com Locomoção                                       0.041096  
Diárias - Civil                                                          0.008193  
Obras e Instalações                                                      0.000000

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                 51.873872     36.663468      41.89032
Transferências Federais            0.005460      0.000000       0.00000

valTotalEmpenhado  \
txtDescricaoItemDespesa                                                                     
Supervisão, Acompanhamento e Suporte de Serviços Técnicos                       11.991727   
Administração de Bens ou Negócios em Geral                                       6.073733   
Publicidade Legal                                                                3.007800   
Patrocínio a Projetos Culturais                                                  1.800000   
Outros Serviços de Apoio Administrativo, Técnico e Operacional                   1.616754   
Copa e Cozinha                                                                   2.612104   
SPTURIS                                                                          1.930917   
INSS / Contribuinte Individual                                                   2.056594   
Palestrantes                                                                     1.708957   
Serviços de Recepção e Portaria                                                  1.148492   
Outras Máquinas e Equipamentos em Geral                                          0.847906   
Indenização                                                                      0.745904   
Técnicos na Área Cultural e Artística                                            0.816441   
Projeto Vocacional                                                               0.750860   
Vale-Alimentação - RGPS                                                          0.648203   
Despesas com Reembolso                                                           0.678064   
Auxílio-Refeição - RGPS                                                          0.603956   
Poços, Reservatórios e Esgotos                                                   0.559806   
Taxa de Administração - Estagiário                                               0.589004   
PIÁ - Programa de Iniciação Artística                                            0.528500   
Especialização e Treinamento                                                     0.545702   
Conselho Municipal de Educação                                                   1.149140   
Tradução ou Interpretação Comercial                                              0.543698   
Copeiragem                                                                       0.487839   
Papel para Copiadora em Geral                                                    0.419486   
Motoristas com Veículos                                                          0.346113   
Postagem de Correspondências                                                     0.691156   
Transporte e Remessa de Encomendas                                               0.211810   
Coffee Break                                                                     0.229506   
Reprografia e Correlatos - Locação                                               0.451650   
...                                                                                   ...   
Outros Seguros                                                                   0.007496   
Reatores e Geradores                                                             0.006768   
Associações                                                                      0.005400   
Apostilas, Almanaques, Folhetos e Periódicos                                     0.005352   
Diversas Flâmulas, Distintivos e/ou Insígnias                                    0.005244   
Contratação por Tempo Determinado - Pessoa Física                                0.004991   
Outros Serviços de Áudio, Vídeo, Foto, Som, Luz e Imagens                        0.004800   
Adiantamento - Inciso VI, Art. 2º da Lei 10.513/88                               0.008112   
Outros Equipamentos para Proteção, Segurança e Socorro                           0.003830   
Adiantamento - Inciso VI, Art. 2º da Lei nº 10.513/88                            0.003568   
Diversas Ferramentas                                                     

...

valTotalEmpenhado  \
txtDescricaoUnidade                                                         
Gabinete do Secretário                                          36.063217   
Diretoria Regional de Educação - Itaquera                        3.847548   
Diretoria Regional de Educação - Pirituba                        1.595141   
Diretoria Regional de Educação - Jaçanã/Tremembé                 1.441218   
Diretoria Regional de Educação - São Mateus                      1.263228   
Diretoria Regional de Educação - São Miguel                      1.489818   
Diretoria Regional de Educação - Santo Amaro                     0.851568   
Diretoria Regional de Educação - Penha                           0.803352   
Diretoria Regional de Educação - Guaianases                      1.026884   
Diretoria Regional de Educação - Campo Limpo                     0.639145   
Diretoria Regional de Educação - Butantã                         0.628745   
Departamento de Alimentação Escolar                              0.445518   
Diretoria Regional de Educação - Freguesia/Brasilândia           0.469268   
Diretoria Regional de Educação  Capela do Socorro                0.310166   
Diretoria Regional de Educação - Capela do Socorro               0.238626   
Diretoria Regional de Educação - Ipiranga                        0.762976   
Coordenadoria de Alimentação Escolar                             0.002913   

                                                        valLiquidado  \
txtDescricaoUnidade                                                    
Gabinete do Secretário                                     26.334069   
Diretoria Regional de Educação - Itaquera                   1.696399   
Diretoria Regional de Educação - Pirituba                   1.238665   
Diretoria Regional de Educação - Jaçanã/Tremembé            1.201522   
Diretoria Regional de Educação - São Mateus                 0.970049   
Diretoria Regional de Educação - São Miguel                 0.839346   
Diretoria Regional de Educação - Santo Amaro                0.730066   
Diretoria Regional de Educação - Penha                      0.699206   
Diretoria Regional de Educação - Guaianases                 0.658777   
Diretoria Regional de Educação - Campo Limpo                0.582068   
Diretoria Regional de Educação - Butantã                    0.502231   
Departamento de Alimentação Escolar                         0.434966   
Diretoria Regional de Educação - Freguesia/Brasilândia      0.269294   
Diretoria Regional de Educação  Capela do Socorro           0.194860   
Diretoria Regional de Educação - Capela do Socorro          0.179439   
Diretoria Regional de Educação - Ipiranga                   0.132510   
Coordenadoria de Alimentação Escolar                        0.000000   

                                                        valPagoTotal  
txtDescricaoUnidade                                                   
Gabinete do Secretário                                     31.034895  
Diretoria Regional de Educação - Itaquera                   1.714604  
Diretoria Regional de Educação - Pirituba                   1.340235  
Diretoria Regional de Educação - Jaçanã/Tremembé            1.282150  
Diretoria Regional de Educação - São Mateus                 1.051017  
Diretoria Regional de Educação - São Miguel                 0.918334  
Diretoria Regional de Educação - Santo Amaro                0.759921  
Diretoria Regional de Educação - Penha                      0.722299  
Diretoria Regional de Educação - Guaianases                 0.683210  
Diretoria Regional de Educação - Campo Limpo                0.583248  
Diretoria Regional de Educação - Butantã                    0.509347  
Departamento de Alimentação Escolar                         0.438456  
Diretoria Regional de Educação - Freguesia/Brasilândia      0.280545  
Diretoria Regional de Educação  Capela do Socorro           0.235528  
Diretoria Regional de Educação - Capela do Socorro          0.183044  
Diretoria Region

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes          51.370645     36.531052     41.638142
Investimentos                       0.508687      0.132416      0.252178

valTotalEmpenhado  \
txtModalidadeAplicacao                                                          
Aplicações Diretas                                                  51.857133   
Transferências a Instituições Privadas sem Fins Lucrativos           0.022199   

                                                            valLiquidado  \
txtModalidadeAplicacao                                                     
Aplicações Diretas                                             36.653231   
Transferências a Instituições Privadas sem Fins Lucrativos      0.010237   

                                                            valPagoTotal  
txtModalidadeAplicacao                                                    
Aplicações Diretas                                             41.880083  
Transferências a Instituições Privadas sem Fins Lucrativos      0.010237

valTotalEmpenhado  \
txtRazaoSocial                                                                                                   
INTEGRA SOLUCOES EM LOGISTICA E TRANSPORTE LTDA - EPP                                                 6.073733   
FUNDACAO PARA O VESTIBULAR DA UNIVERSIDADE ESTADUAL PAULISTA JULIO DE MESQUITA FILHO VUNESP           3.917452   
FEDERAÇÃO DO DESPORTO ESCOLAR DO ESTADO DE SÃO PAULO                                                  3.599508   
LUA PROPAGANDA LTDA.                                                                                  3.000000   
SOCIEDADE DE CONCERTOS DE SÃO PAULO                                                                   2.269378   
EMPRESA DE CINEMA E AUDIOVISUAL DE SÃO PAULO S.A.                                                     1.800000   
JOTABE SERVIÇOS TECNICOS ESPECIALIZADOS LTDA                                                          3.295158   
SÃO PAULO TURISMO S/A.                                                                                2.056456   
INSTITUTO NACIONAL DO SEGURO SOCIAL                                                                   2.043112   
SERV.SEC.MUN. DE EDUCAÇÃO - AUX. REFEIÇÃO                                                             1.250583   
G4S INTERATIVA SERVICE LTDA                                                                           0.815061   
HIPLAN CONSTRUÇÕES E SERVIÇOS DE MANUTENÇÃO URBANA LTDA                                               0.821217   
TB SERVIÇOS TRANSPORTE LIMPEZA GERENCIAMENTO E RECURSOS HUMANOS S/A                                   0.745904   
DEMAX SERVICOS E COMERCIO LTDA                                                                        0.573633   
NORTE-SUL HIDROTECNOLOGIA  E COMÉRCIO  LTDA.                                                          0.559806   
CENTRO DE INTEGRAÇÃO EMPRESA ESCOLA CIEE                                                              0.589004   
NEC LATIN AMERICA S.A.                                                                                0.367215   
INFO-SIG COMÉRCIO DE SUPRIMENTOS DE INFORMÁTICA LTDA.                                                 0.334972   
INCLUIR TECNOLOGIA LTDA ME                                                                            0.346275   
DANLEX SERVIÇOS LTDA.                                                                                 0.289439   
AJC CONSULTORIA EDUCACIONAL LTDA ME                                                                   0.258000   
BRASFILTER INDUSTRIA E COMÉRCIO LTDA                                                                  0.299391   
EMPRESA BRASILEIRA DE CORREIOS E TELÉGRAFOS                                                           0.752231   
GAL TRANSPORTES E LOCAÇÃO DE VEICULOS LTDA - ME                                                       0.268484   
SÃO GUALTER ADMINISTRAÇÃO E PARTICIPAÇÕES LTDA                                                        0.254427   
CAMPER EMPREENDIMENTOS LTDA                                                                           0.215604   
PAINEIRAS LIMPEZA E SERVIÇOS GERAIS LTDA.                                                             0.233701   
H PRINT REPROGRAFIA E AUTOMAÇÃO DE ESCRITÓRIO LTDA                                                    0.451650   
SUEDE SERVIÇOS - EIRELLI - EPP                                                                        0.204776   
VITTA FORTIS SERVIÇOS GERAIS LTDA - ME                                                                0.194587   
...                                                                                                        ...   
RENATA AMORIM DE LIMA SILVA                                                                           0.000168   
ANA CARLA MONTEIRO ALMEIDA                                                                            0.013860   
LEONARDO  BEZERRA DE ARAUJO                                                                           0

txtObjetoContrato
184                              Utilização de Ata de Registro de Preços – Fornecimento de Welcome Coffee 
226                     REPASSE DE RECURSOS DO PNAE PARA O CEI MAYARA ESPERANCA E VIDA - COD.INEP 35432271
251    CONTRATAÇÃO DE EMPRESA ESPECIALIZADA PARA PRESTAÇÃO DE SERVIÇO DE DOIS POSTOS DIURNOS DE AUXILIA...
356                                                   AQUISIÇÃO DE PISCINA DE BOLINHA E TABELA DE BASQUETE
452                                                                                                    NaN
569                                                   DL- RECREIO NAS FÉRIAS - Aquisição de Bem Permanente
620              AQUISIÇÃO DE 05 MESAS DE PING PONG PARA O PROGRAMA RECREIO NAS FÉRIAS EDIÇÃ OJAN DE 2017 
989                AQUISIÇÃO DE MATERIAL PERMANENTE AUDIOVISUAL - RECREIO NAS FÉRIAS - EDIÇÃO JANEIRO/2018
1135      Prestação de serviços de interpretação para LIBRAS (Língua Brasileira de Sinais) da 2ª PROVA EJA
1170                                                                                  MATERIAIS DE HIGIENE
1194                   Contratação de Instrutor de Libras - Eber Spurgeon de Almeida - EMEBS Anne Sullivan
1245                         Confecção e instalação de placas externas de identificação em aço galvanizado
1279                                        Contratação de Instrutor de Instrumentos de Metais e Percussão
1385                            DL- Confecção de troféus e medalhas para o Campeonato de Xadrez Individual
1618                                Utilização de Ata de Registro de Preços – Fornecimento de Coffee Break
1732                                                                    CONFECÇÃO DE PREMIAÇÃO PARA EVENTO
1743                                                             Contratação de Assessoria - Notório Saber
1849   Interpretação para LIBRAS (Língua Brasileira de Sinais) da 2ª Prova Semestral para os alunos do ...
2013   Contratação de Agentes Recreativos credenciados para o desenvolvimento de atividades de lazer e ...
2047                                                        Aquisição de gás liquefeito - botijão de 13 kg
2067                           Contratação de empresa especializada na instalaçã ode camenra de segurança.
2073                                     Aquisição de biscoitos  tipo maisena, tipo waffer, tipo tortinha 
2074                                     Aquisição de biscoitos tipo água e sal, cream cracker e adoçante 
2085                                 Aquisição de biscoito redondo salgado (salsalito) , cha de erva mate 
2235   Contratação de empresa especializada para realizar a interpretação para LIBRAS (Língua Brasileir...
2400                                                      PRESTAÇÃO DE SERVIÇOS DE INTÉRPRETE DE "LIBRAS" 
2423                                                              CONFECÇÃO PASTAS PARA ARQUIVO DESLIZANTE
2571   Contratação do intérprete Thiago Nanuze Verza para a “Seminário Salas de Leitura: 45 Anos Forman...
2655       ATA RP 03-SMG-COBES/2017- Aquisição de papel sulfite A4 branco para uso das Unidades Escolares.
2668                                                                   Contratação de Intérprete de Libras
...                                                                                                    ...
57034                                                           Certificado Digital A-3 e-CPF com leitora 
57042                                                                         Secadora de roupas para CEI 
57085    Confecção de Materiais personalizados para os Seminários "Novembro Negro" e "Dezembro Imigrante".
57172                                     COORDENADOR DE POLO - PROGRAMA RECREIO NAS FÉRIAS - JANEIRO/2017
57176                                    COORDENADOR  DE POLO - PROGRAMA RECREIO NAS FÉRIAS - JANEIRO/2017
57226                                           Aquisição de copo e materiais diversos de limpeza - ATA RP
57321                  

In [628]:
faltantes_det = empenhos_df[(
    empenhos_df['cat_1'].isnull()
    &
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Administração de Bens ou Negócios em Geral', case=False))
)]
groupSum(faltantes_det)

valTotalEmpenhado  valLiquidado  \
txtDescricaoOrgao                                                   
Secretaria Municipal de Educação           6.073733      4.654509   

                                  valPagoTotal  
txtDescricaoOrgao                               
Secretaria Municipal de Educação      5.532017

valTotalEmpenhado  valLiquidado  valPagoTotal
txtCategoriaEconomica                                               
Despesas Correntes              6.073733      4.654509      5.532017

valTotalEmpenhado  \
txtDescricaoElemento                                               
Outros Serviços de Terceiros -Pessoa Jurídica           6.073733   

                                               valLiquidado  valPagoTotal  
txtDescricaoElemento                                                       
Outros Serviços de Terceiros -Pessoa Jurídica      4.654509      5.532017

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoFonteRecurso                                               
Tesouro Municipal                  6.073733      4.654509      5.532017

valTotalEmpenhado  valLiquidado  \
txtDescricaoItemDespesa                                                       
Administração de Bens ou Negócios em Geral           6.073733      4.654509   

                                            valPagoTotal  
txtDescricaoItemDespesa                                   
Administração de Bens ou Negócios em Geral      5.532017

...

valTotalEmpenhado  valLiquidado  valPagoTotal
txtDescricaoUnidade                                                  
Gabinete do Secretário           6.073733      4.654509      5.532017

valTotalEmpenhado  valLiquidado  valPagoTotal
txtGrupoDespesa                                                         
Outras Despesas Correntes           6.073733      4.654509      5.532017

valTotalEmpenhado  valLiquidado  valPagoTotal
txtModalidadeAplicacao                                               
Aplicações Diretas               6.073733      4.654509      5.532017

valTotalEmpenhado  \
txtRazaoSocial                                                             
INTEGRA SOLUCOES EM LOGISTICA E TRANSPORTE LTDA - EPP           6.073733   

                                                       valLiquidado  \
txtRazaoSocial                                                        
INTEGRA SOLUCOES EM LOGISTICA E TRANSPORTE LTDA - EPP      4.654509   

                                                       valPagoTotal  
txtRazaoSocial                                                       
INTEGRA SOLUCOES EM LOGISTICA E TRANSPORTE LTDA - EPP      5.532017

txtObjetoContrato
40040               NaN

In [629]:
# funcionamento - logistica e transportes
funcionamento_logistica_filter = (
    empenhos_df['cat_1'].isnull()
    &
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Administração de Bens ou Negócios em Geral', case=False))
)
funcionamento_logistica = (empenhos_df[funcionamento_logistica_filter])
empenhos_df.loc[funcionamento_logistica_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[funcionamento_logistica_filter, 'cat_2'] = 'logistica_transportes'
# groupSum(funcionamento_logistica)

In [630]:
# CEU - outros
ceu_filter = (
    empenhos_df['cat_1'].isnull()
    &
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('Operação e Manutenção dos Centros Educacionais Unificados', case=False))
)
ceu = (empenhos_df[ceu_filter])
empenhos_df.loc[ceu_filter, 'cat_1'] = 'funcionamento_unidades'
empenhos_df.loc[ceu_filter, 'cat_2'] = 'ceu_outros'
# groupSum(ceu)

In [631]:
# suporte adm - outros
suporte_administrativo_filter = (
    empenhos_df['cat_1'].isnull()
    &
    (empenhos_df['txtDescricaoPrograma'].str.contains('Suporte Administrativo', case=False))
)
suporte_administrativo = (empenhos_df[suporte_administrativo_filter])
empenhos_df.loc[suporte_administrativo_filter, 'cat_1'] = 'suporte_administrativo'
empenhos_df.loc[suporte_administrativo_filter, 'cat_2'] = 'suporte_administrativo_outros'
# groupSum(suporte_administrativo)

In [632]:
# pedagogico - mais formação
pedagogico_form_filter = (
    empenhos_df['cat_1'].isnull()
    &
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('Capacitação, Formação e Aperfeiçoamento de Servidores', case=False))
)
pedagogico_form = (empenhos_df[pedagogico_form_filter])
empenhos_df.loc[pedagogico_form_filter, 'cat_1'] = 'pedagogico'
empenhos_df.loc[pedagogico_form_filter, 'cat_2'] = 'formacao'
# groupSum(pedagogico_form)

## Faz sentido esse filtro e catergorização do Mais Educação?

In [633]:
# pedagogico - mais educação
pedagogico_mais_edu_filter = (
    empenhos_df['cat_1'].isnull()
    &
    (empenhos_df['txtDescricaoProjetoAtividade'].str.contains('Ampliação da jornada escolar - Programa Mais Educação', case=False))
    &
    (empenhos_df['txtDescricaoItemDespesa'].str.contains('Supervisão, Acompanhamento e Suporte de Serviços Técnicos', case=False))
)
pedagogico_mais_edu = (empenhos_df[pedagogico_mais_edu_filter])
empenhos_df.loc[pedagogico_mais_edu_filter, 'cat_1'] = 'pedagogico'
empenhos_df.loc[pedagogico_mais_edu_filter, 'cat_2'] = 'mais_educacao'

# Export

In [634]:
# clean errors, columns with cat_1 but no cat_2
errors_filter = ((empenhos_df['cat_2'].isnull() | (empenhos_df['cat_2'] == '')) & ~empenhos_df['cat_1'].isnull())
print('erros:', len(empenhos_df[errors_filter]))
# empenhos_df.loc[errors_filter, 'cat_1'] = ''
empenhos_df.loc[errors_filter, 'cat_2'] = 'outros'
empenhos_df[errors_filter]['txtDescricaoItemDespesa'].unique()

erros: 269


array(['Outras Despesas Fixas - Pessoal Civil',
       'Convênios - Portadores de Deficiência', 'Switch ',
       'Convênios - Alfabetização, Educação e Outros',
       'Pesquisa em Geral',
       'Outros Serviços de Apoio Administrativo, Técnico e Operacional',
       'Convênio - Creche', 'Guarda e Gerenciamento de Documentos',
       'Certificado Digital',
       'Outras Máquinas e Equipamentos Energéticos ',
       'Aquisição de Softwares - Intangível', 'Hardware',
       'Toner e Cartuchos de Tinta'], dtype=object)

In [635]:
# # todos outros restantes, em uma categoria "outros"
# # clean errors, columns with cat_1 but no cat_2
# errors_filter = ((empenhos_df['cat_2'].isnull() | (empenhos_df['cat_2'] == '')) & empenhos_df['cat_1'].isnull())
# print('erros:', len(empenhos_df[errors_filter]))
# empenhos_df.loc[errors_filter, 'cat_1'] = 'outros'
# empenhos_df.loc[errors_filter, 'cat_2'] = 'outros'
# empenhos_df[errors_filter]['txtDescricaoItemDespesa'].unique()

In [636]:
# coverage
coverage = empenhos_df[~empenhos_df['cat_1'].isnull() & ~empenhos_df['cat_2'].isnull()]['valLiquidado'].sum() / empenhos_df['valLiquidado'].sum()
print(f"cobertura do orçamento: {round(coverage * 100, 2)}%")
print(f"valor faltante {round(empenhos_df[empenhos_df['cat_1'].isnull() & empenhos_df['cat_2'].isnull()]['valLiquidado'].sum() / 1000000, 2)} mi")

cobertura do orçamento: 99.81%
valor faltante 19.03 mi


In [637]:
# coverage PAGO
coverage = empenhos_df[~empenhos_df['cat_1'].isnull() & ~empenhos_df['cat_2'].isnull()]['valPagoTotal'].sum() / empenhos_df['valPagoTotal'].sum()
print(f"cobertura do orçamento: {round(coverage * 100, 2)}%")
print(f"valor faltante {round(empenhos_df[empenhos_df['cat_1'].isnull() & empenhos_df['cat_2'].isnull()]['valPagoTotal'].sum() / 1000000, 2)} mi")

cobertura do orçamento: 99.82%
valor faltante 19.61 mi


In [638]:
out = (empenhos_df[['valPagoTotal', 'cat_1', 'cat_2']]         
    .groupby(['cat_1', 'cat_2'])
    .sum().apply(lambda x: x / 1000000)
#     .sort_values('valLiquidado', ascending=False)
)
display(out)

valPagoTotal
cat_1                  cat_2                                      
alimentacao            insumos                          231.123712
                       leve_leite                        54.456454
                       pnae                              19.721738
                       prep_dist                         57.732279
                       refeicoes                        344.783132
funcionamento_unidades agua_esgoto                      107.440314
                       aluguel_imoveis                   19.519948
                       ceu_outros                        26.846785
                       eletricidade                      50.882340
                       eventos                            9.126208
                       limpeza                          424.731067
                       logistica_transportes              5.532017
                       manutencao                        22.742817
                       mobiliario                         7.332216
                       obras_reformas                    78.704729
                       telefone                           6.216973
                       uniceu                             2.870959
                       vigilancia                       198.547639
parcerias              creches                         1962.607936
                       ed_especial                       36.601538
                       eja                               10.942761
                       outros                             3.635450
pedagogico             formacao                           3.013279
                       mais_educacao                      5.499647
pessoal                adiantamento                      12.202874
                       docentes                        5872.021815
                       estagios                          36.592522
                       gestores                         343.404845
                       outros                             2.179419
suporte_administrativo suporte_administrativo_outros      8.288257
ti                     compra_notebooks                  40.021740
                       internet                          13.518565
                       manutencao                         1.123597
                       manutencao_equip_ti                6.459788
                       manutencao_impressao               1.869473
                       manutencao_software_sistemas      15.273364
                       outros                             7.792898
transferencias         ptrf                              41.846570
transporte             teg                              211.016397
                       veiculos                          17.627189
uniforme_materiais     materiais                         55.646292
                       uniforme                         203.651681

In [639]:
# format data for treemap visualization
index_1 = list(out.index.get_level_values(0).unique())
index_2 = list(out.index.get_level_values(1).unique())
formatted_out = {'name': 'orc', 'children': []}
for i in index_1:
    formatted_out['children'].append({'name': i, 'children': []})
for index, row in out.iterrows():
    cat_1 = index[0]
    cat_2 = index[1]
    # display as millions?
    value = round(row['valPagoTotal'] * 1000000, 2)
    for child_index, child in enumerate(formatted_out['children']):
        if child['name'] == cat_1:
            formatted_out['children'][child_index]['children'].append({'name': cat_2, 'size': value})
pprint.pprint(formatted_out)

{'children': [{'children': [{'name': 'insumos', 'size': 231123711.86},
                            {'name': 'leve_leite', 'size': 54456453.89},
                            {'name': 'pnae', 'size': 19721738.0},
                            {'name': 'prep_dist', 'size': 57732278.68},
                            {'name': 'refeicoes', 'size': 344783132.32}],
               'name': 'alimentacao'},
              {'children': [{'name': 'agua_esgoto', 'size': 107440314.11},
                            {'name': 'aluguel_imoveis', 'size': 19519948.28},
                            {'name': 'ceu_outros', 'size': 26846785.49},
                            {'name': 'eletricidade', 'size': 50882339.96},
                            {'name': 'eventos', 'size': 9126208.33},
                            {'name': 'limpeza', 'size': 424731067.12},
                            {'name': 'logistica_transportes',
                             'size': 5532017.47},
                            {'name': 'manutencao', '

In [640]:
with open('budget.json', 'w') as f:
    f.write(json.dumps(formatted_out))